In [1]:
import pandas as pd
import numpy as np


After discussing the EDA, the preparation of the data and my baseline model, I received a number of additional instructions:

• The separation into a training set and a test set, to be done when each session info id takes place in its entirety and does not split between the sets. This is because in production this is how things will look. Also - each process of feature enrichment to perform for each session info id separately.
• Produce features that refer to data as a Time Series.
This notebook is primarily designed to meet these requirements.

In addition, there is a problem with the data stored in the cloud. If so, I loaded a csv version of the data after deleting the irrelevant columns (having one value, including information tagged retrospectively, etc.)

In [2]:
df = pd.read_csv ('df for split.csv')


In [3]:
df.head()

SESSION_INFO_ID  INTERVAL_IN_FILE  VALUE  SN  ACCL_X  \
0  6a39aff16c954755887e275fdfbcf82e                 7      0  11   32767   
1  6a39aff16c954755887e275fdfbcf82e                20      0  24   32767   
2  6a39aff16c954755887e275fdfbcf82e                36      0  40   32767   
3  6a39aff16c954755887e275fdfbcf82e                45      0  49   32767   
4  6a39aff16c954755887e275fdfbcf82e                52      0  56   32767   

   ACCL_Y  ACCL_Z  BAND_ARR_1  BAND_ARR_2  BAND_ARR_3  ...  BATT_LEVEL  \
0   -5269   32767    0.240264    0.149872    0.091437  ...          67   
1   -5515   32767    0.173969    0.170729    0.091877  ...          67   
2   -5801   32767    0.264151    0.110667    0.081432  ...          67   
3   -6550   32767    3.655040    2.248858    1.993189  ...          67   
4   -6103   32767    2.797805    1.304610    0.664670  ...          67   

      DATE  FIRST_PACKET_TS        GW_MAC       GW_NAME  OPERATION_VALID  \
0  30:24.0              234  E0D87D23F51F  Machine name            False   
1  30:24.0              234  E0D87D23F51F  Machine name            False   
2  30:24.0              234  E0D87D23F51F  Machine name            False   
3  30:24.0              234  E0D87D23F51F  Machine name            False   
4  30:24.0              234  E0D87D23F51F  Machine name            False   

   RSSI      TOOL_MAC     TOOL_NAME  S_I_CREATED_AT  
0   -59  C70BA91FEA15  E0000C23F51F         58:54.8  
1   -59  C70BA91FEA15  E0000C23F51F         58:54.8  
2   -59  C70BA91FEA15  E0000C23F51F         58:54.8  
3   -59  C70BA91FEA15  E0000C23F51F         58:54.8  
4   -59  C70BA91FEA15  E0000C23F51F         58:54.8  

[5 rows x 57 columns]

In [4]:
ts = df.loc[:,[ 'SESSION_INFO_ID', 'INTERVAL_IN_FILE', 
                       'BAND_ARR_2',
                       'BAND_ARR_8',
                       'NTC']]

In order to create features that relate to data as a time series, I have created a short list of a number of relevant features. The first two are the ones that divide the data by time. The next 3 are the 3 features that in the data selection in the previous notebook, received the highest rating. For the results of changing each of these 3 features over time, I will create new features. Initially I wanted to make the move for more than 3 features, but this created memory issues.

The second emphasis I received - the distribution of data according to session info id. Will be performed in the following cells.

In [5]:
id_unique = ts.SESSION_INFO_ID.unique()


In [6]:
id_unique

array(['6a39aff16c954755887e275fdfbcf82e',
       'b15013b59de84573bffc72e466247ad0',
       '05c71780b43648399788edeb658889aa',
       'ecbfec1cda2342adba29c06ec09f5560',
       'd4a812f356fc41ecbe98dde417d54a40',
       'bab4d43dcbc44df4b4ff6a62419f30c6',
       '4d6d95787f2b4dacb99efda11430f135',
       '222495f0d4144d35a811bed17717e446',
       'a1a916f55354450899185d74a25c872c',
       '33df3b0ebdbf468dbc473c0930e8bc03',
       '9bd9c2293fdf4698b1f3ee83122f887c',
       '9549963fd74645f3bab4d788109c514a',
       '1509358e6dda4f7ebaa35521b6811beb',
       '842fd1c6a33f4a9480effef7aebfcd78',
       'a7b88ba73323469ca79292edf20e823b',
       '808fc1e8d91f4503a454b04c4715b47c',
       '6c58ca7a64e44ef793b82be58d24d44f',
       '4a659a0359ac40c39c58430b472bfca7',
       'a38a4696919744baa937f841a320ec86',
       '334bb190b0fc438d9876b087b95329b9',
       'fb050ff8daa441398410292684bc9583',
       '97b01b4a4a334195a9af38e1b0907315',
       '1e3d61b7cac24c62a010f116710b9703',
       '404

In [8]:
import random
random.shuffle(id_unique)


In [9]:
id_unique

array(['15c50a1059a9409aadecaea7c4b2d6c3',
       '06033f092c204fb8a890784f99e1d1fb',
       'c0a5655477844e37b8fcdf0448199abc',
       '33309ed83f8b4e2d8196adb722fd25a7',
       '69109d0681cf4b5888ac9d2a1bdf8a49',
       '1f9e3c25ddbe4e4b870da6c932081c56',
       'c240c36514c4460c954b39fbb1637f1e',
       '151ae4400e8d475181808b73a2dea7ff',
       'd4a812f356fc41ecbe98dde417d54a40',
       '114312590f78424f93e81b4551ebbf34',
       'd04d5e16d8e24105a15010b0c512026b',
       'cf90efff3f2c4b3388a450029f15d01d',
       '20792537c7bd4a7e9f6b734a84b2bffc',
       '9a9e244a4aaa43ccb570385f6702a9ff',
       '8ab1ccdbe963420bbbb54b5e55718482',
       '30786e152e60477db9a6c0de5c8816a8',
       '0149b8bcd7754ff398cc5bebd1e43ccd',
       '95e44eef0e4e4a85b5afc492d5a371fe',
       '13f7093b71054ddaa00b8dc32bc5c14a',
       'e3efb10152c14b2086745b3d6ebdb98e',
       '31736e17591a4e43a4ac7bd8741ffa02',
       '4c9c6fb31254409a913df4bfbe7629e2',
       'd290440871d443e4b08451182c8644ff',
       '56b

In [10]:
dic_tsfresh = {}
for unique in id_unique:
     dic_tsfresh[unique] = ts[ts['SESSION_INFO_ID'] == unique ]
     
    
    


In [11]:
dic_tsfresh

{'15c50a1059a9409aadecaea7c4b2d6c3':                         SESSION_INFO_ID  INTERVAL_IN_FILE  BAND_ARR_2  \
 22862  15c50a1059a9409aadecaea7c4b2d6c3                 0    1.198827   
 22863  15c50a1059a9409aadecaea7c4b2d6c3                26    4.924421   
 22864  15c50a1059a9409aadecaea7c4b2d6c3                31    7.157350   
 22865  15c50a1059a9409aadecaea7c4b2d6c3                40    7.481539   
 22866  15c50a1059a9409aadecaea7c4b2d6c3                44    7.182053   
 ...                                 ...               ...         ...   
 24786  15c50a1059a9409aadecaea7c4b2d6c3               394    0.270072   
 24787  15c50a1059a9409aadecaea7c4b2d6c3               397    0.225037   
 24788  15c50a1059a9409aadecaea7c4b2d6c3               419    0.191502   
 24789  15c50a1059a9409aadecaea7c4b2d6c3               423    0.139803   
 24790  15c50a1059a9409aadecaea7c4b2d6c3               460    0.582073   
 
        BAND_ARR_8   NTC  
 22862    0.304780  1453  
 22863    3.435584  

In [13]:
dic_tsfresh['15c50a1059a9409aadecaea7c4b2d6c3']

SESSION_INFO_ID  INTERVAL_IN_FILE  BAND_ARR_2  \
22862  15c50a1059a9409aadecaea7c4b2d6c3                 0    1.198827   
22863  15c50a1059a9409aadecaea7c4b2d6c3                26    4.924421   
22864  15c50a1059a9409aadecaea7c4b2d6c3                31    7.157350   
22865  15c50a1059a9409aadecaea7c4b2d6c3                40    7.481539   
22866  15c50a1059a9409aadecaea7c4b2d6c3                44    7.182053   
...                                 ...               ...         ...   
24786  15c50a1059a9409aadecaea7c4b2d6c3               394    0.270072   
24787  15c50a1059a9409aadecaea7c4b2d6c3               397    0.225037   
24788  15c50a1059a9409aadecaea7c4b2d6c3               419    0.191502   
24789  15c50a1059a9409aadecaea7c4b2d6c3               423    0.139803   
24790  15c50a1059a9409aadecaea7c4b2d6c3               460    0.582073   

       BAND_ARR_8   NTC  
22862    0.304780  1453  
22863    3.435584  1457  
22864    7.631615  1456  
22865   10.391945  1458  
22866    9.416947  1453  
...           ...   ...  
24786    0.062218  1451  
24787    0.091587  1451  
24788    0.069267  1456  
24789    0.079699  1443  
24790    0.126312  1449  

[478 rows x 5 columns]

We now have a dictionary, in which each key is a unique value of session info id, and each value is basically a data table for that unique value.
   Now, with the help of a dedicated package, we will create new variables for each table based on being a time series. 

In [14]:
from tsfresh import extract_features
from tsfresh.utilities.dataframe_functions import impute


In [15]:
for key in dic_tsfresh:
    table = dic_tsfresh[key]
    X = table.loc[:, table.columns != 'VALUE']
    dic_tsfresh[key] = extract_features(X, column_id="SESSION_INFO_ID", column_sort="INTERVAL_IN_FILE")
    dic_tsfresh[key] = impute(dic_tsfresh[key])



Feature Extraction: 100%|████████████████████████████████████████████████████████████████| 3/3 [00:04<00:00,  1.36s/it]
C:\Users\Arie\AppData\Roaming\Python\Python39\site-packages\tsfresh\utilities\dataframe_functions.py:198: RuntimeWarning: The columns ['NTC__friedrich_coefficients__coeff_0__m_3__r_30'
 'NTC__friedrich_coefficients__coeff_1__m_3__r_30'
 'NTC__friedrich_coefficients__coeff_2__m_3__r_30'
 'NTC__friedrich_coefficients__coeff_3__m_3__r_30'
 'NTC__max_langevin_fixed_point__m_3__r_30'
 'NTC__query_similarity_count__query_None__threshold_0.0'
 'BAND_ARR_2__query_similarity_count__query_None__threshold_0.0'
 'BAND_ARR_8__query_similarity_count__query_None__threshold_0.0'] did not have any finite values. Filling with zeros.
  warnings.warn(
Feature Extraction: 100%|████████████████████████████████████████████████████████████████| 3/3 [00:03<00:00,  1.18s/it]
C:\Users\Arie\AppData\Roaming\Python\Python39\site-packages\tsfresh\utilities\dataframe_functions.py:198: RuntimeWarning

Feature Extraction: 100%|████████████████████████████████████████████████████████████████| 3/3 [00:03<00:00,  1.31s/it]
C:\Users\Arie\AppData\Roaming\Python\Python39\site-packages\tsfresh\utilities\dataframe_functions.py:198: RuntimeWarning: The columns ['NTC__sample_entropy' 'NTC__autocorrelation__lag_4'
 'NTC__autocorrelation__lag_5' ...
 'BAND_ARR_8__matrix_profile__feature_"25"__threshold_0.98'
 'BAND_ARR_8__matrix_profile__feature_"75"__threshold_0.98'
 'BAND_ARR_8__mean_n_absolute_max__number_of_maxima_7'] did not have any finite values. Filling with zeros.
  warnings.warn(
Feature Extraction: 100%|████████████████████████████████████████████████████████████████| 3/3 [00:04<00:00,  1.34s/it]
C:\Users\Arie\AppData\Roaming\Python\Python39\site-packages\tsfresh\utilities\dataframe_functions.py:198: RuntimeWarning: The columns ['BAND_ARR_2__mean_abs_change' 'BAND_ARR_2__mean_change'
 'BAND_ARR_2__mean_second_derivative_central' ...
 'NTC__matrix_profile__feature_"25"__threshold_0.98'

Feature Extraction: 100%|████████████████████████████████████████████████████████████████| 3/3 [00:03<00:00,  1.32s/it]
C:\Users\Arie\AppData\Roaming\Python\Python39\site-packages\tsfresh\utilities\dataframe_functions.py:198: RuntimeWarning: The columns ['BAND_ARR_8__kurtosis' 'BAND_ARR_8__sample_entropy'
 'BAND_ARR_8__autocorrelation__lag_3' ...
 'NTC__matrix_profile__feature_"25"__threshold_0.98'
 'NTC__matrix_profile__feature_"75"__threshold_0.98'
 'NTC__mean_n_absolute_max__number_of_maxima_7'] did not have any finite values. Filling with zeros.
  warnings.warn(
Feature Extraction: 100%|████████████████████████████████████████████████████████████████| 3/3 [00:04<00:00,  1.34s/it]
C:\Users\Arie\AppData\Roaming\Python\Python39\site-packages\tsfresh\utilities\dataframe_functions.py:198: RuntimeWarning: The columns ['BAND_ARR_2__mean_abs_change' 'BAND_ARR_2__mean_change'
 'BAND_ARR_2__mean_second_derivative_central' ...
 'NTC__matrix_profile__feature_"25"__threshold_0.98'
 'NTC__matrix

Feature Extraction: 100%|████████████████████████████████████████████████████████████████| 3/3 [00:04<00:00,  1.41s/it]
C:\Users\Arie\AppData\Roaming\Python\Python39\site-packages\tsfresh\utilities\dataframe_functions.py:198: RuntimeWarning: The columns ['NTC__friedrich_coefficients__coeff_0__m_3__r_30'
 'NTC__friedrich_coefficients__coeff_1__m_3__r_30'
 'NTC__friedrich_coefficients__coeff_2__m_3__r_30'
 'NTC__friedrich_coefficients__coeff_3__m_3__r_30'
 'NTC__max_langevin_fixed_point__m_3__r_30'
 'NTC__query_similarity_count__query_None__threshold_0.0'
 'NTC__matrix_profile__feature_"min"__threshold_0.98'
 'NTC__matrix_profile__feature_"max"__threshold_0.98'
 'NTC__matrix_profile__feature_"mean"__threshold_0.98'
 'NTC__matrix_profile__feature_"median"__threshold_0.98'
 'NTC__matrix_profile__feature_"25"__threshold_0.98'
 'NTC__matrix_profile__feature_"75"__threshold_0.98'
 'BAND_ARR_2__query_similarity_count__query_None__threshold_0.0'
 'BAND_ARR_8__query_similarity_count__query_None_

Feature Extraction: 100%|████████████████████████████████████████████████████████████████| 3/3 [00:04<00:00,  1.49s/it]
C:\Users\Arie\AppData\Roaming\Python\Python39\site-packages\tsfresh\utilities\dataframe_functions.py:198: RuntimeWarning: The columns ['NTC__friedrich_coefficients__coeff_0__m_3__r_30'
 'NTC__friedrich_coefficients__coeff_1__m_3__r_30'
 'NTC__friedrich_coefficients__coeff_2__m_3__r_30'
 'NTC__friedrich_coefficients__coeff_3__m_3__r_30'
 'NTC__max_langevin_fixed_point__m_3__r_30'
 'NTC__query_similarity_count__query_None__threshold_0.0'
 'BAND_ARR_2__query_similarity_count__query_None__threshold_0.0'
 'BAND_ARR_8__query_similarity_count__query_None__threshold_0.0'] did not have any finite values. Filling with zeros.
  warnings.warn(
Feature Extraction: 100%|████████████████████████████████████████████████████████████████| 3/3 [00:03<00:00,  1.30s/it]
C:\Users\Arie\AppData\Roaming\Python\Python39\site-packages\tsfresh\utilities\dataframe_functions.py:198: RuntimeWarning

...

Feature Extraction: 100%|████████████████████████████████████████████████████████████████| 3/3 [00:03<00:00,  1.07s/it]
C:\Users\Arie\AppData\Roaming\Python\Python39\site-packages\tsfresh\utilities\dataframe_functions.py:198: RuntimeWarning: The columns ['BAND_ARR_2__mean_second_derivative_central' 'BAND_ARR_2__skewness'
 'BAND_ARR_2__kurtosis' ...
 'BAND_ARR_8__matrix_profile__feature_"25"__threshold_0.98'
 'BAND_ARR_8__matrix_profile__feature_"75"__threshold_0.98'
 'BAND_ARR_8__mean_n_absolute_max__number_of_maxima_7'] did not have any finite values. Filling with zeros.
  warnings.warn(
Feature Extraction: 100%|████████████████████████████████████████████████████████████████| 3/3 [00:03<00:00,  1.18s/it]
C:\Users\Arie\AppData\Roaming\Python\Python39\site-packages\tsfresh\utilities\dataframe_functions.py:198: RuntimeWarning: The columns ['NTC__friedrich_coefficients__coeff_0__m_3__r_30'
 'NTC__friedrich_coefficients__coeff_1__m_3__r_30'
 'NTC__friedrich_coefficients__coeff_2__m_3__r_3

Feature Extraction: 100%|████████████████████████████████████████████████████████████████| 3/3 [00:03<00:00,  1.09s/it]
C:\Users\Arie\AppData\Roaming\Python\Python39\site-packages\tsfresh\utilities\dataframe_functions.py:198: RuntimeWarning: The columns ['NTC__friedrich_coefficients__coeff_0__m_3__r_30'
 'NTC__friedrich_coefficients__coeff_1__m_3__r_30'
 'NTC__friedrich_coefficients__coeff_2__m_3__r_30'
 'NTC__friedrich_coefficients__coeff_3__m_3__r_30'
 'NTC__max_langevin_fixed_point__m_3__r_30'
 'NTC__query_similarity_count__query_None__threshold_0.0'
 'BAND_ARR_8__query_similarity_count__query_None__threshold_0.0'
 'BAND_ARR_2__query_similarity_count__query_None__threshold_0.0'] did not have any finite values. Filling with zeros.
  warnings.warn(
Feature Extraction: 100%|████████████████████████████████████████████████████████████████| 3/3 [00:02<00:00,  1.00it/s]
C:\Users\Arie\AppData\Roaming\Python\Python39\site-packages\tsfresh\utilities\dataframe_functions.py:198: RuntimeWarning

Feature Extraction: 100%|████████████████████████████████████████████████████████████████| 3/3 [00:03<00:00,  1.12s/it]
C:\Users\Arie\AppData\Roaming\Python\Python39\site-packages\tsfresh\utilities\dataframe_functions.py:198: RuntimeWarning: The columns ['NTC__friedrich_coefficients__coeff_0__m_3__r_30'
 'NTC__friedrich_coefficients__coeff_1__m_3__r_30'
 'NTC__friedrich_coefficients__coeff_2__m_3__r_30'
 'NTC__friedrich_coefficients__coeff_3__m_3__r_30'
 'NTC__max_langevin_fixed_point__m_3__r_30'
 'NTC__query_similarity_count__query_None__threshold_0.0'
 'BAND_ARR_2__query_similarity_count__query_None__threshold_0.0'
 'BAND_ARR_8__query_similarity_count__query_None__threshold_0.0'] did not have any finite values. Filling with zeros.
  warnings.warn(
Feature Extraction: 100%|████████████████████████████████████████████████████████████████| 3/3 [00:03<00:00,  1.05s/it]
C:\Users\Arie\AppData\Roaming\Python\Python39\site-packages\tsfresh\utilities\dataframe_functions.py:198: RuntimeWarning

Feature Extraction: 100%|████████████████████████████████████████████████████████████████| 3/3 [00:03<00:00,  1.15s/it]
C:\Users\Arie\AppData\Roaming\Python\Python39\site-packages\tsfresh\utilities\dataframe_functions.py:198: RuntimeWarning: The columns ['NTC__friedrich_coefficients__coeff_0__m_3__r_30'
 'NTC__friedrich_coefficients__coeff_1__m_3__r_30'
 'NTC__friedrich_coefficients__coeff_2__m_3__r_30'
 'NTC__friedrich_coefficients__coeff_3__m_3__r_30'
 'NTC__max_langevin_fixed_point__m_3__r_30'
 'NTC__query_similarity_count__query_None__threshold_0.0'
 'BAND_ARR_8__query_similarity_count__query_None__threshold_0.0'
 'BAND_ARR_2__query_similarity_count__query_None__threshold_0.0'] did not have any finite values. Filling with zeros.
  warnings.warn(
Feature Extraction: 100%|████████████████████████████████████████████████████████████████| 3/3 [00:03<00:00,  1.07s/it]
C:\Users\Arie\AppData\Roaming\Python\Python39\site-packages\tsfresh\utilities\dataframe_functions.py:198: RuntimeWarning

Feature Extraction: 100%|████████████████████████████████████████████████████████████████| 3/3 [00:04<00:00,  1.40s/it]
C:\Users\Arie\AppData\Roaming\Python\Python39\site-packages\tsfresh\utilities\dataframe_functions.py:198: RuntimeWarning: The columns ['BAND_ARR_2__mean_abs_change' 'BAND_ARR_2__mean_change'
 'BAND_ARR_2__mean_second_derivative_central' ...
 'BAND_ARR_8__matrix_profile__feature_"25"__threshold_0.98'
 'BAND_ARR_8__matrix_profile__feature_"75"__threshold_0.98'
 'BAND_ARR_8__mean_n_absolute_max__number_of_maxima_7'] did not have any finite values. Filling with zeros.
  warnings.warn(
Feature Extraction: 100%|████████████████████████████████████████████████████████████████| 3/3 [00:03<00:00,  1.33s/it]
C:\Users\Arie\AppData\Roaming\Python\Python39\site-packages\tsfresh\utilities\dataframe_functions.py:198: RuntimeWarning: The columns ['BAND_ARR_2__mean_second_derivative_central' 'BAND_ARR_2__skewness'
 'BAND_ARR_2__kurtosis' ...
 'NTC__matrix_profile__feature_"25"__thresh

In [16]:
dic_tsfresh['16f3a37161c443a29ca7a8d2cbc1b8bb']

NTC__variance_larger_than_standard_deviation  \
16f3a37161c443a29ca7a8d2cbc1b8bb                                           1.0   

                                  NTC__has_duplicate_max  \
16f3a37161c443a29ca7a8d2cbc1b8bb                     1.0   

                                  NTC__has_duplicate_min  NTC__has_duplicate  \
16f3a37161c443a29ca7a8d2cbc1b8bb                     1.0                 1.0   

                                  NTC__sum_values  NTC__abs_energy  \
16f3a37161c443a29ca7a8d2cbc1b8bb         680055.0      963495065.0   

                                  NTC__mean_abs_change  NTC__mean_change  \
16f3a37161c443a29ca7a8d2cbc1b8bb               3.73904         -0.002088   

                                  NTC__mean_second_derivative_central  \
16f3a37161c443a29ca7a8d2cbc1b8bb                             0.003138   

                                  NTC__median  ...  \
16f3a37161c443a29ca7a8d2cbc1b8bb       1416.0  ...   

                                  BAND_ARR_2__permutation_entropy__dimension_6__tau_1  \
16f3a37161c443a29ca7a8d2cbc1b8bb                                           5.690768     

                                  BAND_ARR_2__permutation_entropy__dimension_7__tau_1  \
16f3a37161c443a29ca7a8d2cbc1b8bb                                           6.072363     

                                  BAND_ARR_2__query_similarity_count__query_None__threshold_0.0  \
16f3a37161c443a29ca7a8d2cbc1b8bb                                                0.0               

                                  BAND_ARR_2__matrix_profile__feature_"min"__threshold_0.98  \
16f3a37161c443a29ca7a8d2cbc1b8bb                                           1.256444           

                                  BAND_ARR_2__matrix_profile__feature_"max"__threshold_0.98  \
16f3a37161c443a29ca7a8d2cbc1b8bb                                           5.543621           

                                  BAND_ARR_2__matrix_profile__feature_"mean"__threshold_0.98  \
16f3a37161c443a29ca7a8d2cbc1b8bb                                           3.885817            

                                  BAND_ARR_2__matrix_profile__feature_"median"__threshold_0.98  \
16f3a37161c443a29ca7a8d2cbc1b8bb                                           4.324432              

                                  BAND_ARR_2__matrix_profile__feature_"25"__threshold_0.98  \
16f3a37161c443a29ca7a8d2cbc1b8bb                                            3.05797          

                                  BAND_ARR_2__matrix_profile__feature_"75"__threshold_0.98  \
16f3a37161c443a29ca7a8d2cbc1b8bb                                            4.84837          

                                  BAND_ARR_2__mean_n_absolute_max__number_of_maxima_7  
16f3a37161c443a29ca7a8d2cbc1b8bb                                          11.230635    

[1 rows x 2367 columns]

In [17]:
dic_tsfresh

{'15c50a1059a9409aadecaea7c4b2d6c3':                                   NTC__variance_larger_than_standard_deviation  \
 15c50a1059a9409aadecaea7c4b2d6c3                                           1.0   
 
                                   NTC__has_duplicate_max  \
 15c50a1059a9409aadecaea7c4b2d6c3                     0.0   
 
                                   NTC__has_duplicate_min  NTC__has_duplicate  \
 15c50a1059a9409aadecaea7c4b2d6c3                     0.0                 1.0   
 
                                   NTC__sum_values  NTC__abs_energy  \
 15c50a1059a9409aadecaea7c4b2d6c3         694403.0     1.008783e+09   
 
                                   NTC__mean_abs_change  NTC__mean_change  \
 15c50a1059a9409aadecaea7c4b2d6c3              3.698113          0.004193   
 
                                   NTC__mean_second_derivative_central  \
 15c50a1059a9409aadecaea7c4b2d6c3                             -0.00105   
 
                                   NTC__median  ...  \
 15

In [18]:
import pickle

In [19]:
a_file = open("dic_tsfresh.pkl", "wb")
pickle.dump(dic_tsfresh, a_file)
a_file.close()


In the last cell we back up the work so far. And now - it remains to connect the tables that make up the dictionary, so that they connect to 3 data sets: training, validation and test. As stated the instruction was that any info session would not split, and would be complete in one of the 3 data sets. The loop in the next cell is designed to allow me to easily write the data sets. I made several attempts manually in order for the data to be split as follows: 60% training, 20% validation, 20% test.
Keep in mind that at this point there is the original data with the original features, in addition to the same data with the new features. After splitting, it is necessary to make a reconnection.

In [20]:
for session in id_unique:
    print ("dic_tsfresh['",session,"'], ")

dic_tsfresh[' 15c50a1059a9409aadecaea7c4b2d6c3 '], 
dic_tsfresh[' 06033f092c204fb8a890784f99e1d1fb '], 
dic_tsfresh[' c0a5655477844e37b8fcdf0448199abc '], 
dic_tsfresh[' 33309ed83f8b4e2d8196adb722fd25a7 '], 
dic_tsfresh[' 69109d0681cf4b5888ac9d2a1bdf8a49 '], 
dic_tsfresh[' 1f9e3c25ddbe4e4b870da6c932081c56 '], 
dic_tsfresh[' c240c36514c4460c954b39fbb1637f1e '], 
dic_tsfresh[' 151ae4400e8d475181808b73a2dea7ff '], 
dic_tsfresh[' d4a812f356fc41ecbe98dde417d54a40 '], 
dic_tsfresh[' 114312590f78424f93e81b4551ebbf34 '], 
dic_tsfresh[' d04d5e16d8e24105a15010b0c512026b '], 
dic_tsfresh[' cf90efff3f2c4b3388a450029f15d01d '], 
dic_tsfresh[' 20792537c7bd4a7e9f6b734a84b2bffc '], 
dic_tsfresh[' 9a9e244a4aaa43ccb570385f6702a9ff '], 
dic_tsfresh[' 8ab1ccdbe963420bbbb54b5e55718482 '], 
dic_tsfresh[' 30786e152e60477db9a6c0de5c8816a8 '], 
dic_tsfresh[' 0149b8bcd7754ff398cc5bebd1e43ccd '], 
dic_tsfresh[' 95e44eef0e4e4a85b5afc492d5a371fe '], 
dic_tsfresh[' 13f7093b71054ddaa00b8dc32bc5c14a '], 
dic_tsfresh[

In [97]:
train_ids = [dic_tsfresh['15c50a1059a9409aadecaea7c4b2d6c3'],
dic_tsfresh['06033f092c204fb8a890784f99e1d1fb'],
dic_tsfresh['c0a5655477844e37b8fcdf0448199abc'],
dic_tsfresh['33309ed83f8b4e2d8196adb722fd25a7'],
dic_tsfresh['69109d0681cf4b5888ac9d2a1bdf8a49'],
dic_tsfresh['1f9e3c25ddbe4e4b870da6c932081c56'],
dic_tsfresh['c240c36514c4460c954b39fbb1637f1e'],
dic_tsfresh['151ae4400e8d475181808b73a2dea7ff'],
dic_tsfresh['d4a812f356fc41ecbe98dde417d54a40'],
dic_tsfresh['114312590f78424f93e81b4551ebbf34'],
dic_tsfresh['d04d5e16d8e24105a15010b0c512026b'],
dic_tsfresh['cf90efff3f2c4b3388a450029f15d01d'],
dic_tsfresh['20792537c7bd4a7e9f6b734a84b2bffc'],
dic_tsfresh['9a9e244a4aaa43ccb570385f6702a9ff'],
dic_tsfresh['8ab1ccdbe963420bbbb54b5e55718482'],
dic_tsfresh['30786e152e60477db9a6c0de5c8816a8'],
dic_tsfresh['0149b8bcd7754ff398cc5bebd1e43ccd'],
dic_tsfresh['95e44eef0e4e4a85b5afc492d5a371fe'],
dic_tsfresh['13f7093b71054ddaa00b8dc32bc5c14a'],
dic_tsfresh['e3efb10152c14b2086745b3d6ebdb98e'],
dic_tsfresh['31736e17591a4e43a4ac7bd8741ffa02'],
dic_tsfresh['4c9c6fb31254409a913df4bfbe7629e2'],
dic_tsfresh['d290440871d443e4b08451182c8644ff'],
dic_tsfresh['56b43ec23389426f82b02463efa828c9'],
dic_tsfresh['d1cc7b7f2e4646abb1bbe8189c4a9c9d'],
dic_tsfresh['b643285a4f98496a85ff98c4e1851b1b'],
dic_tsfresh['d8c100c22cb14511a64f1105ee02a945'],
dic_tsfresh['4461aafa091c4b23b93a139544ef85c0'],
dic_tsfresh['4d6d95787f2b4dacb99efda11430f135'],
dic_tsfresh['a39fb11877a9459b95093e9787ba4b5b'],
dic_tsfresh['7933c57cc4d042b9b2e752100beb97d1'],
dic_tsfresh['6ee4abab3e784df19e6786b28cd0ea9b'],
dic_tsfresh['0a763b0c08664340a2beb63a7302474d'],
dic_tsfresh['18b9f9df61fc42f9a8d1b5cfd696071b'],
dic_tsfresh['11b995acdcfc4829a34585fa1c7c57af'],
dic_tsfresh['39c817b15c8a4b9780387e7639be6829'],
dic_tsfresh['b47d61c56d9e4bc7860992167cf76ef7'],
dic_tsfresh['aef6dafddad64424a3ea1f3129ad911d'],
dic_tsfresh['494263c4869d4480a8b54154d1ab2319'],
dic_tsfresh['6d0465247a3c48339eeb577c52f101ca'],
dic_tsfresh['c98b570f13574f6099f8b5705953e67a'],
dic_tsfresh['e6602a27157f435a803576082c9629c1'],
dic_tsfresh['e750a55d9c974cedaa1e5117c9465f7f'],
dic_tsfresh['4804c35d92a54e39b220a725d716bb3d'],
dic_tsfresh['203b006afc7943fb9941c466aa5e8e78'],
dic_tsfresh['3f6c0780c0f24a2d8854c902185c5126'],
dic_tsfresh['bc4413765d5b4b3780cb2413a4eb66e7'],
dic_tsfresh['d68d03ba60774ef9ba8e16fa9002f1a0'],
dic_tsfresh['a0856f98a2324d5ca7cd7da624984e03'],
dic_tsfresh['c97ba2a7527742248434345d42e55702'],
dic_tsfresh['be6fa4072df74baab99e6804dc63970d'],
dic_tsfresh['d57fc7a6359c4cae88704e73f74591b3'],
dic_tsfresh['8517c5373920464aa8f0b1fa509b0bf3'],
dic_tsfresh['b1d0ca7a39fd42bd844bcca43060fbaf'],
dic_tsfresh['b7e2e34b598c4e24be73487d67bc1f69'],
dic_tsfresh['a8e62837adf0462c981524094a66215a'],
dic_tsfresh['965a29c3aab64e1fb6e23b70cb66f006'],
dic_tsfresh['2633f27f7cd8434a975d1137ff1c03ab'],
dic_tsfresh['24bc47dd9c064b979b618d017ea82065'],
dic_tsfresh['47684cb9488a4f04bdef6e1b4f8c8dab'],
dic_tsfresh['1528a431dc164b6fa861510ff3e6c23c'],
dic_tsfresh['94027fe3458442c3b3c45f255a8af2c3'],
dic_tsfresh['f902d4bbe966493992194be788712ecf'],
dic_tsfresh['1934f59cf5c0455dbc0bd1e54b8f67a5'],
dic_tsfresh['ac898147c741406fa352251c4a911cd6'],
dic_tsfresh['b1b73e70bfca4cb2926e5a0538773b97'],
dic_tsfresh['4de6c5b3659d4912ac45edc5db557523'],
dic_tsfresh['aaedd9dac590487b8eb4e073c145c707'],
dic_tsfresh['fbe54f5e44284ec8b059efa407423d82'],
dic_tsfresh['37dcadf8bee2464f92b3dfd9922d0efd'],
dic_tsfresh['22c510ecf32e454f9003178e50ae0cd7'],
dic_tsfresh['1edca2c0c20c4235a11570383018d3b5'],
dic_tsfresh['49817d0ad1874b358dbbf5937913fb5e'],
dic_tsfresh['334bb190b0fc438d9876b087b95329b9'],
dic_tsfresh['17062a3d350f44339a402a8bc3d07d3d'],
dic_tsfresh['4fe8d5a9bbee4a84be2cf1a85988253b'],
dic_tsfresh['31d5dc052ce84152849548c080de2d07'],
dic_tsfresh['0b34b99f103c47438407bed0b2da8439'],
dic_tsfresh['fb050ff8daa441398410292684bc9583'],
dic_tsfresh['647b3d941d13445c8b0b7c8346d55954'],
dic_tsfresh['99fe00e6822a41b1b21197a6e781decd'],
dic_tsfresh['77e7f672e2d444988efe9252fd4df541'],
dic_tsfresh['7b060c7dbe8541e19d27cf83ed979be6'],
dic_tsfresh['4e47be082845477f9cdea025f0e2a06c'],
dic_tsfresh['96da762b2e084b5187af78a77a53beea'],
dic_tsfresh['faf490ab5ac74c3ca98a892ff0dfdbb2'],
dic_tsfresh['07ba8987fc9b49b9adca1f839160345b'],
dic_tsfresh['9bd30738f62147429221241a4b589c68'],
dic_tsfresh['16f3a37161c443a29ca7a8d2cbc1b8bb'],
dic_tsfresh['8990921171bc46f89e882a46f06b43cb'],
dic_tsfresh['681ef375d1394d2d98ff6bc1eae8d918'],
dic_tsfresh['4a659a0359ac40c39c58430b472bfca7'],
dic_tsfresh['23e61690544f458783d5cde98a781db8'],
dic_tsfresh['4db8fbae29d24e96a13babdb8f27a1c3'],
dic_tsfresh['0e01bfe404df403eb7cf2055c07d7105'],
dic_tsfresh['da4a1468bca0425482ea79aca86c03b8'],
dic_tsfresh['2e1ba85abc144074af3d02a5a348bb37'],
dic_tsfresh['b15013b59de84573bffc72e466247ad0'],
dic_tsfresh['bee94fdb39e2487481231fc97ece92ce'],
dic_tsfresh['9a46404aae3b406693885256d3232df3'],
dic_tsfresh['9195ec9a3acb463bbf29dfd981718e64'],
dic_tsfresh['584e346feb8b4915a829c8e7f76f85ec'],
dic_tsfresh['25cb45d1f3c8455f93886835dd71ad14'],
dic_tsfresh['c1c861e064504c21b2b8bc81ea8e6c3b'],
dic_tsfresh['33e0d8d0c5d04b55891144fdeced6b60'],
dic_tsfresh['6cc8a7a6953e4de391e609e941171a3a'],
dic_tsfresh['1631cedf3ef540ada1c5096060dd44ad'],
dic_tsfresh['ffe7d512018242e28df76cce0cc036de'],
dic_tsfresh['e1af6e6ae9424736845f43b09eefaf7a'],
dic_tsfresh['c0f0f35b65c54f2baa1da3e3f0f369c0'],
dic_tsfresh['221162a24c654905b6f8944d5e0cf991'],
dic_tsfresh['1c2ac0c0b5a54fe7a033e62b41ca1075'],
dic_tsfresh['f9f7906bf6f245b7b23fa4642d691412'],
dic_tsfresh['eca0b3df4faf4e50af74b489dadc2603'],
dic_tsfresh['90855a2f313747f9ac11e42044daf04f'],
dic_tsfresh['23b90502773d497b87a2dfff69872b08'],
dic_tsfresh['64a081bd61724b9391390b677af376c9'],
dic_tsfresh['cd831bf5ab0842fbac7684856ecca9f6'],
dic_tsfresh['88ff47085a2c4d90acb511d491358a1b'],
dic_tsfresh['8302e73b81114304aaf65786f57a77ed'],
dic_tsfresh['2c691111ebaf4a06b38d76573848b7c3'],
dic_tsfresh['a7d60379352646d1a6840f5849e39a24'],
dic_tsfresh['ffd5d2e11df24b978d51d4abdd4bdd77'],
dic_tsfresh['2ade630714c646c5b19386e34eabd6c4'],
dic_tsfresh['05c71780b43648399788edeb658889aa'],
dic_tsfresh['f5945ab2fd844c60bda09494c3d59873'],
dic_tsfresh['4317049dce9347e0be140564a5bed832'],
dic_tsfresh['e7743c527b894d2dbbe627cf5191c9c3'],
dic_tsfresh['dd6c96ee1a0a44f0bebf3ea6b2ec5e3e'],
dic_tsfresh['318a57ffb9f14c9b95479d2ae959770d'],
dic_tsfresh['be405a3f4b3344a6b356a8317da6d617'],
dic_tsfresh['958e097b302c479e8f7972bf30f8caa2'],
dic_tsfresh['0cdbb28163f84cf08d5cd9a6abc7c275'],
dic_tsfresh['490aae7eac1249c5bfb69d2be84cb58a'],
dic_tsfresh['40434e7ae7804d3794cf6069bf4fb7f5'],
dic_tsfresh['0316a719cdc240d8a8ae6608484dffae'],
dic_tsfresh['38fedebb96c14c79a458737d49e6aef0'],
dic_tsfresh['3fe7cec58c3f49eebe6f9987a4cbb6f1'],
dic_tsfresh['b9667493c28b4f8eb4959f51516fbc70'],
dic_tsfresh['2b5cf6cb8580456398ebd0ef64a897d7'],
dic_tsfresh['842fd1c6a33f4a9480effef7aebfcd78'],
dic_tsfresh['cbb288d4ff414dc4837fd806df166ef9'],
dic_tsfresh['36381d689bbc492daa140b0f6aee978e'],
dic_tsfresh['6fc4b3e1874a443c9dfc75dc03f21f10'],
dic_tsfresh['8327dce04e0946f1aaff1f8ac001c2dc'],
dic_tsfresh['b4b4651bfd7d473288f0fc57c6e0616a'],
dic_tsfresh['45aefaf00de543ff82af074521f6d485'],
dic_tsfresh['306513a1f03541c6b74e90453f43c878'],
dic_tsfresh['b5479ae69f02460c8609acf3587a8c61'],
dic_tsfresh['f41c2f1312d345d9bc102054b53a72c7'],
dic_tsfresh['6a39aff16c954755887e275fdfbcf82e'],
dic_tsfresh['1909e0c0b1354fb4aa17f15bcc159bcc'],
dic_tsfresh['7df435f7674340028c1383bca234af09'],
dic_tsfresh['796655b085484a5f9a699254ec1fee71'],
dic_tsfresh['75a25dfcea3c4b5980a38e69a3cffb56'],
dic_tsfresh['c16095d6d92c48a79dc9dcd016141bc8'],
dic_tsfresh['b76b726e0a774fb2b195f0fd72924ca6'],
dic_tsfresh['95556f1d3124427f90893eabe0bb48dc'],
dic_tsfresh['31ab3a9817674a9aa33dc0412b8940cf'],
dic_tsfresh['93b014542b7f426394ad0565b4dd72b3'],
dic_tsfresh['39964f0b1ca346daaea23e95ca71c546'],
dic_tsfresh['a38a4696919744baa937f841a320ec86'],
dic_tsfresh['89759fd6302c4c61a09be63ec73f2bc7'],
dic_tsfresh['e0825defcdb543aa89c0964da84ae2e0'],
dic_tsfresh['ec56919c2a5b4acd959d5d361731588f'],
dic_tsfresh['13fb7d91a5434be3acdc6650136c4528'],
dic_tsfresh['4a761002d37c4428a9ea65adf941f33d'],
dic_tsfresh['67840e4f5e2e40ae879470c644bf5f9c'],
dic_tsfresh['a9307f6c0c5f4771a211a03cff0b0f99'],
dic_tsfresh['0e5ea17c192d4ce993bf172b99f357f6'],
dic_tsfresh['bab4d43dcbc44df4b4ff6a62419f30c6'],
dic_tsfresh['82d1e36041244fdea5cc356679e7e926'],
dic_tsfresh['b5218d72ac5c4a4fb1a58aa7cb4331d3'],
dic_tsfresh['9549963fd74645f3bab4d788109c514a'],
dic_tsfresh['243446a2f339479289485abf72b752c5'],
dic_tsfresh['1e3d61b7cac24c62a010f116710b9703'],
dic_tsfresh['fe1a9f34769d499196438d2f9c09765e'],
dic_tsfresh['72be22140e814b90bd77bd83bbb971ad'],
dic_tsfresh['6c58ca7a64e44ef793b82be58d24d44f']

]

train_ids = pd.concat(train_ids)
train_ids.shape

(179, 2367)

In [94]:
validation_ids = [dic_tsfresh['cc5c8bcfb8c348a18c34523bc8705645'],
dic_tsfresh['13ff1cd6be5a4af0b4dd2f5fa24cff6b'],
dic_tsfresh['6418a96dd176490fbd4df5623c1a2ee3'],
dic_tsfresh['f7215673af734314a9e5798074c2a8c2'],
dic_tsfresh['f7b54a99049a4169aa3da093254ecb76'],
dic_tsfresh['b660d177d6a84d2dba1e23b92301279c'],
dic_tsfresh['ecb61756dbd14a7cb678d79c0c691c10'],
dic_tsfresh['98285ddc802648e6b86e5cdf7aa3c41a'],
dic_tsfresh['ce20e41a51dd4cc6b4fc0e035ec5079d'],
dic_tsfresh['7c7b5ca9eef84b45b30914d568860775'],
dic_tsfresh['0d62401243a147b6942f38ec0a103e73'],
dic_tsfresh['c45c3bcd5e8542c48f9ec4c4fee3c074'],
dic_tsfresh['2a1a43ad7a30460dbc8fea4f5fc07ade'],
dic_tsfresh['477a067121dc4a3db0a7f86b87279aa9'],
dic_tsfresh['121a0a371aa24781868792af2e030e5f'],
dic_tsfresh['fba643b92532440ea9776c33c35b6ace'],
dic_tsfresh['6b534e5354394a7281d592e724a279a0'],
dic_tsfresh['a1a916f55354450899185d74a25c872c'],
dic_tsfresh['6933e306784d4bfa809307744e12c82a'],
dic_tsfresh['1509358e6dda4f7ebaa35521b6811beb'],
dic_tsfresh['45dfe3e2dced4c46b6fab6cc74c2ad57'],
dic_tsfresh['e56da7e42a72495188df72d7ce34c19c'],
dic_tsfresh['9170712a51e944dcb877b3c425791e17'],
dic_tsfresh['9afb7961cfb2406d90ee5a162350e86b'],
dic_tsfresh['e7cd598fde834ce7b73a146598b6f768'],
dic_tsfresh['b61fd222b7ff4581b962b9c82aa187ee'],
dic_tsfresh['5c0decab30c540d290f3db54b61e62bc'],
dic_tsfresh['0f3ecc21cca044f889e17541eff51a88'],
dic_tsfresh['d505825721104ed7a624d2d20aaa40df'],
dic_tsfresh['50057e85e6bd48d98cc2b07fa10c5886'],
dic_tsfresh['15969800ce3140169107aa2fc58cd8fd'],
dic_tsfresh['1202068c82a8469d8765040d58b8df57'],
dic_tsfresh['cedbdd9d9e24409c9704a11ca0470a74'],
dic_tsfresh['ce9b7631df5846eeb7dbc1bc3271dc6a'],
dic_tsfresh['1ee54a59431c4025bc181b0d88a628da'],
dic_tsfresh['8cc080131be146deb2b5fa3e85da6563'],
dic_tsfresh['70d728fb861e45f8954bbb5ec5a47dcb'],
dic_tsfresh['99d11e15c4d440deb0183195faeea1a2'],
dic_tsfresh['e9acd14a218c4fa4b8a07345022a3f17'],
dic_tsfresh['afc8da1dbc3e4d7087e82ccc2d9a2ccd'],
dic_tsfresh['e3130d395ebd4409802874d380015f60'],
dic_tsfresh['faf5fbaf0e0a49fc96fa5ed1cd7b8ce2'],
dic_tsfresh['b0604e64e447484d8cc0f706ea2ec33a'],
dic_tsfresh['27f7055be4a74e68968df48a6bc6abbe'],
dic_tsfresh['d8c549b1b5d5454d9ed299a7b7ff87f8'],
dic_tsfresh['ee3761b64bfc4d6e8486404fadbecfc1'],
dic_tsfresh['f96905f611dc42338449fa984a6755f6'],
dic_tsfresh['cd6cd64e20544dccaf20cca2d80ec6c6'],
dic_tsfresh['808fc1e8d91f4503a454b04c4715b47c'],
dic_tsfresh['37ce4ebe8de74850bf795484b146faf3'],
dic_tsfresh['01f1616f1d05450188aab06aec94e657'],
dic_tsfresh['c95d52c117dc4007834271189dc835b3'],
dic_tsfresh['720c89d8ab7d4f99870b57cde11e6812']]


validation_ids = pd.concat(validation_ids)
validation_ids.shape

(53, 2367)

In [95]:
test_ids = [dic_tsfresh['817e4eb11ce74b18849f9a0ec56ec022'],
dic_tsfresh['97b85892e4ef482e93f7fd8eb6a60d3c'],
dic_tsfresh['0fafaa30e2d34398b8a14e566c73591d'],
dic_tsfresh['00cc0fe224394ebe88fc140bde163e22'],
dic_tsfresh['bbcf96de056d4f6aa169ff151859f7e8'],
dic_tsfresh['9bd9c2293fdf4698b1f3ee83122f887c'],
dic_tsfresh['3c74c2a63dac481097b86b373ef47c60'],
dic_tsfresh['9b19123bbf104a1f8e030a9a76363783'],
dic_tsfresh['ecd16cdad7ed49d2a9bebd504047373a'],
dic_tsfresh['a067a505377a431b97d0d6325162e96e'],
dic_tsfresh['e61522088c6c4b7295c886cbe81b298c'],
dic_tsfresh['000c889269f643d9ba032bebc2ec1181'],
dic_tsfresh['73e521a8bfa54cbbbfc29e6ee415705e'],
dic_tsfresh['ecbfec1cda2342adba29c06ec09f5560'],
dic_tsfresh['9b121aa54e3f45bab6f1ef3d94dd7677'],
dic_tsfresh['bf4d2a97b3d44a0a954ac48afd477b5e'],
dic_tsfresh['a7b88ba73323469ca79292edf20e823b'],
dic_tsfresh['3fc9f39cf8d5420b996a50013fdb99e7'],
dic_tsfresh['33df3b0ebdbf468dbc473c0930e8bc03'],
dic_tsfresh['7e6892fc4bfd4914b92017f5942b8699'],
dic_tsfresh['c233539ce22d4c1693a6ebe389cd499a'],
dic_tsfresh['7e705a09f79d4c789c6f434f672589a7'],
dic_tsfresh['61b41b3dd79846b9a832230d51348a05'],
dic_tsfresh['1d5cf518c55d47f393cfa5db789fa728'],
dic_tsfresh['50f0d4f37cd0459987cd6f8ff7b05819'],
dic_tsfresh['222495f0d4144d35a811bed17717e446'],
dic_tsfresh['cff1585ffc1a43f28085855ee2e66a40'],
dic_tsfresh['0c748aceb67b475499b349ab7aa3241f'],
dic_tsfresh['c1b24b35c969405594386ded2940699e'],
dic_tsfresh['c0b4e6e8dd7b4f6b924b60f5196df539'],
dic_tsfresh['5decd915fc374b689bdfbfe4cca85144'],
dic_tsfresh['97b01b4a4a334195a9af38e1b0907315'],
dic_tsfresh['25ecd11110054862a461b23a0d33412f'],
dic_tsfresh['f2c023bf838d480b9648832a66c72196'],
dic_tsfresh['96e36a49d2864d979ca84a85175ed971'],
dic_tsfresh['3464d8cb09234b278f2f6cbac06a250b'],
dic_tsfresh['e5f34d61e0b94f3e801bd3d63c821820'],
dic_tsfresh['aa2eccaa47044e858a7778c6dd0218d7'],
dic_tsfresh['78706db3677b4054a86a53213e69c188'],
dic_tsfresh['99a7b013570c4d5c80cdb1890192fca3'],
dic_tsfresh['93715d44d9984ff5abbb65a475a1e45f'],
dic_tsfresh['76437b2136f14590b4f8e8290be791d0'],
dic_tsfresh['73f68ff2dc2049ce96f172fbffb84bae'],
dic_tsfresh['a2a5ba65eff945a2a500f53734cce1bf'],
dic_tsfresh['2aa11595ddbb4bb68907c9065c5641f9'],
dic_tsfresh['61f2378d187a4121865d2b99d6f8d83d'],
dic_tsfresh['3532a27187254df9a6561e484b9ace74'],
dic_tsfresh['d652ab2a0fe84cfe98053bb0aca4c178'],
dic_tsfresh['22ed8e22f0d0421da9b25a55cc7acf30']
]

test_ids = pd.concat(test_ids)
test_ids.shape

(49, 2367)

In [90]:
ids_test = ['817e4eb11ce74b18849f9a0ec56ec022',
'97b85892e4ef482e93f7fd8eb6a60d3c',
'0fafaa30e2d34398b8a14e566c73591d',
'00cc0fe224394ebe88fc140bde163e22',
'bbcf96de056d4f6aa169ff151859f7e8',
'9bd9c2293fdf4698b1f3ee83122f887c',
'3c74c2a63dac481097b86b373ef47c60',
'9b19123bbf104a1f8e030a9a76363783',
'ecd16cdad7ed49d2a9bebd504047373a',
'a067a505377a431b97d0d6325162e96e',
'e61522088c6c4b7295c886cbe81b298c',
'000c889269f643d9ba032bebc2ec1181',
'73e521a8bfa54cbbbfc29e6ee415705e',
'ecbfec1cda2342adba29c06ec09f5560',
'9b121aa54e3f45bab6f1ef3d94dd7677',
'bf4d2a97b3d44a0a954ac48afd477b5e',
'a7b88ba73323469ca79292edf20e823b',
'3fc9f39cf8d5420b996a50013fdb99e7',
'33df3b0ebdbf468dbc473c0930e8bc03',
'7e6892fc4bfd4914b92017f5942b8699',
'c233539ce22d4c1693a6ebe389cd499a',
'7e705a09f79d4c789c6f434f672589a7',
'61b41b3dd79846b9a832230d51348a05',
'1d5cf518c55d47f393cfa5db789fa728',
'50f0d4f37cd0459987cd6f8ff7b05819',
'222495f0d4144d35a811bed17717e446',
'cff1585ffc1a43f28085855ee2e66a40',
'0c748aceb67b475499b349ab7aa3241f',
'c1b24b35c969405594386ded2940699e',
'c0b4e6e8dd7b4f6b924b60f5196df539',
'5decd915fc374b689bdfbfe4cca85144',
'97b01b4a4a334195a9af38e1b0907315',
'25ecd11110054862a461b23a0d33412f',
'f2c023bf838d480b9648832a66c72196',
'96e36a49d2864d979ca84a85175ed971',
'3464d8cb09234b278f2f6cbac06a250b',
'e5f34d61e0b94f3e801bd3d63c821820',
'aa2eccaa47044e858a7778c6dd0218d7',
'78706db3677b4054a86a53213e69c188',
'99a7b013570c4d5c80cdb1890192fca3',
'93715d44d9984ff5abbb65a475a1e45f',
'76437b2136f14590b4f8e8290be791d0',
'73f68ff2dc2049ce96f172fbffb84bae',
'a2a5ba65eff945a2a500f53734cce1bf',
'2aa11595ddbb4bb68907c9065c5641f9',
'61f2378d187a4121865d2b99d6f8d83d',
'3532a27187254df9a6561e484b9ace74',
'd652ab2a0fe84cfe98053bb0aca4c178',
'22ed8e22f0d0421da9b25a55cc7acf30',

]
df_test = df[df.SESSION_INFO_ID.isin(ids_test)]
df_test.shape

(22289, 57)

In [107]:
ids_train = ['15c50a1059a9409aadecaea7c4b2d6c3',
'06033f092c204fb8a890784f99e1d1fb',
'c0a5655477844e37b8fcdf0448199abc',
'33309ed83f8b4e2d8196adb722fd25a7',
'69109d0681cf4b5888ac9d2a1bdf8a49',
'1f9e3c25ddbe4e4b870da6c932081c56',
'c240c36514c4460c954b39fbb1637f1e',
'151ae4400e8d475181808b73a2dea7ff',
'd4a812f356fc41ecbe98dde417d54a40',
'114312590f78424f93e81b4551ebbf34',
'd04d5e16d8e24105a15010b0c512026b',
'cf90efff3f2c4b3388a450029f15d01d',
'20792537c7bd4a7e9f6b734a84b2bffc',
'9a9e244a4aaa43ccb570385f6702a9ff',
'8ab1ccdbe963420bbbb54b5e55718482',
'30786e152e60477db9a6c0de5c8816a8',
'0149b8bcd7754ff398cc5bebd1e43ccd',
'95e44eef0e4e4a85b5afc492d5a371fe',
'13f7093b71054ddaa00b8dc32bc5c14a',
'e3efb10152c14b2086745b3d6ebdb98e',
'31736e17591a4e43a4ac7bd8741ffa02',
'4c9c6fb31254409a913df4bfbe7629e2',
'd290440871d443e4b08451182c8644ff',
'56b43ec23389426f82b02463efa828c9',
'd1cc7b7f2e4646abb1bbe8189c4a9c9d',
'b643285a4f98496a85ff98c4e1851b1b',
'd8c100c22cb14511a64f1105ee02a945',
'4461aafa091c4b23b93a139544ef85c0',
'4d6d95787f2b4dacb99efda11430f135',
'a39fb11877a9459b95093e9787ba4b5b',
'7933c57cc4d042b9b2e752100beb97d1',
'6ee4abab3e784df19e6786b28cd0ea9b',
'0a763b0c08664340a2beb63a7302474d',
'18b9f9df61fc42f9a8d1b5cfd696071b',
'11b995acdcfc4829a34585fa1c7c57af',
'39c817b15c8a4b9780387e7639be6829',
'b47d61c56d9e4bc7860992167cf76ef7',
'aef6dafddad64424a3ea1f3129ad911d',
'494263c4869d4480a8b54154d1ab2319',
'6d0465247a3c48339eeb577c52f101ca',
'c98b570f13574f6099f8b5705953e67a',
'e6602a27157f435a803576082c9629c1',
'e750a55d9c974cedaa1e5117c9465f7f',
'4804c35d92a54e39b220a725d716bb3d',
'203b006afc7943fb9941c466aa5e8e78',
'3f6c0780c0f24a2d8854c902185c5126',
'bc4413765d5b4b3780cb2413a4eb66e7',
'd68d03ba60774ef9ba8e16fa9002f1a0',
'a0856f98a2324d5ca7cd7da624984e03',
'c97ba2a7527742248434345d42e55702',
'be6fa4072df74baab99e6804dc63970d',
'd57fc7a6359c4cae88704e73f74591b3',
'8517c5373920464aa8f0b1fa509b0bf3',
'b1d0ca7a39fd42bd844bcca43060fbaf',
'b7e2e34b598c4e24be73487d67bc1f69',
'a8e62837adf0462c981524094a66215a',
'965a29c3aab64e1fb6e23b70cb66f006',
'2633f27f7cd8434a975d1137ff1c03ab',
'24bc47dd9c064b979b618d017ea82065',
'47684cb9488a4f04bdef6e1b4f8c8dab',
'1528a431dc164b6fa861510ff3e6c23c',
'94027fe3458442c3b3c45f255a8af2c3',
'f902d4bbe966493992194be788712ecf',
'1934f59cf5c0455dbc0bd1e54b8f67a5',
'ac898147c741406fa352251c4a911cd6',
'b1b73e70bfca4cb2926e5a0538773b97',
'4de6c5b3659d4912ac45edc5db557523',
'aaedd9dac590487b8eb4e073c145c707',
'fbe54f5e44284ec8b059efa407423d82',
'37dcadf8bee2464f92b3dfd9922d0efd',
'22c510ecf32e454f9003178e50ae0cd7',
'1edca2c0c20c4235a11570383018d3b5',
'49817d0ad1874b358dbbf5937913fb5e',
'334bb190b0fc438d9876b087b95329b9',
'17062a3d350f44339a402a8bc3d07d3d',
'4fe8d5a9bbee4a84be2cf1a85988253b',
'31d5dc052ce84152849548c080de2d07',
'0b34b99f103c47438407bed0b2da8439',
'fb050ff8daa441398410292684bc9583',
'647b3d941d13445c8b0b7c8346d55954',
'99fe00e6822a41b1b21197a6e781decd',
'77e7f672e2d444988efe9252fd4df541',
'7b060c7dbe8541e19d27cf83ed979be6',
'4e47be082845477f9cdea025f0e2a06c',
'96da762b2e084b5187af78a77a53beea',
'faf490ab5ac74c3ca98a892ff0dfdbb2',
'07ba8987fc9b49b9adca1f839160345b',
'9bd30738f62147429221241a4b589c68',
'16f3a37161c443a29ca7a8d2cbc1b8bb',
'8990921171bc46f89e882a46f06b43cb',
'681ef375d1394d2d98ff6bc1eae8d918',
'4a659a0359ac40c39c58430b472bfca7',
'23e61690544f458783d5cde98a781db8',
'4db8fbae29d24e96a13babdb8f27a1c3',
'0e01bfe404df403eb7cf2055c07d7105',
'da4a1468bca0425482ea79aca86c03b8',
'2e1ba85abc144074af3d02a5a348bb37',
'b15013b59de84573bffc72e466247ad0',
'bee94fdb39e2487481231fc97ece92ce',
'9a46404aae3b406693885256d3232df3',
'9195ec9a3acb463bbf29dfd981718e64',
'584e346feb8b4915a829c8e7f76f85ec',
'25cb45d1f3c8455f93886835dd71ad14',
'c1c861e064504c21b2b8bc81ea8e6c3b',
'33e0d8d0c5d04b55891144fdeced6b60',
'6cc8a7a6953e4de391e609e941171a3a',
'1631cedf3ef540ada1c5096060dd44ad',
'ffe7d512018242e28df76cce0cc036de',
'e1af6e6ae9424736845f43b09eefaf7a',
'c0f0f35b65c54f2baa1da3e3f0f369c0',
'221162a24c654905b6f8944d5e0cf991',
'1c2ac0c0b5a54fe7a033e62b41ca1075',
'f9f7906bf6f245b7b23fa4642d691412',
'eca0b3df4faf4e50af74b489dadc2603',
'90855a2f313747f9ac11e42044daf04f',
'23b90502773d497b87a2dfff69872b08',
'64a081bd61724b9391390b677af376c9',
'cd831bf5ab0842fbac7684856ecca9f6',
'88ff47085a2c4d90acb511d491358a1b',
'8302e73b81114304aaf65786f57a77ed',
'2c691111ebaf4a06b38d76573848b7c3',
'a7d60379352646d1a6840f5849e39a24',
'ffd5d2e11df24b978d51d4abdd4bdd77',
'2ade630714c646c5b19386e34eabd6c4',
'05c71780b43648399788edeb658889aa',
'f5945ab2fd844c60bda09494c3d59873',
'4317049dce9347e0be140564a5bed832',
'e7743c527b894d2dbbe627cf5191c9c3',
'dd6c96ee1a0a44f0bebf3ea6b2ec5e3e',
'318a57ffb9f14c9b95479d2ae959770d',
'be405a3f4b3344a6b356a8317da6d617',
'958e097b302c479e8f7972bf30f8caa2',
'0cdbb28163f84cf08d5cd9a6abc7c275',
'490aae7eac1249c5bfb69d2be84cb58a',
'40434e7ae7804d3794cf6069bf4fb7f5',
'0316a719cdc240d8a8ae6608484dffae',
'38fedebb96c14c79a458737d49e6aef0',
'3fe7cec58c3f49eebe6f9987a4cbb6f1',
'b9667493c28b4f8eb4959f51516fbc70',
'2b5cf6cb8580456398ebd0ef64a897d7',
'842fd1c6a33f4a9480effef7aebfcd78',
'cbb288d4ff414dc4837fd806df166ef9',
'36381d689bbc492daa140b0f6aee978e',
'6fc4b3e1874a443c9dfc75dc03f21f10',
'8327dce04e0946f1aaff1f8ac001c2dc',
'b4b4651bfd7d473288f0fc57c6e0616a',
'45aefaf00de543ff82af074521f6d485',
'306513a1f03541c6b74e90453f43c878',
'b5479ae69f02460c8609acf3587a8c61',
'f41c2f1312d345d9bc102054b53a72c7',
'6a39aff16c954755887e275fdfbcf82e',
'1909e0c0b1354fb4aa17f15bcc159bcc',
'7df435f7674340028c1383bca234af09',
'796655b085484a5f9a699254ec1fee71',
'75a25dfcea3c4b5980a38e69a3cffb56',
'c16095d6d92c48a79dc9dcd016141bc8',
'b76b726e0a774fb2b195f0fd72924ca6',
'95556f1d3124427f90893eabe0bb48dc',
'31ab3a9817674a9aa33dc0412b8940cf',
'93b014542b7f426394ad0565b4dd72b3',
'39964f0b1ca346daaea23e95ca71c546',
'a38a4696919744baa937f841a320ec86',
'89759fd6302c4c61a09be63ec73f2bc7',
'e0825defcdb543aa89c0964da84ae2e0',
'ec56919c2a5b4acd959d5d361731588f',
'13fb7d91a5434be3acdc6650136c4528',
'4a761002d37c4428a9ea65adf941f33d',
'67840e4f5e2e40ae879470c644bf5f9c',
'a9307f6c0c5f4771a211a03cff0b0f99',
'0e5ea17c192d4ce993bf172b99f357f6',
'bab4d43dcbc44df4b4ff6a62419f30c6',
'82d1e36041244fdea5cc356679e7e926',
'b5218d72ac5c4a4fb1a58aa7cb4331d3',
'9549963fd74645f3bab4d788109c514a',
'243446a2f339479289485abf72b752c5',
'1e3d61b7cac24c62a010f116710b9703',
'fe1a9f34769d499196438d2f9c09765e',
'72be22140e814b90bd77bd83bbb971ad'
'6c58ca7a64e44ef793b82be58d24d44f',







]
df_train = df[df.SESSION_INFO_ID.isin(ids_train)]
df_train.shape

(69445, 57)

In [47]:
len(ids_train)

170

In [87]:
ids_validation =  ['cc5c8bcfb8c348a18c34523bc8705645',
'13ff1cd6be5a4af0b4dd2f5fa24cff6b',
'6418a96dd176490fbd4df5623c1a2ee3',
'f7215673af734314a9e5798074c2a8c2',
'f7b54a99049a4169aa3da093254ecb76',
'b660d177d6a84d2dba1e23b92301279c',
'ecb61756dbd14a7cb678d79c0c691c10',
'98285ddc802648e6b86e5cdf7aa3c41a',
'ce20e41a51dd4cc6b4fc0e035ec5079d',
'7c7b5ca9eef84b45b30914d568860775',
'0d62401243a147b6942f38ec0a103e73',
'c45c3bcd5e8542c48f9ec4c4fee3c074',
'2a1a43ad7a30460dbc8fea4f5fc07ade',
'477a067121dc4a3db0a7f86b87279aa9',
'121a0a371aa24781868792af2e030e5f',
'fba643b92532440ea9776c33c35b6ace',
'6b534e5354394a7281d592e724a279a0',
'a1a916f55354450899185d74a25c872c',
'6933e306784d4bfa809307744e12c82a',
'1509358e6dda4f7ebaa35521b6811beb',
'45dfe3e2dced4c46b6fab6cc74c2ad57',
'e56da7e42a72495188df72d7ce34c19c',
'9170712a51e944dcb877b3c425791e17',
'9afb7961cfb2406d90ee5a162350e86b',
'e7cd598fde834ce7b73a146598b6f768',
'b61fd222b7ff4581b962b9c82aa187ee',
'5c0decab30c540d290f3db54b61e62bc',
'0f3ecc21cca044f889e17541eff51a88',
'd505825721104ed7a624d2d20aaa40df',
'50057e85e6bd48d98cc2b07fa10c5886',
'15969800ce3140169107aa2fc58cd8fd',
'1202068c82a8469d8765040d58b8df57',
'cedbdd9d9e24409c9704a11ca0470a74',
'ce9b7631df5846eeb7dbc1bc3271dc6a',
'1ee54a59431c4025bc181b0d88a628da',
'8cc080131be146deb2b5fa3e85da6563',
'70d728fb861e45f8954bbb5ec5a47dcb',
'99d11e15c4d440deb0183195faeea1a2',
'e9acd14a218c4fa4b8a07345022a3f17',
'afc8da1dbc3e4d7087e82ccc2d9a2ccd',
'e3130d395ebd4409802874d380015f60',
'faf5fbaf0e0a49fc96fa5ed1cd7b8ce2',
'b0604e64e447484d8cc0f706ea2ec33a',
'27f7055be4a74e68968df48a6bc6abbe',
'd8c549b1b5d5454d9ed299a7b7ff87f8',
'ee3761b64bfc4d6e8486404fadbecfc1',
'f96905f611dc42338449fa984a6755f6',
'cd6cd64e20544dccaf20cca2d80ec6c6',
'808fc1e8d91f4503a454b04c4715b47c',
'37ce4ebe8de74850bf795484b146faf3',
'01f1616f1d05450188aab06aec94e657',
'c95d52c117dc4007834271189dc835b3',
'720c89d8ab7d4f99870b57cde11e6812',

]
df_validation = df[df.SESSION_INFO_ID.isin(ids_validation)]


In [88]:
df_validation.shape

(22537, 57)

In [98]:
test_ids['SESSION_INFO_ID'] = ids_test

In [33]:
test_ids

BAND_ARR_2__variance_larger_than_standard_deviation  \
817e4eb11ce74b18849f9a0ec56ec022                                                0.0     
97b85892e4ef482e93f7fd8eb6a60d3c                                                0.0     
0fafaa30e2d34398b8a14e566c73591d                                                1.0     
00cc0fe224394ebe88fc140bde163e22                                                0.0     
bbcf96de056d4f6aa169ff151859f7e8                                                0.0     
9bd9c2293fdf4698b1f3ee83122f887c                                                1.0     
3c74c2a63dac481097b86b373ef47c60                                                1.0     
9b19123bbf104a1f8e030a9a76363783                                                0.0     
ecd16cdad7ed49d2a9bebd504047373a                                                1.0     
a067a505377a431b97d0d6325162e96e                                                1.0     
e61522088c6c4b7295c886cbe81b298c                                                1.0     
000c889269f643d9ba032bebc2ec1181                                                0.0     
73e521a8bfa54cbbbfc29e6ee415705e                                                0.0     
ecbfec1cda2342adba29c06ec09f5560                                                1.0     
9b121aa54e3f45bab6f1ef3d94dd7677                                                0.0     
bf4d2a97b3d44a0a954ac48afd477b5e                                                0.0     
a7b88ba73323469ca79292edf20e823b                                                1.0     
3fc9f39cf8d5420b996a50013fdb99e7                                                1.0     
33df3b0ebdbf468dbc473c0930e8bc03                                                1.0     
7e6892fc4bfd4914b92017f5942b8699                                                1.0     
c233539ce22d4c1693a6ebe389cd499a                                                1.0     
7e705a09f79d4c789c6f434f672589a7                                                1.0     
61b41b3dd79846b9a832230d51348a05                                                0.0     
1d5cf518c55d47f393cfa5db789fa728                                                0.0     
50f0d4f37cd0459987cd6f8ff7b05819                                                0.0     
222495f0d4144d35a811bed17717e446                                                1.0     
cff1585ffc1a43f28085855ee2e66a40                                                0.0     
0c748aceb67b475499b349ab7aa3241f                                                1.0     
c1b24b35c969405594386ded2940699e                                                1.0     
c0b4e6e8dd7b4f6b924b60f5196df539                                                1.0     
5decd915fc374b689bdfbfe4cca85144                                                0.0     
97b01b4a4a334195a9af38e1b0907315                                                0.0     
25ecd11110054862a461b23a0d33412f                                                1.0     
f2c023bf838d480b9648832a66c72196                                                1.0     
96e36a49d2864d979ca84a85175ed971                                                1.0     
3464d8cb09234b278f2f6cbac06a250b                                                1.0     
e5f34d61e0b94f3e801bd3d63c821820                                                1.0     
aa2eccaa47044e858a7778c6dd0218d7                                                0.0     
78706db3677b4054a86a53213e69c188                                                1.0     
99a7b013570c4d5c80cdb1890192fca3                                                0.0     
93715d44d9984ff5abbb65a475a1e45f                                                1.0     
76437b2136f14590b4f8e8290be791d0                                                0.0     
73f68ff2dc2049ce96f172fbffb84bae                                                0.0     
a2a5ba65eff945a2a500f53734cce1bf                                                0.0     
2aa11595ddbb4bb68907c9065c564

Now - connecting the parts of the training, validation and test, to 3 final data sets.

In [99]:
df_test = df_test.set_index('SESSION_INFO_ID').join(test_ids.set_index('SESSION_INFO_ID'))

In [100]:
df_test.shape

(22289, 2423)

In [101]:
validation_ids['SESSION_INFO_ID'] = ids_validation


In [102]:
df_validation = df_validation.set_index('SESSION_INFO_ID').join(validation_ids.set_index('SESSION_INFO_ID'))

In [103]:
df_validation.shape

(22537, 2423)

In [105]:
train_ids.shape

(179, 2367)

In [106]:
len(ids_train)

178

In [108]:
train_ids['SESSION_INFO_ID'] = ids_train

In [109]:
df_train = df_train.set_index('SESSION_INFO_ID').join(train_ids.set_index('SESSION_INFO_ID'))

In [110]:
df_train.shape

(69445, 2423)

Now that we have the final data sets, we will save them for backup.

In [111]:
a_file = open("df_train.pkl", "wb")
pickle.dump(df_train, a_file)
a_file.close()


In [112]:
a_file = open("df_test.pkl", "wb")
pickle.dump(df_test, a_file)
a_file.close()




In [113]:
a_file = open("df_validation.pkl", "wb")
pickle.dump(df_validation, a_file)
a_file.close()




We will now select the final features that we will use for model training. To do this, we will create a table in which each row is a feature,
And each column is a method for selecting features, with each method giving each feature a score of 1 or 0.
Later in the process we will see how many points each feature received, and move on from there.

In [117]:
varSel = pd.DataFrame({'Variable': df_train.columns[0:2423]})
varSel = varSel.drop(index = 1)

varSel

Variable
0                                      INTERVAL_IN_FILE
2                                                    SN
3                                                ACCL_X
4                                                ACCL_Y
5                                                ACCL_Z
...                                                 ...
2418  BAND_ARR_8__matrix_profile__feature_"mean"__th...
2419  BAND_ARR_8__matrix_profile__feature_"median"__...
2420  BAND_ARR_8__matrix_profile__feature_"25"__thre...
2421  BAND_ARR_8__matrix_profile__feature_"75"__thre...
2422  BAND_ARR_8__mean_n_absolute_max__number_of_max...

[2422 rows x 1 columns]

In [118]:
X = df_train.loc[:, df_train.columns != 'VALUE']
y = df_train['VALUE']


In [119]:
from sklearn import preprocessing

def convert(data):
    number = preprocessing.LabelEncoder()
    data['S_I_CREATED_AT'] = number.fit_transform(data.S_I_CREATED_AT)
    data['DATE'] = number.fit_transform(data.DATE)
    data['GW_MAC'] = number.fit_transform(data.GW_MAC)
    data['GW_NAME'] = number.fit_transform(data.GW_NAME)
    data['TOOL_MAC'] = number.fit_transform(data.TOOL_MAC)
    data['TOOL_NAME'] = number.fit_transform(data.TOOL_NAME)       
    return data

X=convert(X)


C:\Users\Arie\AppData\Local\Temp/ipykernel_6140/3103963910.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data['S_I_CREATED_AT'] = number.fit_transform(data.S_I_CREATED_AT)
C:\Users\Arie\AppData\Local\Temp/ipykernel_6140/3103963910.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data['DATE'] = number.fit_transform(data.DATE)
C:\Users\Arie\AppData\Local\Temp/ipykernel_6140/3103963910.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_

In [120]:
from sklearn.linear_model import Lasso
from sklearn.feature_selection import SelectFromModel

lassomod = Lasso(alpha=0.01).fit(X, y)
model = SelectFromModel(lassomod, prefit=True)
varSel['Lasso'] = model.get_support().astype('int64')
varSel

C:\ProgramData\Anaconda3\lib\site-packages\sklearn\linear_model\_coordinate_descent.py:530: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 1805.0933897405407, tolerance: 1.5207241356469003
  model = cd_fast.enet_coordinate_descent(


Variable  Lasso
0                                      INTERVAL_IN_FILE      1
2                                                    SN      1
3                                                ACCL_X      0
4                                                ACCL_Y      0
5                                                ACCL_Z      0
...                                                 ...    ...
2418  BAND_ARR_8__matrix_profile__feature_"mean"__th...      0
2419  BAND_ARR_8__matrix_profile__feature_"median"__...      0
2420  BAND_ARR_8__matrix_profile__feature_"25"__thre...      0
2421  BAND_ARR_8__matrix_profile__feature_"75"__thre...      0
2422  BAND_ARR_8__mean_n_absolute_max__number_of_max...      0

[2422 rows x 2 columns]

In [121]:
from sklearn.ensemble import RandomForestClassifier
from sklearn.feature_selection import SelectFromModel

rfmod = RandomForestClassifier().fit(X, y)
model = SelectFromModel(rfmod, prefit=True)
varSel['RandomForest'] = model.get_support().astype('int64')
varSel

Variable  Lasso  RandomForest
0                                      INTERVAL_IN_FILE      1             1
2                                                    SN      1             1
3                                                ACCL_X      0             1
4                                                ACCL_Y      0             1
5                                                ACCL_Z      0             0
...                                                 ...    ...           ...
2418  BAND_ARR_8__matrix_profile__feature_"mean"__th...      0             0
2419  BAND_ARR_8__matrix_profile__feature_"median"__...      0             0
2420  BAND_ARR_8__matrix_profile__feature_"25"__thre...      0             0
2421  BAND_ARR_8__matrix_profile__feature_"75"__thre...      0             0
2422  BAND_ARR_8__mean_n_absolute_max__number_of_max...      0             0

[2422 rows x 3 columns]

In [122]:
from sklearn.ensemble import GradientBoostingClassifier
from sklearn.feature_selection import SelectFromModel

gbmod = GradientBoostingClassifier().fit(X, y)
model = SelectFromModel(gbmod, prefit=True)
varSel['GradientBoost'] = model.get_support().astype('int64')
varSel

Variable  Lasso  RandomForest  \
0                                      INTERVAL_IN_FILE      1             1   
2                                                    SN      1             1   
3                                                ACCL_X      0             1   
4                                                ACCL_Y      0             1   
5                                                ACCL_Z      0             0   
...                                                 ...    ...           ...   
2418  BAND_ARR_8__matrix_profile__feature_"mean"__th...      0             0   
2419  BAND_ARR_8__matrix_profile__feature_"median"__...      0             0   
2420  BAND_ARR_8__matrix_profile__feature_"25"__thre...      0             0   
2421  BAND_ARR_8__matrix_profile__feature_"75"__thre...      0             0   
2422  BAND_ARR_8__mean_n_absolute_max__number_of_max...      0             0   

      GradientBoost  
0                 1  
2                 0  
3                 0  
4                 0  
5                 0  
...             ...  
2418              0  
2419              0  
2420              0  
2421              0  
2422              0  

[2422 rows x 4 columns]

In [123]:
from sklearn.svm import LinearSVC
from sklearn.feature_selection import SelectFromModel

svmmod = LinearSVC(C=0.01, penalty="l1",dual=False).fit(X, y)

model = SelectFromModel(svmmod, prefit=True)
varSel['SVM'] = model.get_support().astype('int64')
varSel

C:\ProgramData\Anaconda3\lib\site-packages\sklearn\svm\_base.py:985: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  warnings.warn("Liblinear failed to converge, increase "


Variable  Lasso  RandomForest  \
0                                      INTERVAL_IN_FILE      1             1   
2                                                    SN      1             1   
3                                                ACCL_X      0             1   
4                                                ACCL_Y      0             1   
5                                                ACCL_Z      0             0   
...                                                 ...    ...           ...   
2418  BAND_ARR_8__matrix_profile__feature_"mean"__th...      0             0   
2419  BAND_ARR_8__matrix_profile__feature_"median"__...      0             0   
2420  BAND_ARR_8__matrix_profile__feature_"25"__thre...      0             0   
2421  BAND_ARR_8__matrix_profile__feature_"75"__thre...      0             0   
2422  BAND_ARR_8__mean_n_absolute_max__number_of_max...      0             0   

      GradientBoost  SVM  
0                 1    1  
2                 0    1  
3                 0    1  
4                 0    1  
5                 0    0  
...             ...  ...  
2418              0    0  
2419              0    0  
2420              0    0  
2421              0    0  
2422              0    0  

[2422 rows x 5 columns]

In [124]:
varSel['Sum'] =  np.sum(varSel,axis=1)
varSel.sort_values(by = 'Sum', ascending=False)

C:\Users\Arie\AppData\Roaming\Python\Python39\site-packages\numpy\core\fromnumeric.py:84: FutureWarning: Dropping of nuisance columns in DataFrame reductions (with 'numeric_only=None') is deprecated; in a future version this will raise TypeError.  Select only valid columns before calling the reduction.
  return reduction(axis=axis, out=out, **passkwargs)


Variable  Lasso  RandomForest  \
0                                      INTERVAL_IN_FILE      1             1   
39                                             BIT_FLAG      1             1   
13                                           BAND_ARR_8      1             1   
12                                           BAND_ARR_7      1             1   
11                                           BAND_ARR_6      1             1   
...                                                 ...    ...           ...   
1028  BAND_ARR_2__cwt_coefficients__coeff_13__w_2__w...      0             0   
1027  BAND_ARR_2__cwt_coefficients__coeff_12__w_20__...      0             0   
1025  BAND_ARR_2__cwt_coefficients__coeff_12__w_5__w...      0             0   
1024  BAND_ARR_2__cwt_coefficients__coeff_12__w_2__w...      0             0   
2422  BAND_ARR_8__mean_n_absolute_max__number_of_max...      0             0   

      GradientBoost  SVM  Sum  
0                 1    1    4  
39                1    1    4  
13                1    1    4  
12                1    1    4  
11                1    1    4  
...             ...  ...  ...  
1028              0    0    0  
1027              0    0    0  
1025              0    0    0  
1024              0    0    0  
2422              0    0    0  

[2422 rows x 6 columns]

In [319]:
a_file = open("varSel.pkl", "wb")
pickle.dump(varSel, a_file)
a_file.close()


Now that we have a score for each variable, we have to decide features starting from which score we want to put in the final data set. Only features that got all 4 possible points?
Features that received at least one point? Other?
To do this, we will create a number of data sets, based on the different scoring options - a data set only with the features that received 4 points, a data set with features that received 3 points or more, etc ...
On each data set we will run a baseline model and check its results. The data set that will get the best results, will be the one with which we will continue.

In [126]:
varSel.groupby('Sum')['Variable'].count()


Sum
0    1623
1     673
2     102
3      13
4      11
Name: Variable, dtype: int64

In [127]:
varSel_4 = varSel[varSel['Sum']==4]
varSel_4 = varSel_4['Variable']

In [128]:
for var in varSel_4:
    {print ("'",var,"',")}

' INTERVAL_IN_FILE ',
' BAND_ARR_5 ',
' BAND_ARR_6 ',
' BAND_ARR_7 ',
' BAND_ARR_8 ',
' BAND_ARR_13 ',
' BIT_FLAG ',
' MAX_VALUE ',
' NTC ',
' BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_1 ',
' BAND_ARR_8__fft_coefficient__attr_"real"__coeff_4 ',


In [180]:
df_train_4 = df_train[['INTERVAL_IN_FILE',
'BAND_ARR_5',
'BAND_ARR_6',
'BAND_ARR_7',
'BAND_ARR_8',
'BAND_ARR_13',
'BIT_FLAG',
'MAX_VALUE',
'NTC',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_1',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_4',
'VALUE'

]]

df_validation_4 = df_validation[['INTERVAL_IN_FILE',
'BAND_ARR_5',
'BAND_ARR_6',
'BAND_ARR_7',
'BAND_ARR_8',
'BAND_ARR_13',
'BIT_FLAG',
'MAX_VALUE',
'NTC',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_1',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_4',
'VALUE'

]]

df_test_4 = df_test[['INTERVAL_IN_FILE',
'BAND_ARR_5',
'BAND_ARR_6',
'BAND_ARR_7',
'BAND_ARR_8',
'BAND_ARR_13',
'BIT_FLAG',
'MAX_VALUE',
'NTC',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_1',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_4',
'VALUE'

]]



In [181]:
print (df_train_4.shape, df_validation_4.shape, df_test_4.shape)


(69445, 12) (22537, 12) (22289, 12)


In [134]:
varSel_at_leat_3 = varSel[varSel['Sum']>2]
varSel_at_leat_3 = varSel_at_leat_3['Variable']


In [135]:
for var in varSel_at_leat_3:
    {print ("'",var,"',")}

' INTERVAL_IN_FILE ',
' SN ',
' BAND_ARR_1 ',
' BAND_ARR_2 ',
' BAND_ARR_5 ',
' BAND_ARR_6 ',
' BAND_ARR_7 ',
' BAND_ARR_8 ',
' BAND_ARR_13 ',
' BAND_ARR_14 ',
' BAND_ARR_15 ',
' BIT_FLAG ',
' MAX_VALUE ',
' NTC ',
' NTC__cwt_coefficients__coeff_7__w_10__widths_(2, 5, 10, 20) ',
' NTC__cwt_coefficients__coeff_8__w_10__widths_(2, 5, 10, 20) ',
' NTC__cwt_coefficients__coeff_9__w_10__widths_(2, 5, 10, 20) ',
' NTC__cwt_coefficients__coeff_12__w_20__widths_(2, 5, 10, 20) ',
' NTC__cwt_coefficients__coeff_13__w_20__widths_(2, 5, 10, 20) ',
' NTC__ar_coefficient__coeff_0__k_10 ',
' NTC__fft_coefficient__attr_"real"__coeff_52 ',
' BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_1 ',
' BAND_ARR_8__sum_values ',
' BAND_ARR_8__fft_coefficient__attr_"real"__coeff_4 ',


In [182]:
df_test_at_least_3 = df_test[['INTERVAL_IN_FILE',
'SN',
'BAND_ARR_1',
'BAND_ARR_2',
'BAND_ARR_5',
'BAND_ARR_6',
'BAND_ARR_7',
'BAND_ARR_8',
'BAND_ARR_13',
'BAND_ARR_14',
'BAND_ARR_15',
'BIT_FLAG',
'MAX_VALUE',
'NTC',
'NTC__cwt_coefficients__coeff_7__w_10__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_8__w_10__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_9__w_10__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_12__w_20__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_13__w_20__widths_(2, 5, 10, 20)',
'NTC__ar_coefficient__coeff_0__k_10',
'NTC__fft_coefficient__attr_"real"__coeff_52',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_1',
'BAND_ARR_8__sum_values',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_4',
'VALUE'
]]

df_validation_at_least_3 = df_validation[['INTERVAL_IN_FILE',
'SN',
'BAND_ARR_1',
'BAND_ARR_2',
'BAND_ARR_5',
'BAND_ARR_6',
'BAND_ARR_7',
'BAND_ARR_8',
'BAND_ARR_13',
'BAND_ARR_14',
'BAND_ARR_15',
'BIT_FLAG',
'MAX_VALUE',
'NTC',
'NTC__cwt_coefficients__coeff_7__w_10__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_8__w_10__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_9__w_10__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_12__w_20__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_13__w_20__widths_(2, 5, 10, 20)',
'NTC__ar_coefficient__coeff_0__k_10',
'NTC__fft_coefficient__attr_"real"__coeff_52',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_1',
'BAND_ARR_8__sum_values',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_4',
'VALUE']]

df_train_at_least_3 = df_train[['INTERVAL_IN_FILE',
'SN',
'BAND_ARR_1',
'BAND_ARR_2',
'BAND_ARR_5',
'BAND_ARR_6',
'BAND_ARR_7',
'BAND_ARR_8',
'BAND_ARR_13',
'BAND_ARR_14',
'BAND_ARR_15',
'BIT_FLAG',
'MAX_VALUE',
'NTC',
'NTC__cwt_coefficients__coeff_7__w_10__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_8__w_10__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_9__w_10__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_12__w_20__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_13__w_20__widths_(2, 5, 10, 20)',
'NTC__ar_coefficient__coeff_0__k_10',
'NTC__fft_coefficient__attr_"real"__coeff_52',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_1',
'BAND_ARR_8__sum_values',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_4',
'VALUE']]


In [183]:
print (df_train_at_least_3.shape, df_validation_at_least_3.shape, df_test_at_least_3.shape)


(69445, 25) (22537, 25) (22289, 25)


In [161]:
varSel_at_leat_2 = varSel[varSel['Sum']>1]
varSel_at_leat_2 = varSel_at_leat_2['Variable']
for var in varSel_at_leat_2:
    {print ("'",var,"',")}

' INTERVAL_IN_FILE ',
' SN ',
' ACCL_X ',
' ACCL_Y ',
' BAND_ARR_1 ',
' BAND_ARR_2 ',
' BAND_ARR_3 ',
' BAND_ARR_4 ',
' BAND_ARR_5 ',
' BAND_ARR_6 ',
' BAND_ARR_7 ',
' BAND_ARR_8 ',
' BAND_ARR_9 ',
' BAND_ARR_10 ',
' BAND_ARR_11 ',
' BAND_ARR_12 ',
' BAND_ARR_13 ',
' BAND_ARR_14 ',
' BAND_ARR_15 ',
' BAND_ARR_16 ',
' BAND_ARR_17 ',
' BAND_ARR_21 ',
' BAND_ARR_25 ',
' BAND_ARR_27 ',
' BAND_ARR_28 ',
' BAND_ARR_30 ',
' BAND_ARR_32 ',
' BATTERY ',
' BIT_FLAG ',
' MAX_VALUE ',
' MIC_TD_RAW ',
' NTC ',
' FIRST_PACKET_TS ',
' NTC__mean ',
' NTC__quantile__q_0.2 ',
' NTC__quantile__q_0.6 ',
' NTC__cwt_coefficients__coeff_2__w_2__widths_(2, 5, 10, 20) ',
' NTC__cwt_coefficients__coeff_3__w_5__widths_(2, 5, 10, 20) ',
' NTC__cwt_coefficients__coeff_4__w_5__widths_(2, 5, 10, 20) ',
' NTC__cwt_coefficients__coeff_6__w_20__widths_(2, 5, 10, 20) ',
' NTC__cwt_coefficients__coeff_7__w_5__widths_(2, 5, 10, 20) ',
' NTC__cwt_coefficients__coeff_7__w_10__widths_(2, 5, 10, 20) ',
' NTC__cwt_coefficients

In [184]:
df_test_at_least_2 = df_test[['INTERVAL_IN_FILE',
'SN',
'ACCL_X',
'ACCL_Y',
'BAND_ARR_1',
'BAND_ARR_2',
'BAND_ARR_3',
'BAND_ARR_4',
'BAND_ARR_5',
'BAND_ARR_6',
'BAND_ARR_7',
'BAND_ARR_8',
'BAND_ARR_9',
'BAND_ARR_10',
'BAND_ARR_11',
'BAND_ARR_12',
'BAND_ARR_13',
'BAND_ARR_14',
'BAND_ARR_15',
'BAND_ARR_16',
'BAND_ARR_17',
'BAND_ARR_21',
'BAND_ARR_25',
'BAND_ARR_27',
'BAND_ARR_28',
'BAND_ARR_30',
'BAND_ARR_32',
'BATTERY',
'BIT_FLAG',
'MAX_VALUE',
'MIC_TD_RAW',
'NTC',
'FIRST_PACKET_TS',
'NTC__mean',
'NTC__quantile__q_0.2',
'NTC__quantile__q_0.6',
'NTC__cwt_coefficients__coeff_2__w_2__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_3__w_5__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_4__w_5__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_6__w_20__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_7__w_5__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_7__w_10__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_8__w_10__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_9__w_5__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_9__w_10__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_10__w_20__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_11__w_20__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_12__w_10__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_12__w_20__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_13__w_20__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_14__w_20__widths_(2, 5, 10, 20)',
'NTC__ar_coefficient__coeff_0__k_10',
'NTC__fft_coefficient__attr_"real"__coeff_1',
'NTC__fft_coefficient__attr_"real"__coeff_4',
'NTC__fft_coefficient__attr_"real"__coeff_52',
'NTC__fft_coefficient__attr_"real"__coeff_90',
'NTC__fft_coefficient__attr_"imag"__coeff_3',
'NTC__fft_coefficient__attr_"imag"__coeff_4',
'NTC__fft_coefficient__attr_"imag"__coeff_17',
'NTC__fft_coefficient__attr_"imag"__coeff_26',
'NTC__fft_coefficient__attr_"imag"__coeff_27',
'NTC__fft_coefficient__attr_"imag"__coeff_28',
'NTC__fft_coefficient__attr_"imag"__coeff_29',
'NTC__fft_coefficient__attr_"imag"__coeff_33',
'NTC__fft_coefficient__attr_"imag"__coeff_37',
'NTC__fft_coefficient__attr_"imag"__coeff_59',
'NTC__fft_coefficient__attr_"imag"__coeff_93',
'NTC__fft_coefficient__attr_"abs"__coeff_8',
'NTC__fft_coefficient__attr_"angle"__coeff_9',
'NTC__fft_coefficient__attr_"angle"__coeff_10',
'NTC__fft_coefficient__attr_"angle"__coeff_45',
'NTC__fft_coefficient__attr_"angle"__coeff_46',
'NTC__fft_coefficient__attr_"angle"__coeff_59',
'NTC__fft_coefficient__attr_"angle"__coeff_77',
'NTC__fft_coefficient__attr_"angle"__coeff_86',
'NTC__fft_coefficient__attr_"angle"__coeff_95',
'NTC__agg_linear_trend__attr_"intercept"__chunk_len_5__f_agg_"max"',
'NTC__agg_linear_trend__attr_"intercept"__chunk_len_50__f_agg_"max"',
'BAND_ARR_2__sum_values',
'BAND_ARR_2__count_below_mean',
'BAND_ARR_2__spkt_welch_density__coeff_2',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_2',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_3',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_1',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_2',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_3',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_5',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_1',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_2',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_4',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_9',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_12',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_40',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_49',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_51',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_64',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_65',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_70',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_81',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_89',
'BAND_ARR_2__range_count__max_1__min_-1',
'BAND_ARR_2__agg_linear_trend__attr_"rvalue"__chunk_len_50__f_agg_"mean"',
'BAND_ARR_2__agg_linear_trend__attr_"intercept"__chunk_len_50__f_agg_"min"',
'BAND_ARR_8__sum_values',
'BAND_ARR_8__longest_strike_below_mean',
'BAND_ARR_8__c3__lag_1',
'BAND_ARR_8__quantile__q_0.8',
'BAND_ARR_8__change_quantiles__f_agg_"mean"__isabs_True__qh_0.8__ql_0.6',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_3',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_4',
'BAND_ARR_8__fft_coefficient__attr_"abs"__coeff_0',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_2',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_7',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_14',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_15',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_38',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_58',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_62',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_64',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_65',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_69',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_72',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_78',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_95',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_96',
'BAND_ARR_8__max_langevin_fixed_point__m_3__r_30',
'VALUE'

]]

df_validation_at_least_2 = df_validation[['INTERVAL_IN_FILE',
'SN',
'ACCL_X',
'ACCL_Y',
'BAND_ARR_1',
'BAND_ARR_2',
'BAND_ARR_3',
'BAND_ARR_4',
'BAND_ARR_5',
'BAND_ARR_6',
'BAND_ARR_7',
'BAND_ARR_8',
'BAND_ARR_9',
'BAND_ARR_10',
'BAND_ARR_11',
'BAND_ARR_12',
'BAND_ARR_13',
'BAND_ARR_14',
'BAND_ARR_15',
'BAND_ARR_16',
'BAND_ARR_17',
'BAND_ARR_21',
'BAND_ARR_25',
'BAND_ARR_27',
'BAND_ARR_28',
'BAND_ARR_30',
'BAND_ARR_32',
'BATTERY',
'BIT_FLAG',
'MAX_VALUE',
'MIC_TD_RAW',
'NTC',
'FIRST_PACKET_TS',
'NTC__mean',
'NTC__quantile__q_0.2',
'NTC__quantile__q_0.6',
'NTC__cwt_coefficients__coeff_2__w_2__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_3__w_5__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_4__w_5__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_6__w_20__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_7__w_5__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_7__w_10__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_8__w_10__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_9__w_5__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_9__w_10__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_10__w_20__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_11__w_20__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_12__w_10__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_12__w_20__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_13__w_20__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_14__w_20__widths_(2, 5, 10, 20)',
'NTC__ar_coefficient__coeff_0__k_10',
'NTC__fft_coefficient__attr_"real"__coeff_1',
'NTC__fft_coefficient__attr_"real"__coeff_4',
'NTC__fft_coefficient__attr_"real"__coeff_52',
'NTC__fft_coefficient__attr_"real"__coeff_90',
'NTC__fft_coefficient__attr_"imag"__coeff_3',
'NTC__fft_coefficient__attr_"imag"__coeff_4',
'NTC__fft_coefficient__attr_"imag"__coeff_17',
'NTC__fft_coefficient__attr_"imag"__coeff_26',
'NTC__fft_coefficient__attr_"imag"__coeff_27',
'NTC__fft_coefficient__attr_"imag"__coeff_28',
'NTC__fft_coefficient__attr_"imag"__coeff_29',
'NTC__fft_coefficient__attr_"imag"__coeff_33',
'NTC__fft_coefficient__attr_"imag"__coeff_37',
'NTC__fft_coefficient__attr_"imag"__coeff_59',
'NTC__fft_coefficient__attr_"imag"__coeff_93',
'NTC__fft_coefficient__attr_"abs"__coeff_8',
'NTC__fft_coefficient__attr_"angle"__coeff_9',
'NTC__fft_coefficient__attr_"angle"__coeff_10',
'NTC__fft_coefficient__attr_"angle"__coeff_45',
'NTC__fft_coefficient__attr_"angle"__coeff_46',
'NTC__fft_coefficient__attr_"angle"__coeff_59',
'NTC__fft_coefficient__attr_"angle"__coeff_77',
'NTC__fft_coefficient__attr_"angle"__coeff_86',
'NTC__fft_coefficient__attr_"angle"__coeff_95',
'NTC__agg_linear_trend__attr_"intercept"__chunk_len_5__f_agg_"max"',
'NTC__agg_linear_trend__attr_"intercept"__chunk_len_50__f_agg_"max"',
'BAND_ARR_2__sum_values',
'BAND_ARR_2__count_below_mean',
'BAND_ARR_2__spkt_welch_density__coeff_2',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_2',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_3',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_1',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_2',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_3',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_5',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_1',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_2',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_4',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_9',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_12',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_40',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_49',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_51',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_64',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_65',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_70',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_81',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_89',
'BAND_ARR_2__range_count__max_1__min_-1',
'BAND_ARR_2__agg_linear_trend__attr_"rvalue"__chunk_len_50__f_agg_"mean"',
'BAND_ARR_2__agg_linear_trend__attr_"intercept"__chunk_len_50__f_agg_"min"',
'BAND_ARR_8__sum_values',
'BAND_ARR_8__longest_strike_below_mean',
'BAND_ARR_8__c3__lag_1',
'BAND_ARR_8__quantile__q_0.8',
'BAND_ARR_8__change_quantiles__f_agg_"mean"__isabs_True__qh_0.8__ql_0.6',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_3',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_4',
'BAND_ARR_8__fft_coefficient__attr_"abs"__coeff_0',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_2',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_7',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_14',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_15',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_38',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_58',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_62',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_64',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_65',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_69',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_72',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_78',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_95',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_96',
'BAND_ARR_8__max_langevin_fixed_point__m_3__r_30',
'VALUE'

]]

df_train_at_least_2 = df_train[['INTERVAL_IN_FILE',
'SN',
'ACCL_X',
'ACCL_Y',
'BAND_ARR_1',
'BAND_ARR_2',
'BAND_ARR_3',
'BAND_ARR_4',
'BAND_ARR_5',
'BAND_ARR_6',
'BAND_ARR_7',
'BAND_ARR_8',
'BAND_ARR_9',
'BAND_ARR_10',
'BAND_ARR_11',
'BAND_ARR_12',
'BAND_ARR_13',
'BAND_ARR_14',
'BAND_ARR_15',
'BAND_ARR_16',
'BAND_ARR_17',
'BAND_ARR_21',
'BAND_ARR_25',
'BAND_ARR_27',
'BAND_ARR_28',
'BAND_ARR_30',
'BAND_ARR_32',
'BATTERY',
'BIT_FLAG',
'MAX_VALUE',
'MIC_TD_RAW',
'NTC',
'FIRST_PACKET_TS',
'NTC__mean',
'NTC__quantile__q_0.2',
'NTC__quantile__q_0.6',
'NTC__cwt_coefficients__coeff_2__w_2__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_3__w_5__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_4__w_5__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_6__w_20__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_7__w_5__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_7__w_10__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_8__w_10__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_9__w_5__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_9__w_10__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_10__w_20__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_11__w_20__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_12__w_10__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_12__w_20__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_13__w_20__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_14__w_20__widths_(2, 5, 10, 20)',
'NTC__ar_coefficient__coeff_0__k_10',
'NTC__fft_coefficient__attr_"real"__coeff_1',
'NTC__fft_coefficient__attr_"real"__coeff_4',
'NTC__fft_coefficient__attr_"real"__coeff_52',
'NTC__fft_coefficient__attr_"real"__coeff_90',
'NTC__fft_coefficient__attr_"imag"__coeff_3',
'NTC__fft_coefficient__attr_"imag"__coeff_4',
'NTC__fft_coefficient__attr_"imag"__coeff_17',
'NTC__fft_coefficient__attr_"imag"__coeff_26',
'NTC__fft_coefficient__attr_"imag"__coeff_27',
'NTC__fft_coefficient__attr_"imag"__coeff_28',
'NTC__fft_coefficient__attr_"imag"__coeff_29',
'NTC__fft_coefficient__attr_"imag"__coeff_33',
'NTC__fft_coefficient__attr_"imag"__coeff_37',
'NTC__fft_coefficient__attr_"imag"__coeff_59',
'NTC__fft_coefficient__attr_"imag"__coeff_93',
'NTC__fft_coefficient__attr_"abs"__coeff_8',
'NTC__fft_coefficient__attr_"angle"__coeff_9',
'NTC__fft_coefficient__attr_"angle"__coeff_10',
'NTC__fft_coefficient__attr_"angle"__coeff_45',
'NTC__fft_coefficient__attr_"angle"__coeff_46',
'NTC__fft_coefficient__attr_"angle"__coeff_59',
'NTC__fft_coefficient__attr_"angle"__coeff_77',
'NTC__fft_coefficient__attr_"angle"__coeff_86',
'NTC__fft_coefficient__attr_"angle"__coeff_95',
'NTC__agg_linear_trend__attr_"intercept"__chunk_len_5__f_agg_"max"',
'NTC__agg_linear_trend__attr_"intercept"__chunk_len_50__f_agg_"max"',
'BAND_ARR_2__sum_values',
'BAND_ARR_2__count_below_mean',
'BAND_ARR_2__spkt_welch_density__coeff_2',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_2',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_3',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_1',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_2',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_3',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_5',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_1',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_2',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_4',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_9',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_12',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_40',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_49',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_51',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_64',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_65',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_70',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_81',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_89',
'BAND_ARR_2__range_count__max_1__min_-1',
'BAND_ARR_2__agg_linear_trend__attr_"rvalue"__chunk_len_50__f_agg_"mean"',
'BAND_ARR_2__agg_linear_trend__attr_"intercept"__chunk_len_50__f_agg_"min"',
'BAND_ARR_8__sum_values',
'BAND_ARR_8__longest_strike_below_mean',
'BAND_ARR_8__c3__lag_1',
'BAND_ARR_8__quantile__q_0.8',
'BAND_ARR_8__change_quantiles__f_agg_"mean"__isabs_True__qh_0.8__ql_0.6',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_3',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_4',
'BAND_ARR_8__fft_coefficient__attr_"abs"__coeff_0',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_2',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_7',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_14',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_15',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_38',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_58',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_62',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_64',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_65',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_69',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_72',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_78',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_95',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_96',
'BAND_ARR_8__max_langevin_fixed_point__m_3__r_30',
'VALUE'

]]



In [185]:
print(df_train_at_least_2.shape, df_validation_at_least_2.shape, df_test_at_least_2.shape)

(69445, 127) (22537, 127) (22289, 127)


In [165]:
varSel_at_leat_1 = varSel[varSel['Sum']>0]
varSel_at_leat_1 = varSel_at_leat_1['Variable']
for var in varSel_at_leat_1:
    {print ("'",var,"',")}

' INTERVAL_IN_FILE ',
' SN ',
' ACCL_X ',
' ACCL_Y ',
' BAND_ARR_1 ',
' BAND_ARR_2 ',
' BAND_ARR_3 ',
' BAND_ARR_4 ',
' BAND_ARR_5 ',
' BAND_ARR_6 ',
' BAND_ARR_7 ',
' BAND_ARR_8 ',
' BAND_ARR_9 ',
' BAND_ARR_10 ',
' BAND_ARR_11 ',
' BAND_ARR_12 ',
' BAND_ARR_13 ',
' BAND_ARR_14 ',
' BAND_ARR_15 ',
' BAND_ARR_16 ',
' BAND_ARR_17 ',
' BAND_ARR_18 ',
' BAND_ARR_19 ',
' BAND_ARR_20 ',
' BAND_ARR_21 ',
' BAND_ARR_22 ',
' BAND_ARR_23 ',
' BAND_ARR_24 ',
' BAND_ARR_25 ',
' BAND_ARR_26 ',
' BAND_ARR_27 ',
' BAND_ARR_28 ',
' BAND_ARR_29 ',
' BAND_ARR_30 ',
' BAND_ARR_31 ',
' BAND_ARR_32 ',
' BATTERY ',
' BIT_FLAG ',
' MAX_VALUE ',
' MIC_TD_RAW ',
' MIN_VALUE ',
' NTC ',
' VAA ',
' ADVERTISE_TS ',
' FIRST_PACKET_TS ',
' RSSI ',
' NTC__mean_change ',
' NTC__median ',
' NTC__mean ',
' NTC__standard_deviation ',
' NTC__root_mean_square ',
' NTC__count_above_mean ',
' NTC__count_below_mean ',
' NTC__maximum ',
' NTC__absolute_maximum ',
' NTC__minimum ',
' NTC__c3__lag_3 ',
' NTC__cid_ce__normalize

In [186]:
df_test_at_least_1 = df_test[['INTERVAL_IN_FILE',
'SN',
'ACCL_X',
'ACCL_Y',
'BAND_ARR_1',
'BAND_ARR_2',
'BAND_ARR_3',
'BAND_ARR_4',
'BAND_ARR_5',
'BAND_ARR_6',
'BAND_ARR_7',
'BAND_ARR_8',
'BAND_ARR_9',
'BAND_ARR_10',
'BAND_ARR_11',
'BAND_ARR_12',
'BAND_ARR_13',
'BAND_ARR_14',
'BAND_ARR_15',
'BAND_ARR_16',
'BAND_ARR_17',
'BAND_ARR_18',
'BAND_ARR_19',
'BAND_ARR_20',
'BAND_ARR_21',
'BAND_ARR_22',
'BAND_ARR_23',
'BAND_ARR_24',
'BAND_ARR_25',
'BAND_ARR_26',
'BAND_ARR_27',
'BAND_ARR_28',
'BAND_ARR_29',
'BAND_ARR_30',
'BAND_ARR_31',
'BAND_ARR_32',
'BATTERY',
'BIT_FLAG',
'MAX_VALUE',
'MIC_TD_RAW',
'MIN_VALUE',
'NTC',
'VAA',
'ADVERTISE_TS',
'FIRST_PACKET_TS',
'RSSI',
'NTC__mean_change',
'NTC__median',
'NTC__mean',
'NTC__standard_deviation',
'NTC__root_mean_square',
'NTC__count_above_mean',
'NTC__count_below_mean',
'NTC__maximum',
'NTC__absolute_maximum',
'NTC__minimum',
'NTC__c3__lag_3',
'NTC__cid_ce__normalize_False',
'NTC__quantile__q_0.1',
'NTC__quantile__q_0.2',
'NTC__quantile__q_0.3',
'NTC__quantile__q_0.4',
'NTC__quantile__q_0.6',
'NTC__quantile__q_0.7',
'NTC__quantile__q_0.8',
'NTC__quantile__q_0.9',
'NTC__number_cwt_peaks__n_1',
'NTC__number_cwt_peaks__n_5',
'NTC__number_peaks__n_1',
'NTC__cwt_coefficients__coeff_0__w_2__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_1__w_2__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_1__w_5__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_1__w_10__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_1__w_20__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_2__w_2__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_2__w_5__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_2__w_10__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_2__w_20__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_3__w_2__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_3__w_5__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_3__w_10__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_3__w_20__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_4__w_2__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_4__w_5__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_4__w_10__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_4__w_20__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_5__w_2__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_5__w_5__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_5__w_10__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_5__w_20__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_6__w_2__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_6__w_5__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_6__w_10__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_6__w_20__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_7__w_5__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_7__w_10__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_7__w_20__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_8__w_5__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_8__w_10__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_8__w_20__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_9__w_5__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_9__w_10__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_9__w_20__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_10__w_5__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_10__w_10__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_10__w_20__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_11__w_5__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_11__w_10__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_11__w_20__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_12__w_5__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_12__w_10__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_12__w_20__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_13__w_5__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_13__w_10__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_13__w_20__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_14__w_5__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_14__w_10__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_14__w_20__widths_(2, 5, 10, 20)',
'NTC__ar_coefficient__coeff_0__k_10',
'NTC__change_quantiles__f_agg_"var"__isabs_False__qh_0.4__ql_0.2',
'NTC__fft_coefficient__attr_"real"__coeff_1',
'NTC__fft_coefficient__attr_"real"__coeff_2',
'NTC__fft_coefficient__attr_"real"__coeff_3',
'NTC__fft_coefficient__attr_"real"__coeff_4',
'NTC__fft_coefficient__attr_"real"__coeff_9',
'NTC__fft_coefficient__attr_"real"__coeff_10',
'NTC__fft_coefficient__attr_"real"__coeff_13',
'NTC__fft_coefficient__attr_"real"__coeff_15',
'NTC__fft_coefficient__attr_"real"__coeff_18',
'NTC__fft_coefficient__attr_"real"__coeff_21',
'NTC__fft_coefficient__attr_"real"__coeff_22',
'NTC__fft_coefficient__attr_"real"__coeff_23',
'NTC__fft_coefficient__attr_"real"__coeff_24',
'NTC__fft_coefficient__attr_"real"__coeff_27',
'NTC__fft_coefficient__attr_"real"__coeff_28',
'NTC__fft_coefficient__attr_"real"__coeff_30',
'NTC__fft_coefficient__attr_"real"__coeff_31',
'NTC__fft_coefficient__attr_"real"__coeff_32',
'NTC__fft_coefficient__attr_"real"__coeff_38',
'NTC__fft_coefficient__attr_"real"__coeff_40',
'NTC__fft_coefficient__attr_"real"__coeff_42',
'NTC__fft_coefficient__attr_"real"__coeff_43',
'NTC__fft_coefficient__attr_"real"__coeff_45',
'NTC__fft_coefficient__attr_"real"__coeff_46',
'NTC__fft_coefficient__attr_"real"__coeff_50',
'NTC__fft_coefficient__attr_"real"__coeff_52',
'NTC__fft_coefficient__attr_"real"__coeff_55',
'NTC__fft_coefficient__attr_"real"__coeff_57',
'NTC__fft_coefficient__attr_"real"__coeff_59',
'NTC__fft_coefficient__attr_"real"__coeff_64',
'NTC__fft_coefficient__attr_"real"__coeff_65',
'NTC__fft_coefficient__attr_"real"__coeff_66',
'NTC__fft_coefficient__attr_"real"__coeff_67',
'NTC__fft_coefficient__attr_"real"__coeff_68',
'NTC__fft_coefficient__attr_"real"__coeff_69',
'NTC__fft_coefficient__attr_"real"__coeff_70',
'NTC__fft_coefficient__attr_"real"__coeff_71',
'NTC__fft_coefficient__attr_"real"__coeff_72',
'NTC__fft_coefficient__attr_"real"__coeff_74',
'NTC__fft_coefficient__attr_"real"__coeff_75',
'NTC__fft_coefficient__attr_"real"__coeff_76',
'NTC__fft_coefficient__attr_"real"__coeff_77',
'NTC__fft_coefficient__attr_"real"__coeff_78',
'NTC__fft_coefficient__attr_"real"__coeff_81',
'NTC__fft_coefficient__attr_"real"__coeff_83',
'NTC__fft_coefficient__attr_"real"__coeff_86',
'NTC__fft_coefficient__attr_"real"__coeff_87',
'NTC__fft_coefficient__attr_"real"__coeff_90',
'NTC__fft_coefficient__attr_"real"__coeff_92',
'NTC__fft_coefficient__attr_"real"__coeff_94',
'NTC__fft_coefficient__attr_"imag"__coeff_1',
'NTC__fft_coefficient__attr_"imag"__coeff_3',
'NTC__fft_coefficient__attr_"imag"__coeff_4',
'NTC__fft_coefficient__attr_"imag"__coeff_5',
'NTC__fft_coefficient__attr_"imag"__coeff_6',
'NTC__fft_coefficient__attr_"imag"__coeff_7',
'NTC__fft_coefficient__attr_"imag"__coeff_8',
'NTC__fft_coefficient__attr_"imag"__coeff_9',
'NTC__fft_coefficient__attr_"imag"__coeff_10',
'NTC__fft_coefficient__attr_"imag"__coeff_11',
'NTC__fft_coefficient__attr_"imag"__coeff_15',
'NTC__fft_coefficient__attr_"imag"__coeff_17',
'NTC__fft_coefficient__attr_"imag"__coeff_18',
'NTC__fft_coefficient__attr_"imag"__coeff_19',
'NTC__fft_coefficient__attr_"imag"__coeff_20',
'NTC__fft_coefficient__attr_"imag"__coeff_22',
'NTC__fft_coefficient__attr_"imag"__coeff_23',
'NTC__fft_coefficient__attr_"imag"__coeff_24',
'NTC__fft_coefficient__attr_"imag"__coeff_25',
'NTC__fft_coefficient__attr_"imag"__coeff_26',
'NTC__fft_coefficient__attr_"imag"__coeff_27',
'NTC__fft_coefficient__attr_"imag"__coeff_28',
'NTC__fft_coefficient__attr_"imag"__coeff_29',
'NTC__fft_coefficient__attr_"imag"__coeff_32',
'NTC__fft_coefficient__attr_"imag"__coeff_33',
'NTC__fft_coefficient__attr_"imag"__coeff_34',
'NTC__fft_coefficient__attr_"imag"__coeff_35',
'NTC__fft_coefficient__attr_"imag"__coeff_36',
'NTC__fft_coefficient__attr_"imag"__coeff_37',
'NTC__fft_coefficient__attr_"imag"__coeff_38',
'NTC__fft_coefficient__attr_"imag"__coeff_39',
'NTC__fft_coefficient__attr_"imag"__coeff_40',
'NTC__fft_coefficient__attr_"imag"__coeff_41',
'NTC__fft_coefficient__attr_"imag"__coeff_42',
'NTC__fft_coefficient__attr_"imag"__coeff_43',
'NTC__fft_coefficient__attr_"imag"__coeff_45',
'NTC__fft_coefficient__attr_"imag"__coeff_47',
'NTC__fft_coefficient__attr_"imag"__coeff_48',
'NTC__fft_coefficient__attr_"imag"__coeff_51',
'NTC__fft_coefficient__attr_"imag"__coeff_53',
'NTC__fft_coefficient__attr_"imag"__coeff_54',
'NTC__fft_coefficient__attr_"imag"__coeff_57',
'NTC__fft_coefficient__attr_"imag"__coeff_58',
'NTC__fft_coefficient__attr_"imag"__coeff_59',
'NTC__fft_coefficient__attr_"imag"__coeff_61',
'NTC__fft_coefficient__attr_"imag"__coeff_63',
'NTC__fft_coefficient__attr_"imag"__coeff_66',
'NTC__fft_coefficient__attr_"imag"__coeff_67',
'NTC__fft_coefficient__attr_"imag"__coeff_68',
'NTC__fft_coefficient__attr_"imag"__coeff_75',
'NTC__fft_coefficient__attr_"imag"__coeff_77',
'NTC__fft_coefficient__attr_"imag"__coeff_78',
'NTC__fft_coefficient__attr_"imag"__coeff_83',
'NTC__fft_coefficient__attr_"imag"__coeff_84',
'NTC__fft_coefficient__attr_"imag"__coeff_85',
'NTC__fft_coefficient__attr_"imag"__coeff_89',
'NTC__fft_coefficient__attr_"imag"__coeff_90',
'NTC__fft_coefficient__attr_"imag"__coeff_91',
'NTC__fft_coefficient__attr_"imag"__coeff_93',
'NTC__fft_coefficient__attr_"imag"__coeff_94',
'NTC__fft_coefficient__attr_"imag"__coeff_96',
'NTC__fft_coefficient__attr_"imag"__coeff_97',
'NTC__fft_coefficient__attr_"abs"__coeff_3',
'NTC__fft_coefficient__attr_"abs"__coeff_4',
'NTC__fft_coefficient__attr_"abs"__coeff_6',
'NTC__fft_coefficient__attr_"abs"__coeff_7',
'NTC__fft_coefficient__attr_"abs"__coeff_8',
'NTC__fft_coefficient__attr_"abs"__coeff_13',
'NTC__fft_coefficient__attr_"abs"__coeff_14',
'NTC__fft_coefficient__attr_"abs"__coeff_17',
'NTC__fft_coefficient__attr_"abs"__coeff_18',
'NTC__fft_coefficient__attr_"abs"__coeff_21',
'NTC__fft_coefficient__attr_"abs"__coeff_23',
'NTC__fft_coefficient__attr_"abs"__coeff_25',
'NTC__fft_coefficient__attr_"abs"__coeff_29',
'NTC__fft_coefficient__attr_"abs"__coeff_32',
'NTC__fft_coefficient__attr_"abs"__coeff_33',
'NTC__fft_coefficient__attr_"abs"__coeff_34',
'NTC__fft_coefficient__attr_"abs"__coeff_35',
'NTC__fft_coefficient__attr_"abs"__coeff_36',
'NTC__fft_coefficient__attr_"abs"__coeff_37',
'NTC__fft_coefficient__attr_"abs"__coeff_39',
'NTC__fft_coefficient__attr_"abs"__coeff_41',
'NTC__fft_coefficient__attr_"abs"__coeff_42',
'NTC__fft_coefficient__attr_"abs"__coeff_44',
'NTC__fft_coefficient__attr_"abs"__coeff_47',
'NTC__fft_coefficient__attr_"abs"__coeff_48',
'NTC__fft_coefficient__attr_"abs"__coeff_49',
'NTC__fft_coefficient__attr_"abs"__coeff_51',
'NTC__fft_coefficient__attr_"abs"__coeff_54',
'NTC__fft_coefficient__attr_"abs"__coeff_56',
'NTC__fft_coefficient__attr_"abs"__coeff_57',
'NTC__fft_coefficient__attr_"abs"__coeff_59',
'NTC__fft_coefficient__attr_"abs"__coeff_61',
'NTC__fft_coefficient__attr_"abs"__coeff_67',
'NTC__fft_coefficient__attr_"abs"__coeff_69',
'NTC__fft_coefficient__attr_"abs"__coeff_70',
'NTC__fft_coefficient__attr_"abs"__coeff_73',
'NTC__fft_coefficient__attr_"abs"__coeff_77',
'NTC__fft_coefficient__attr_"abs"__coeff_78',
'NTC__fft_coefficient__attr_"abs"__coeff_80',
'NTC__fft_coefficient__attr_"abs"__coeff_81',
'NTC__fft_coefficient__attr_"abs"__coeff_86',
'NTC__fft_coefficient__attr_"abs"__coeff_87',
'NTC__fft_coefficient__attr_"abs"__coeff_88',
'NTC__fft_coefficient__attr_"abs"__coeff_90',
'NTC__fft_coefficient__attr_"abs"__coeff_91',
'NTC__fft_coefficient__attr_"abs"__coeff_97',
'NTC__fft_coefficient__attr_"abs"__coeff_98',
'NTC__fft_coefficient__attr_"angle"__coeff_1',
'NTC__fft_coefficient__attr_"angle"__coeff_3',
'NTC__fft_coefficient__attr_"angle"__coeff_4',
'NTC__fft_coefficient__attr_"angle"__coeff_7',
'NTC__fft_coefficient__attr_"angle"__coeff_8',
'NTC__fft_coefficient__attr_"angle"__coeff_9',
'NTC__fft_coefficient__attr_"angle"__coeff_10',
'NTC__fft_coefficient__attr_"angle"__coeff_12',
'NTC__fft_coefficient__attr_"angle"__coeff_13',
'NTC__fft_coefficient__attr_"angle"__coeff_14',
'NTC__fft_coefficient__attr_"angle"__coeff_15',
'NTC__fft_coefficient__attr_"angle"__coeff_17',
'NTC__fft_coefficient__attr_"angle"__coeff_19',
'NTC__fft_coefficient__attr_"angle"__coeff_20',
'NTC__fft_coefficient__attr_"angle"__coeff_21',
'NTC__fft_coefficient__attr_"angle"__coeff_22',
'NTC__fft_coefficient__attr_"angle"__coeff_23',
'NTC__fft_coefficient__attr_"angle"__coeff_24',
'NTC__fft_coefficient__attr_"angle"__coeff_25',
'NTC__fft_coefficient__attr_"angle"__coeff_27',
'NTC__fft_coefficient__attr_"angle"__coeff_31',
'NTC__fft_coefficient__attr_"angle"__coeff_33',
'NTC__fft_coefficient__attr_"angle"__coeff_34',
'NTC__fft_coefficient__attr_"angle"__coeff_35',
'NTC__fft_coefficient__attr_"angle"__coeff_38',
'NTC__fft_coefficient__attr_"angle"__coeff_39',
'NTC__fft_coefficient__attr_"angle"__coeff_40',
'NTC__fft_coefficient__attr_"angle"__coeff_41',
'NTC__fft_coefficient__attr_"angle"__coeff_42',
'NTC__fft_coefficient__attr_"angle"__coeff_43',
'NTC__fft_coefficient__attr_"angle"__coeff_44',
'NTC__fft_coefficient__attr_"angle"__coeff_45',
'NTC__fft_coefficient__attr_"angle"__coeff_46',
'NTC__fft_coefficient__attr_"angle"__coeff_47',
'NTC__fft_coefficient__attr_"angle"__coeff_48',
'NTC__fft_coefficient__attr_"angle"__coeff_49',
'NTC__fft_coefficient__attr_"angle"__coeff_50',
'NTC__fft_coefficient__attr_"angle"__coeff_51',
'NTC__fft_coefficient__attr_"angle"__coeff_52',
'NTC__fft_coefficient__attr_"angle"__coeff_53',
'NTC__fft_coefficient__attr_"angle"__coeff_54',
'NTC__fft_coefficient__attr_"angle"__coeff_56',
'NTC__fft_coefficient__attr_"angle"__coeff_58',
'NTC__fft_coefficient__attr_"angle"__coeff_59',
'NTC__fft_coefficient__attr_"angle"__coeff_60',
'NTC__fft_coefficient__attr_"angle"__coeff_61',
'NTC__fft_coefficient__attr_"angle"__coeff_63',
'NTC__fft_coefficient__attr_"angle"__coeff_64',
'NTC__fft_coefficient__attr_"angle"__coeff_65',
'NTC__fft_coefficient__attr_"angle"__coeff_66',
'NTC__fft_coefficient__attr_"angle"__coeff_67',
'NTC__fft_coefficient__attr_"angle"__coeff_68',
'NTC__fft_coefficient__attr_"angle"__coeff_69',
'NTC__fft_coefficient__attr_"angle"__coeff_70',
'NTC__fft_coefficient__attr_"angle"__coeff_71',
'NTC__fft_coefficient__attr_"angle"__coeff_72',
'NTC__fft_coefficient__attr_"angle"__coeff_75',
'NTC__fft_coefficient__attr_"angle"__coeff_76',
'NTC__fft_coefficient__attr_"angle"__coeff_77',
'NTC__fft_coefficient__attr_"angle"__coeff_79',
'NTC__fft_coefficient__attr_"angle"__coeff_81',
'NTC__fft_coefficient__attr_"angle"__coeff_82',
'NTC__fft_coefficient__attr_"angle"__coeff_83',
'NTC__fft_coefficient__attr_"angle"__coeff_84',
'NTC__fft_coefficient__attr_"angle"__coeff_85',
'NTC__fft_coefficient__attr_"angle"__coeff_86',
'NTC__fft_coefficient__attr_"angle"__coeff_87',
'NTC__fft_coefficient__attr_"angle"__coeff_88',
'NTC__fft_coefficient__attr_"angle"__coeff_89',
'NTC__fft_coefficient__attr_"angle"__coeff_90',
'NTC__fft_coefficient__attr_"angle"__coeff_91',
'NTC__fft_coefficient__attr_"angle"__coeff_93',
'NTC__fft_coefficient__attr_"angle"__coeff_94',
'NTC__fft_coefficient__attr_"angle"__coeff_95',
'NTC__fft_coefficient__attr_"angle"__coeff_96',
'NTC__fft_coefficient__attr_"angle"__coeff_97',
'NTC__fft_coefficient__attr_"angle"__coeff_98',
'NTC__fft_coefficient__attr_"angle"__coeff_99',
'NTC__max_langevin_fixed_point__m_3__r_30',
'NTC__linear_trend__attr_"intercept"',
'NTC__linear_trend__attr_"slope"',
'NTC__agg_linear_trend__attr_"rvalue"__chunk_len_5__f_agg_"min"',
'NTC__agg_linear_trend__attr_"rvalue"__chunk_len_10__f_agg_"min"',
'NTC__agg_linear_trend__attr_"rvalue"__chunk_len_10__f_agg_"mean"',
'NTC__agg_linear_trend__attr_"rvalue"__chunk_len_50__f_agg_"mean"',
'NTC__agg_linear_trend__attr_"intercept"__chunk_len_5__f_agg_"max"',
'NTC__agg_linear_trend__attr_"intercept"__chunk_len_5__f_agg_"min"',
'NTC__agg_linear_trend__attr_"intercept"__chunk_len_5__f_agg_"mean"',
'NTC__agg_linear_trend__attr_"intercept"__chunk_len_10__f_agg_"max"',
'NTC__agg_linear_trend__attr_"intercept"__chunk_len_10__f_agg_"min"',
'NTC__agg_linear_trend__attr_"intercept"__chunk_len_10__f_agg_"mean"',
'NTC__agg_linear_trend__attr_"intercept"__chunk_len_50__f_agg_"max"',
'NTC__agg_linear_trend__attr_"intercept"__chunk_len_50__f_agg_"min"',
'NTC__agg_linear_trend__attr_"intercept"__chunk_len_50__f_agg_"mean"',
'NTC__agg_linear_trend__attr_"slope"__chunk_len_5__f_agg_"mean"',
'NTC__agg_linear_trend__attr_"slope"__chunk_len_10__f_agg_"max"',
'NTC__agg_linear_trend__attr_"slope"__chunk_len_50__f_agg_"mean"',
'NTC__agg_linear_trend__attr_"stderr"__chunk_len_50__f_agg_"max"',
'NTC__energy_ratio_by_chunks__num_segments_10__segment_focus_7',
'NTC__mean_n_absolute_max__number_of_maxima_7',
'BAND_ARR_2__sum_values',
'BAND_ARR_2__variation_coefficient',
'BAND_ARR_2__skewness',
'BAND_ARR_2__longest_strike_above_mean',
'BAND_ARR_2__count_below_mean',
'BAND_ARR_2__last_location_of_minimum',
'BAND_ARR_2__first_location_of_minimum',
'BAND_ARR_2__c3__lag_1',
'BAND_ARR_2__c3__lag_2',
'BAND_ARR_2__c3__lag_3',
'BAND_ARR_2__cid_ce__normalize_False',
'BAND_ARR_2__large_standard_deviation__r_0.15000000000000002',
'BAND_ARR_2__autocorrelation__lag_6',
'BAND_ARR_2__number_peaks__n_5',
'BAND_ARR_2__binned_entropy__max_bins_10',
'BAND_ARR_2__cwt_coefficients__coeff_6__w_10__widths_(2, 5, 10, 20)',
'BAND_ARR_2__cwt_coefficients__coeff_10__w_10__widths_(2, 5, 10, 20)',
'BAND_ARR_2__cwt_coefficients__coeff_12__w_10__widths_(2, 5, 10, 20)',
'BAND_ARR_2__cwt_coefficients__coeff_13__w_10__widths_(2, 5, 10, 20)',
'BAND_ARR_2__spkt_welch_density__coeff_2',
'BAND_ARR_2__spkt_welch_density__coeff_5',
'BAND_ARR_2__change_quantiles__f_agg_"mean"__isabs_False__qh_0.2__ql_0.0',
'BAND_ARR_2__change_quantiles__f_agg_"var"__isabs_False__qh_0.4__ql_0.0',
'BAND_ARR_2__change_quantiles__f_agg_"var"__isabs_False__qh_0.6__ql_0.0',
'BAND_ARR_2__change_quantiles__f_agg_"var"__isabs_False__qh_1.0__ql_0.6',
'BAND_ARR_2__change_quantiles__f_agg_"var"__isabs_False__qh_1.0__ql_0.8',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_0',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_1',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_2',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_3',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_4',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_5',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_6',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_7',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_9',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_10',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_12',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_15',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_16',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_17',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_19',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_25',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_28',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_31',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_32',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_39',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_43',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_44',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_48',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_56',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_59',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_60',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_61',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_68',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_76',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_88',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_1',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_2',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_3',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_5',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_7',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_8',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_12',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_13',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_14',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_17',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_20',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_25',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_26',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_30',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_31',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_34',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_39',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_40',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_60',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_65',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_96',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_0',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_1',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_2',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_3',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_6',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_7',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_10',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_12',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_19',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_20',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_22',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_23',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_24',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_26',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_27',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_28',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_29',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_30',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_31',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_34',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_36',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_37',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_39',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_40',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_42',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_45',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_46',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_47',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_62',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_68',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_69',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_73',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_74',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_82',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_85',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_90',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_1',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_2',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_3',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_4',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_6',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_7',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_8',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_9',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_10',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_11',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_12',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_14',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_15',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_16',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_17',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_18',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_19',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_20',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_21',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_22',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_23',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_24',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_25',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_27',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_28',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_31',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_32',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_33',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_34',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_35',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_36',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_37',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_38',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_39',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_40',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_41',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_42',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_43',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_44',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_45',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_46',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_47',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_48',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_49',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_50',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_51',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_52',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_53',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_54',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_55',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_59',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_60',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_61',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_62',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_64',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_65',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_66',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_69',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_70',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_71',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_72',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_73',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_74',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_75',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_77',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_78',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_81',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_82',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_83',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_84',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_85',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_86',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_87',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_88',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_89',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_90',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_91',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_92',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_94',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_96',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_98',
'BAND_ARR_2__fft_aggregated__aggtype_"skew"',
'BAND_ARR_2__range_count__max_1__min_-1',
'BAND_ARR_2__range_count__max_1000000000000.0__min_0',
'BAND_ARR_2__friedrich_coefficients__coeff_0__m_3__r_30',
'BAND_ARR_2__friedrich_coefficients__coeff_1__m_3__r_30',
'BAND_ARR_2__linear_trend__attr_"rvalue"',
'BAND_ARR_2__agg_linear_trend__attr_"rvalue"__chunk_len_5__f_agg_"max"',
'BAND_ARR_2__agg_linear_trend__attr_"rvalue"__chunk_len_5__f_agg_"min"',
'BAND_ARR_2__agg_linear_trend__attr_"rvalue"__chunk_len_10__f_agg_"min"',
'BAND_ARR_2__agg_linear_trend__attr_"rvalue"__chunk_len_50__f_agg_"mean"',
'BAND_ARR_2__agg_linear_trend__attr_"intercept"__chunk_len_5__f_agg_"min"',
'BAND_ARR_2__agg_linear_trend__attr_"intercept"__chunk_len_10__f_agg_"max"',
'BAND_ARR_2__agg_linear_trend__attr_"intercept"__chunk_len_10__f_agg_"min"',
'BAND_ARR_2__agg_linear_trend__attr_"intercept"__chunk_len_50__f_agg_"min"',
'BAND_ARR_2__agg_linear_trend__attr_"slope"__chunk_len_5__f_agg_"mean"',
'BAND_ARR_2__agg_linear_trend__attr_"stderr"__chunk_len_5__f_agg_"min"',
'BAND_ARR_2__energy_ratio_by_chunks__num_segments_10__segment_focus_5',
'BAND_ARR_2__energy_ratio_by_chunks__num_segments_10__segment_focus_8',
'BAND_ARR_2__ratio_beyond_r_sigma__r_5',
'BAND_ARR_2__ratio_beyond_r_sigma__r_7',
'BAND_ARR_2__matrix_profile__feature_"75"__threshold_0.98',
'BAND_ARR_2__mean_n_absolute_max__number_of_maxima_7',
'BAND_ARR_8__sum_values',
'BAND_ARR_8__median',
'BAND_ARR_8__skewness',
'BAND_ARR_8__absolute_sum_of_changes',
'BAND_ARR_8__longest_strike_below_mean',
'BAND_ARR_8__longest_strike_above_mean',
'BAND_ARR_8__count_above_mean',
'BAND_ARR_8__count_below_mean',
'BAND_ARR_8__minimum',
'BAND_ARR_8__c3__lag_1',
'BAND_ARR_8__c3__lag_2',
'BAND_ARR_8__c3__lag_3',
'BAND_ARR_8__cid_ce__normalize_True',
'BAND_ARR_8__quantile__q_0.1',
'BAND_ARR_8__quantile__q_0.2',
'BAND_ARR_8__quantile__q_0.3',
'BAND_ARR_8__quantile__q_0.4',
'BAND_ARR_8__quantile__q_0.6',
'BAND_ARR_8__quantile__q_0.7',
'BAND_ARR_8__quantile__q_0.8',
'BAND_ARR_8__number_peaks__n_1',
'BAND_ARR_8__number_peaks__n_5',
'BAND_ARR_8__number_peaks__n_50',
'BAND_ARR_8__binned_entropy__max_bins_10',
'BAND_ARR_8__index_mass_quantile__q_0.7',
'BAND_ARR_8__cwt_coefficients__coeff_6__w_5__widths_(2, 5, 10, 20)',
'BAND_ARR_8__spkt_welch_density__coeff_2',
'BAND_ARR_8__spkt_welch_density__coeff_5',
'BAND_ARR_8__change_quantiles__f_agg_"var"__isabs_False__qh_0.2__ql_0.0',
'BAND_ARR_8__change_quantiles__f_agg_"var"__isabs_False__qh_0.4__ql_0.0',
'BAND_ARR_8__change_quantiles__f_agg_"mean"__isabs_True__qh_0.4__ql_0.0',
'BAND_ARR_8__change_quantiles__f_agg_"var"__isabs_False__qh_0.6__ql_0.0',
'BAND_ARR_8__change_quantiles__f_agg_"var"__isabs_False__qh_0.4__ql_0.2',
'BAND_ARR_8__change_quantiles__f_agg_"mean"__isabs_True__qh_0.4__ql_0.2',
'BAND_ARR_8__change_quantiles__f_agg_"var"__isabs_True__qh_0.4__ql_0.2',
'BAND_ARR_8__change_quantiles__f_agg_"var"__isabs_False__qh_0.6__ql_0.2',
'BAND_ARR_8__change_quantiles__f_agg_"mean"__isabs_True__qh_0.6__ql_0.2',
'BAND_ARR_8__change_quantiles__f_agg_"mean"__isabs_True__qh_0.6__ql_0.4',
'BAND_ARR_8__change_quantiles__f_agg_"var"__isabs_True__qh_0.6__ql_0.4',
'BAND_ARR_8__change_quantiles__f_agg_"var"__isabs_False__qh_1.0__ql_0.4',
'BAND_ARR_8__change_quantiles__f_agg_"var"__isabs_False__qh_0.8__ql_0.6',
'BAND_ARR_8__change_quantiles__f_agg_"mean"__isabs_True__qh_0.8__ql_0.6',
'BAND_ARR_8__change_quantiles__f_agg_"var"__isabs_True__qh_0.8__ql_0.6',
'BAND_ARR_8__change_quantiles__f_agg_"mean"__isabs_True__qh_1.0__ql_0.8',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_0',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_1',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_2',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_3',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_4',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_5',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_6',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_7',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_8',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_9',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_14',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_15',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_16',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_17',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_19',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_20',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_23',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_24',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_25',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_27',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_29',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_39',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_43',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_48',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_52',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_69',
'BAND_ARR_8__fft_coefficient__attr_"imag"__coeff_1',
'BAND_ARR_8__fft_coefficient__attr_"imag"__coeff_2',
'BAND_ARR_8__fft_coefficient__attr_"imag"__coeff_3',
'BAND_ARR_8__fft_coefficient__attr_"imag"__coeff_5',
'BAND_ARR_8__fft_coefficient__attr_"imag"__coeff_6',
'BAND_ARR_8__fft_coefficient__attr_"imag"__coeff_7',
'BAND_ARR_8__fft_coefficient__attr_"imag"__coeff_8',
'BAND_ARR_8__fft_coefficient__attr_"imag"__coeff_10',
'BAND_ARR_8__fft_coefficient__attr_"imag"__coeff_11',
'BAND_ARR_8__fft_coefficient__attr_"imag"__coeff_12',
'BAND_ARR_8__fft_coefficient__attr_"imag"__coeff_14',
'BAND_ARR_8__fft_coefficient__attr_"imag"__coeff_19',
'BAND_ARR_8__fft_coefficient__attr_"imag"__coeff_20',
'BAND_ARR_8__fft_coefficient__attr_"imag"__coeff_23',
'BAND_ARR_8__fft_coefficient__attr_"imag"__coeff_25',
'BAND_ARR_8__fft_coefficient__attr_"imag"__coeff_26',
'BAND_ARR_8__fft_coefficient__attr_"imag"__coeff_27',
'BAND_ARR_8__fft_coefficient__attr_"imag"__coeff_28',
'BAND_ARR_8__fft_coefficient__attr_"imag"__coeff_31',
'BAND_ARR_8__fft_coefficient__attr_"imag"__coeff_32',
'BAND_ARR_8__fft_coefficient__attr_"imag"__coeff_37',
'BAND_ARR_8__fft_coefficient__attr_"abs"__coeff_0',
'BAND_ARR_8__fft_coefficient__attr_"abs"__coeff_1',
'BAND_ARR_8__fft_coefficient__attr_"abs"__coeff_2',
'BAND_ARR_8__fft_coefficient__attr_"abs"__coeff_3',
'BAND_ARR_8__fft_coefficient__attr_"abs"__coeff_4',
'BAND_ARR_8__fft_coefficient__attr_"abs"__coeff_5',
'BAND_ARR_8__fft_coefficient__attr_"abs"__coeff_6',
'BAND_ARR_8__fft_coefficient__attr_"abs"__coeff_10',
'BAND_ARR_8__fft_coefficient__attr_"abs"__coeff_13',
'BAND_ARR_8__fft_coefficient__attr_"abs"__coeff_14',
'BAND_ARR_8__fft_coefficient__attr_"abs"__coeff_15',
'BAND_ARR_8__fft_coefficient__attr_"abs"__coeff_19',
'BAND_ARR_8__fft_coefficient__attr_"abs"__coeff_21',
'BAND_ARR_8__fft_coefficient__attr_"abs"__coeff_22',
'BAND_ARR_8__fft_coefficient__attr_"abs"__coeff_23',
'BAND_ARR_8__fft_coefficient__attr_"abs"__coeff_26',
'BAND_ARR_8__fft_coefficient__attr_"abs"__coeff_28',
'BAND_ARR_8__fft_coefficient__attr_"abs"__coeff_29',
'BAND_ARR_8__fft_coefficient__attr_"abs"__coeff_30',
'BAND_ARR_8__fft_coefficient__attr_"abs"__coeff_37',
'BAND_ARR_8__fft_coefficient__attr_"abs"__coeff_83',
'BAND_ARR_8__fft_coefficient__attr_"abs"__coeff_94',
'BAND_ARR_8__fft_coefficient__attr_"abs"__coeff_98',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_1',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_2',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_3',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_4',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_6',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_7',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_8',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_10',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_11',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_14',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_15',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_16',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_17',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_19',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_21',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_22',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_23',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_27',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_29',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_30',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_31',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_32',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_34',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_35',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_36',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_37',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_38',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_39',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_40',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_41',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_42',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_43',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_44',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_46',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_47',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_48',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_49',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_50',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_52',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_53',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_54',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_55',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_56',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_57',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_58',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_62',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_64',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_65',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_66',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_67',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_69',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_70',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_71',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_72',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_74',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_75',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_78',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_79',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_80',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_81',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_83',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_84',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_86',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_87',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_88',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_89',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_90',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_92',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_93',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_94',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_95',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_96',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_97',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_98',
'BAND_ARR_8__range_count__max_1__min_-1',
'BAND_ARR_8__friedrich_coefficients__coeff_0__m_3__r_30',
'BAND_ARR_8__friedrich_coefficients__coeff_1__m_3__r_30',
'BAND_ARR_8__max_langevin_fixed_point__m_3__r_30',
'BAND_ARR_8__agg_linear_trend__attr_"rvalue"__chunk_len_5__f_agg_"mean"',
'BAND_ARR_8__agg_linear_trend__attr_"rvalue"__chunk_len_10__f_agg_"max"',
'BAND_ARR_8__agg_linear_trend__attr_"intercept"__chunk_len_5__f_agg_"max"',
'BAND_ARR_8__agg_linear_trend__attr_"intercept"__chunk_len_50__f_agg_"mean"',
'BAND_ARR_8__agg_linear_trend__attr_"slope"__chunk_len_10__f_agg_"max"',
'BAND_ARR_8__agg_linear_trend__attr_"slope"__chunk_len_50__f_agg_"min"',
'BAND_ARR_8__agg_linear_trend__attr_"stderr"__chunk_len_5__f_agg_"var"',
'BAND_ARR_8__agg_linear_trend__attr_"stderr"__chunk_len_10__f_agg_"min"',
'BAND_ARR_8__augmented_dickey_fuller__attr_"teststat"__autolag_"AIC"',
'BAND_ARR_8__energy_ratio_by_chunks__num_segments_10__segment_focus_1',
'BAND_ARR_8__energy_ratio_by_chunks__num_segments_10__segment_focus_5',
'BAND_ARR_8__ratio_beyond_r_sigma__r_1',
'VALUE'

]]


In [187]:
df_validation_at_least_1 = df_validation[['INTERVAL_IN_FILE',
'SN',
'ACCL_X',
'ACCL_Y',
'BAND_ARR_1',
'BAND_ARR_2',
'BAND_ARR_3',
'BAND_ARR_4',
'BAND_ARR_5',
'BAND_ARR_6',
'BAND_ARR_7',
'BAND_ARR_8',
'BAND_ARR_9',
'BAND_ARR_10',
'BAND_ARR_11',
'BAND_ARR_12',
'BAND_ARR_13',
'BAND_ARR_14',
'BAND_ARR_15',
'BAND_ARR_16',
'BAND_ARR_17',
'BAND_ARR_18',
'BAND_ARR_19',
'BAND_ARR_20',
'BAND_ARR_21',
'BAND_ARR_22',
'BAND_ARR_23',
'BAND_ARR_24',
'BAND_ARR_25',
'BAND_ARR_26',
'BAND_ARR_27',
'BAND_ARR_28',
'BAND_ARR_29',
'BAND_ARR_30',
'BAND_ARR_31',
'BAND_ARR_32',
'BATTERY',
'BIT_FLAG',
'MAX_VALUE',
'MIC_TD_RAW',
'MIN_VALUE',
'NTC',
'VAA',
'ADVERTISE_TS',
'FIRST_PACKET_TS',
'RSSI',
'NTC__mean_change',
'NTC__median',
'NTC__mean',
'NTC__standard_deviation',
'NTC__root_mean_square',
'NTC__count_above_mean',
'NTC__count_below_mean',
'NTC__maximum',
'NTC__absolute_maximum',
'NTC__minimum',
'NTC__c3__lag_3',
'NTC__cid_ce__normalize_False',
'NTC__quantile__q_0.1',
'NTC__quantile__q_0.2',
'NTC__quantile__q_0.3',
'NTC__quantile__q_0.4',
'NTC__quantile__q_0.6',
'NTC__quantile__q_0.7',
'NTC__quantile__q_0.8',
'NTC__quantile__q_0.9',
'NTC__number_cwt_peaks__n_1',
'NTC__number_cwt_peaks__n_5',
'NTC__number_peaks__n_1',
'NTC__cwt_coefficients__coeff_0__w_2__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_1__w_2__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_1__w_5__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_1__w_10__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_1__w_20__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_2__w_2__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_2__w_5__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_2__w_10__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_2__w_20__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_3__w_2__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_3__w_5__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_3__w_10__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_3__w_20__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_4__w_2__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_4__w_5__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_4__w_10__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_4__w_20__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_5__w_2__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_5__w_5__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_5__w_10__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_5__w_20__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_6__w_2__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_6__w_5__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_6__w_10__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_6__w_20__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_7__w_5__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_7__w_10__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_7__w_20__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_8__w_5__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_8__w_10__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_8__w_20__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_9__w_5__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_9__w_10__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_9__w_20__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_10__w_5__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_10__w_10__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_10__w_20__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_11__w_5__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_11__w_10__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_11__w_20__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_12__w_5__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_12__w_10__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_12__w_20__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_13__w_5__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_13__w_10__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_13__w_20__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_14__w_5__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_14__w_10__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_14__w_20__widths_(2, 5, 10, 20)',
'NTC__ar_coefficient__coeff_0__k_10',
'NTC__change_quantiles__f_agg_"var"__isabs_False__qh_0.4__ql_0.2',
'NTC__fft_coefficient__attr_"real"__coeff_1',
'NTC__fft_coefficient__attr_"real"__coeff_2',
'NTC__fft_coefficient__attr_"real"__coeff_3',
'NTC__fft_coefficient__attr_"real"__coeff_4',
'NTC__fft_coefficient__attr_"real"__coeff_9',
'NTC__fft_coefficient__attr_"real"__coeff_10',
'NTC__fft_coefficient__attr_"real"__coeff_13',
'NTC__fft_coefficient__attr_"real"__coeff_15',
'NTC__fft_coefficient__attr_"real"__coeff_18',
'NTC__fft_coefficient__attr_"real"__coeff_21',
'NTC__fft_coefficient__attr_"real"__coeff_22',
'NTC__fft_coefficient__attr_"real"__coeff_23',
'NTC__fft_coefficient__attr_"real"__coeff_24',
'NTC__fft_coefficient__attr_"real"__coeff_27',
'NTC__fft_coefficient__attr_"real"__coeff_28',
'NTC__fft_coefficient__attr_"real"__coeff_30',
'NTC__fft_coefficient__attr_"real"__coeff_31',
'NTC__fft_coefficient__attr_"real"__coeff_32',
'NTC__fft_coefficient__attr_"real"__coeff_38',
'NTC__fft_coefficient__attr_"real"__coeff_40',
'NTC__fft_coefficient__attr_"real"__coeff_42',
'NTC__fft_coefficient__attr_"real"__coeff_43',
'NTC__fft_coefficient__attr_"real"__coeff_45',
'NTC__fft_coefficient__attr_"real"__coeff_46',
'NTC__fft_coefficient__attr_"real"__coeff_50',
'NTC__fft_coefficient__attr_"real"__coeff_52',
'NTC__fft_coefficient__attr_"real"__coeff_55',
'NTC__fft_coefficient__attr_"real"__coeff_57',
'NTC__fft_coefficient__attr_"real"__coeff_59',
'NTC__fft_coefficient__attr_"real"__coeff_64',
'NTC__fft_coefficient__attr_"real"__coeff_65',
'NTC__fft_coefficient__attr_"real"__coeff_66',
'NTC__fft_coefficient__attr_"real"__coeff_67',
'NTC__fft_coefficient__attr_"real"__coeff_68',
'NTC__fft_coefficient__attr_"real"__coeff_69',
'NTC__fft_coefficient__attr_"real"__coeff_70',
'NTC__fft_coefficient__attr_"real"__coeff_71',
'NTC__fft_coefficient__attr_"real"__coeff_72',
'NTC__fft_coefficient__attr_"real"__coeff_74',
'NTC__fft_coefficient__attr_"real"__coeff_75',
'NTC__fft_coefficient__attr_"real"__coeff_76',
'NTC__fft_coefficient__attr_"real"__coeff_77',
'NTC__fft_coefficient__attr_"real"__coeff_78',
'NTC__fft_coefficient__attr_"real"__coeff_81',
'NTC__fft_coefficient__attr_"real"__coeff_83',
'NTC__fft_coefficient__attr_"real"__coeff_86',
'NTC__fft_coefficient__attr_"real"__coeff_87',
'NTC__fft_coefficient__attr_"real"__coeff_90',
'NTC__fft_coefficient__attr_"real"__coeff_92',
'NTC__fft_coefficient__attr_"real"__coeff_94',
'NTC__fft_coefficient__attr_"imag"__coeff_1',
'NTC__fft_coefficient__attr_"imag"__coeff_3',
'NTC__fft_coefficient__attr_"imag"__coeff_4',
'NTC__fft_coefficient__attr_"imag"__coeff_5',
'NTC__fft_coefficient__attr_"imag"__coeff_6',
'NTC__fft_coefficient__attr_"imag"__coeff_7',
'NTC__fft_coefficient__attr_"imag"__coeff_8',
'NTC__fft_coefficient__attr_"imag"__coeff_9',
'NTC__fft_coefficient__attr_"imag"__coeff_10',
'NTC__fft_coefficient__attr_"imag"__coeff_11',
'NTC__fft_coefficient__attr_"imag"__coeff_15',
'NTC__fft_coefficient__attr_"imag"__coeff_17',
'NTC__fft_coefficient__attr_"imag"__coeff_18',
'NTC__fft_coefficient__attr_"imag"__coeff_19',
'NTC__fft_coefficient__attr_"imag"__coeff_20',
'NTC__fft_coefficient__attr_"imag"__coeff_22',
'NTC__fft_coefficient__attr_"imag"__coeff_23',
'NTC__fft_coefficient__attr_"imag"__coeff_24',
'NTC__fft_coefficient__attr_"imag"__coeff_25',
'NTC__fft_coefficient__attr_"imag"__coeff_26',
'NTC__fft_coefficient__attr_"imag"__coeff_27',
'NTC__fft_coefficient__attr_"imag"__coeff_28',
'NTC__fft_coefficient__attr_"imag"__coeff_29',
'NTC__fft_coefficient__attr_"imag"__coeff_32',
'NTC__fft_coefficient__attr_"imag"__coeff_33',
'NTC__fft_coefficient__attr_"imag"__coeff_34',
'NTC__fft_coefficient__attr_"imag"__coeff_35',
'NTC__fft_coefficient__attr_"imag"__coeff_36',
'NTC__fft_coefficient__attr_"imag"__coeff_37',
'NTC__fft_coefficient__attr_"imag"__coeff_38',
'NTC__fft_coefficient__attr_"imag"__coeff_39',
'NTC__fft_coefficient__attr_"imag"__coeff_40',
'NTC__fft_coefficient__attr_"imag"__coeff_41',
'NTC__fft_coefficient__attr_"imag"__coeff_42',
'NTC__fft_coefficient__attr_"imag"__coeff_43',
'NTC__fft_coefficient__attr_"imag"__coeff_45',
'NTC__fft_coefficient__attr_"imag"__coeff_47',
'NTC__fft_coefficient__attr_"imag"__coeff_48',
'NTC__fft_coefficient__attr_"imag"__coeff_51',
'NTC__fft_coefficient__attr_"imag"__coeff_53',
'NTC__fft_coefficient__attr_"imag"__coeff_54',
'NTC__fft_coefficient__attr_"imag"__coeff_57',
'NTC__fft_coefficient__attr_"imag"__coeff_58',
'NTC__fft_coefficient__attr_"imag"__coeff_59',
'NTC__fft_coefficient__attr_"imag"__coeff_61',
'NTC__fft_coefficient__attr_"imag"__coeff_63',
'NTC__fft_coefficient__attr_"imag"__coeff_66',
'NTC__fft_coefficient__attr_"imag"__coeff_67',
'NTC__fft_coefficient__attr_"imag"__coeff_68',
'NTC__fft_coefficient__attr_"imag"__coeff_75',
'NTC__fft_coefficient__attr_"imag"__coeff_77',
'NTC__fft_coefficient__attr_"imag"__coeff_78',
'NTC__fft_coefficient__attr_"imag"__coeff_83',
'NTC__fft_coefficient__attr_"imag"__coeff_84',
'NTC__fft_coefficient__attr_"imag"__coeff_85',
'NTC__fft_coefficient__attr_"imag"__coeff_89',
'NTC__fft_coefficient__attr_"imag"__coeff_90',
'NTC__fft_coefficient__attr_"imag"__coeff_91',
'NTC__fft_coefficient__attr_"imag"__coeff_93',
'NTC__fft_coefficient__attr_"imag"__coeff_94',
'NTC__fft_coefficient__attr_"imag"__coeff_96',
'NTC__fft_coefficient__attr_"imag"__coeff_97',
'NTC__fft_coefficient__attr_"abs"__coeff_3',
'NTC__fft_coefficient__attr_"abs"__coeff_4',
'NTC__fft_coefficient__attr_"abs"__coeff_6',
'NTC__fft_coefficient__attr_"abs"__coeff_7',
'NTC__fft_coefficient__attr_"abs"__coeff_8',
'NTC__fft_coefficient__attr_"abs"__coeff_13',
'NTC__fft_coefficient__attr_"abs"__coeff_14',
'NTC__fft_coefficient__attr_"abs"__coeff_17',
'NTC__fft_coefficient__attr_"abs"__coeff_18',
'NTC__fft_coefficient__attr_"abs"__coeff_21',
'NTC__fft_coefficient__attr_"abs"__coeff_23',
'NTC__fft_coefficient__attr_"abs"__coeff_25',
'NTC__fft_coefficient__attr_"abs"__coeff_29',
'NTC__fft_coefficient__attr_"abs"__coeff_32',
'NTC__fft_coefficient__attr_"abs"__coeff_33',
'NTC__fft_coefficient__attr_"abs"__coeff_34',
'NTC__fft_coefficient__attr_"abs"__coeff_35',
'NTC__fft_coefficient__attr_"abs"__coeff_36',
'NTC__fft_coefficient__attr_"abs"__coeff_37',
'NTC__fft_coefficient__attr_"abs"__coeff_39',
'NTC__fft_coefficient__attr_"abs"__coeff_41',
'NTC__fft_coefficient__attr_"abs"__coeff_42',
'NTC__fft_coefficient__attr_"abs"__coeff_44',
'NTC__fft_coefficient__attr_"abs"__coeff_47',
'NTC__fft_coefficient__attr_"abs"__coeff_48',
'NTC__fft_coefficient__attr_"abs"__coeff_49',
'NTC__fft_coefficient__attr_"abs"__coeff_51',
'NTC__fft_coefficient__attr_"abs"__coeff_54',
'NTC__fft_coefficient__attr_"abs"__coeff_56',
'NTC__fft_coefficient__attr_"abs"__coeff_57',
'NTC__fft_coefficient__attr_"abs"__coeff_59',
'NTC__fft_coefficient__attr_"abs"__coeff_61',
'NTC__fft_coefficient__attr_"abs"__coeff_67',
'NTC__fft_coefficient__attr_"abs"__coeff_69',
'NTC__fft_coefficient__attr_"abs"__coeff_70',
'NTC__fft_coefficient__attr_"abs"__coeff_73',
'NTC__fft_coefficient__attr_"abs"__coeff_77',
'NTC__fft_coefficient__attr_"abs"__coeff_78',
'NTC__fft_coefficient__attr_"abs"__coeff_80',
'NTC__fft_coefficient__attr_"abs"__coeff_81',
'NTC__fft_coefficient__attr_"abs"__coeff_86',
'NTC__fft_coefficient__attr_"abs"__coeff_87',
'NTC__fft_coefficient__attr_"abs"__coeff_88',
'NTC__fft_coefficient__attr_"abs"__coeff_90',
'NTC__fft_coefficient__attr_"abs"__coeff_91',
'NTC__fft_coefficient__attr_"abs"__coeff_97',
'NTC__fft_coefficient__attr_"abs"__coeff_98',
'NTC__fft_coefficient__attr_"angle"__coeff_1',
'NTC__fft_coefficient__attr_"angle"__coeff_3',
'NTC__fft_coefficient__attr_"angle"__coeff_4',
'NTC__fft_coefficient__attr_"angle"__coeff_7',
'NTC__fft_coefficient__attr_"angle"__coeff_8',
'NTC__fft_coefficient__attr_"angle"__coeff_9',
'NTC__fft_coefficient__attr_"angle"__coeff_10',
'NTC__fft_coefficient__attr_"angle"__coeff_12',
'NTC__fft_coefficient__attr_"angle"__coeff_13',
'NTC__fft_coefficient__attr_"angle"__coeff_14',
'NTC__fft_coefficient__attr_"angle"__coeff_15',
'NTC__fft_coefficient__attr_"angle"__coeff_17',
'NTC__fft_coefficient__attr_"angle"__coeff_19',
'NTC__fft_coefficient__attr_"angle"__coeff_20',
'NTC__fft_coefficient__attr_"angle"__coeff_21',
'NTC__fft_coefficient__attr_"angle"__coeff_22',
'NTC__fft_coefficient__attr_"angle"__coeff_23',
'NTC__fft_coefficient__attr_"angle"__coeff_24',
'NTC__fft_coefficient__attr_"angle"__coeff_25',
'NTC__fft_coefficient__attr_"angle"__coeff_27',
'NTC__fft_coefficient__attr_"angle"__coeff_31',
'NTC__fft_coefficient__attr_"angle"__coeff_33',
'NTC__fft_coefficient__attr_"angle"__coeff_34',
'NTC__fft_coefficient__attr_"angle"__coeff_35',
'NTC__fft_coefficient__attr_"angle"__coeff_38',
'NTC__fft_coefficient__attr_"angle"__coeff_39',
'NTC__fft_coefficient__attr_"angle"__coeff_40',
'NTC__fft_coefficient__attr_"angle"__coeff_41',
'NTC__fft_coefficient__attr_"angle"__coeff_42',
'NTC__fft_coefficient__attr_"angle"__coeff_43',
'NTC__fft_coefficient__attr_"angle"__coeff_44',
'NTC__fft_coefficient__attr_"angle"__coeff_45',
'NTC__fft_coefficient__attr_"angle"__coeff_46',
'NTC__fft_coefficient__attr_"angle"__coeff_47',
'NTC__fft_coefficient__attr_"angle"__coeff_48',
'NTC__fft_coefficient__attr_"angle"__coeff_49',
'NTC__fft_coefficient__attr_"angle"__coeff_50',
'NTC__fft_coefficient__attr_"angle"__coeff_51',
'NTC__fft_coefficient__attr_"angle"__coeff_52',
'NTC__fft_coefficient__attr_"angle"__coeff_53',
'NTC__fft_coefficient__attr_"angle"__coeff_54',
'NTC__fft_coefficient__attr_"angle"__coeff_56',
'NTC__fft_coefficient__attr_"angle"__coeff_58',
'NTC__fft_coefficient__attr_"angle"__coeff_59',
'NTC__fft_coefficient__attr_"angle"__coeff_60',
'NTC__fft_coefficient__attr_"angle"__coeff_61',
'NTC__fft_coefficient__attr_"angle"__coeff_63',
'NTC__fft_coefficient__attr_"angle"__coeff_64',
'NTC__fft_coefficient__attr_"angle"__coeff_65',
'NTC__fft_coefficient__attr_"angle"__coeff_66',
'NTC__fft_coefficient__attr_"angle"__coeff_67',
'NTC__fft_coefficient__attr_"angle"__coeff_68',
'NTC__fft_coefficient__attr_"angle"__coeff_69',
'NTC__fft_coefficient__attr_"angle"__coeff_70',
'NTC__fft_coefficient__attr_"angle"__coeff_71',
'NTC__fft_coefficient__attr_"angle"__coeff_72',
'NTC__fft_coefficient__attr_"angle"__coeff_75',
'NTC__fft_coefficient__attr_"angle"__coeff_76',
'NTC__fft_coefficient__attr_"angle"__coeff_77',
'NTC__fft_coefficient__attr_"angle"__coeff_79',
'NTC__fft_coefficient__attr_"angle"__coeff_81',
'NTC__fft_coefficient__attr_"angle"__coeff_82',
'NTC__fft_coefficient__attr_"angle"__coeff_83',
'NTC__fft_coefficient__attr_"angle"__coeff_84',
'NTC__fft_coefficient__attr_"angle"__coeff_85',
'NTC__fft_coefficient__attr_"angle"__coeff_86',
'NTC__fft_coefficient__attr_"angle"__coeff_87',
'NTC__fft_coefficient__attr_"angle"__coeff_88',
'NTC__fft_coefficient__attr_"angle"__coeff_89',
'NTC__fft_coefficient__attr_"angle"__coeff_90',
'NTC__fft_coefficient__attr_"angle"__coeff_91',
'NTC__fft_coefficient__attr_"angle"__coeff_93',
'NTC__fft_coefficient__attr_"angle"__coeff_94',
'NTC__fft_coefficient__attr_"angle"__coeff_95',
'NTC__fft_coefficient__attr_"angle"__coeff_96',
'NTC__fft_coefficient__attr_"angle"__coeff_97',
'NTC__fft_coefficient__attr_"angle"__coeff_98',
'NTC__fft_coefficient__attr_"angle"__coeff_99',
'NTC__max_langevin_fixed_point__m_3__r_30',
'NTC__linear_trend__attr_"intercept"',
'NTC__linear_trend__attr_"slope"',
'NTC__agg_linear_trend__attr_"rvalue"__chunk_len_5__f_agg_"min"',
'NTC__agg_linear_trend__attr_"rvalue"__chunk_len_10__f_agg_"min"',
'NTC__agg_linear_trend__attr_"rvalue"__chunk_len_10__f_agg_"mean"',
'NTC__agg_linear_trend__attr_"rvalue"__chunk_len_50__f_agg_"mean"',
'NTC__agg_linear_trend__attr_"intercept"__chunk_len_5__f_agg_"max"',
'NTC__agg_linear_trend__attr_"intercept"__chunk_len_5__f_agg_"min"',
'NTC__agg_linear_trend__attr_"intercept"__chunk_len_5__f_agg_"mean"',
'NTC__agg_linear_trend__attr_"intercept"__chunk_len_10__f_agg_"max"',
'NTC__agg_linear_trend__attr_"intercept"__chunk_len_10__f_agg_"min"',
'NTC__agg_linear_trend__attr_"intercept"__chunk_len_10__f_agg_"mean"',
'NTC__agg_linear_trend__attr_"intercept"__chunk_len_50__f_agg_"max"',
'NTC__agg_linear_trend__attr_"intercept"__chunk_len_50__f_agg_"min"',
'NTC__agg_linear_trend__attr_"intercept"__chunk_len_50__f_agg_"mean"',
'NTC__agg_linear_trend__attr_"slope"__chunk_len_5__f_agg_"mean"',
'NTC__agg_linear_trend__attr_"slope"__chunk_len_10__f_agg_"max"',
'NTC__agg_linear_trend__attr_"slope"__chunk_len_50__f_agg_"mean"',
'NTC__agg_linear_trend__attr_"stderr"__chunk_len_50__f_agg_"max"',
'NTC__energy_ratio_by_chunks__num_segments_10__segment_focus_7',
'NTC__mean_n_absolute_max__number_of_maxima_7',
'BAND_ARR_2__sum_values',
'BAND_ARR_2__variation_coefficient',
'BAND_ARR_2__skewness',
'BAND_ARR_2__longest_strike_above_mean',
'BAND_ARR_2__count_below_mean',
'BAND_ARR_2__last_location_of_minimum',
'BAND_ARR_2__first_location_of_minimum',
'BAND_ARR_2__c3__lag_1',
'BAND_ARR_2__c3__lag_2',
'BAND_ARR_2__c3__lag_3',
'BAND_ARR_2__cid_ce__normalize_False',
'BAND_ARR_2__large_standard_deviation__r_0.15000000000000002',
'BAND_ARR_2__autocorrelation__lag_6',
'BAND_ARR_2__number_peaks__n_5',
'BAND_ARR_2__binned_entropy__max_bins_10',
'BAND_ARR_2__cwt_coefficients__coeff_6__w_10__widths_(2, 5, 10, 20)',
'BAND_ARR_2__cwt_coefficients__coeff_10__w_10__widths_(2, 5, 10, 20)',
'BAND_ARR_2__cwt_coefficients__coeff_12__w_10__widths_(2, 5, 10, 20)',
'BAND_ARR_2__cwt_coefficients__coeff_13__w_10__widths_(2, 5, 10, 20)',
'BAND_ARR_2__spkt_welch_density__coeff_2',
'BAND_ARR_2__spkt_welch_density__coeff_5',
'BAND_ARR_2__change_quantiles__f_agg_"mean"__isabs_False__qh_0.2__ql_0.0',
'BAND_ARR_2__change_quantiles__f_agg_"var"__isabs_False__qh_0.4__ql_0.0',
'BAND_ARR_2__change_quantiles__f_agg_"var"__isabs_False__qh_0.6__ql_0.0',
'BAND_ARR_2__change_quantiles__f_agg_"var"__isabs_False__qh_1.0__ql_0.6',
'BAND_ARR_2__change_quantiles__f_agg_"var"__isabs_False__qh_1.0__ql_0.8',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_0',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_1',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_2',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_3',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_4',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_5',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_6',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_7',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_9',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_10',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_12',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_15',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_16',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_17',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_19',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_25',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_28',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_31',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_32',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_39',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_43',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_44',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_48',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_56',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_59',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_60',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_61',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_68',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_76',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_88',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_1',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_2',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_3',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_5',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_7',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_8',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_12',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_13',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_14',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_17',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_20',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_25',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_26',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_30',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_31',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_34',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_39',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_40',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_60',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_65',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_96',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_0',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_1',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_2',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_3',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_6',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_7',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_10',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_12',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_19',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_20',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_22',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_23',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_24',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_26',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_27',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_28',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_29',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_30',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_31',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_34',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_36',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_37',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_39',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_40',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_42',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_45',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_46',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_47',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_62',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_68',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_69',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_73',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_74',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_82',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_85',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_90',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_1',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_2',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_3',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_4',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_6',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_7',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_8',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_9',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_10',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_11',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_12',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_14',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_15',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_16',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_17',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_18',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_19',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_20',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_21',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_22',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_23',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_24',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_25',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_27',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_28',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_31',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_32',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_33',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_34',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_35',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_36',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_37',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_38',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_39',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_40',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_41',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_42',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_43',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_44',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_45',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_46',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_47',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_48',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_49',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_50',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_51',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_52',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_53',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_54',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_55',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_59',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_60',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_61',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_62',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_64',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_65',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_66',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_69',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_70',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_71',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_72',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_73',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_74',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_75',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_77',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_78',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_81',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_82',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_83',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_84',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_85',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_86',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_87',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_88',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_89',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_90',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_91',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_92',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_94',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_96',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_98',
'BAND_ARR_2__fft_aggregated__aggtype_"skew"',
'BAND_ARR_2__range_count__max_1__min_-1',
'BAND_ARR_2__range_count__max_1000000000000.0__min_0',
'BAND_ARR_2__friedrich_coefficients__coeff_0__m_3__r_30',
'BAND_ARR_2__friedrich_coefficients__coeff_1__m_3__r_30',
'BAND_ARR_2__linear_trend__attr_"rvalue"',
'BAND_ARR_2__agg_linear_trend__attr_"rvalue"__chunk_len_5__f_agg_"max"',
'BAND_ARR_2__agg_linear_trend__attr_"rvalue"__chunk_len_5__f_agg_"min"',
'BAND_ARR_2__agg_linear_trend__attr_"rvalue"__chunk_len_10__f_agg_"min"',
'BAND_ARR_2__agg_linear_trend__attr_"rvalue"__chunk_len_50__f_agg_"mean"',
'BAND_ARR_2__agg_linear_trend__attr_"intercept"__chunk_len_5__f_agg_"min"',
'BAND_ARR_2__agg_linear_trend__attr_"intercept"__chunk_len_10__f_agg_"max"',
'BAND_ARR_2__agg_linear_trend__attr_"intercept"__chunk_len_10__f_agg_"min"',
'BAND_ARR_2__agg_linear_trend__attr_"intercept"__chunk_len_50__f_agg_"min"',
'BAND_ARR_2__agg_linear_trend__attr_"slope"__chunk_len_5__f_agg_"mean"',
'BAND_ARR_2__agg_linear_trend__attr_"stderr"__chunk_len_5__f_agg_"min"',
'BAND_ARR_2__energy_ratio_by_chunks__num_segments_10__segment_focus_5',
'BAND_ARR_2__energy_ratio_by_chunks__num_segments_10__segment_focus_8',
'BAND_ARR_2__ratio_beyond_r_sigma__r_5',
'BAND_ARR_2__ratio_beyond_r_sigma__r_7',
'BAND_ARR_2__matrix_profile__feature_"75"__threshold_0.98',
'BAND_ARR_2__mean_n_absolute_max__number_of_maxima_7',
'BAND_ARR_8__sum_values',
'BAND_ARR_8__median',
'BAND_ARR_8__skewness',
'BAND_ARR_8__absolute_sum_of_changes',
'BAND_ARR_8__longest_strike_below_mean',
'BAND_ARR_8__longest_strike_above_mean',
'BAND_ARR_8__count_above_mean',
'BAND_ARR_8__count_below_mean',
'BAND_ARR_8__minimum',
'BAND_ARR_8__c3__lag_1',
'BAND_ARR_8__c3__lag_2',
'BAND_ARR_8__c3__lag_3',
'BAND_ARR_8__cid_ce__normalize_True',
'BAND_ARR_8__quantile__q_0.1',
'BAND_ARR_8__quantile__q_0.2',
'BAND_ARR_8__quantile__q_0.3',
'BAND_ARR_8__quantile__q_0.4',
'BAND_ARR_8__quantile__q_0.6',
'BAND_ARR_8__quantile__q_0.7',
'BAND_ARR_8__quantile__q_0.8',
'BAND_ARR_8__number_peaks__n_1',
'BAND_ARR_8__number_peaks__n_5',
'BAND_ARR_8__number_peaks__n_50',
'BAND_ARR_8__binned_entropy__max_bins_10',
'BAND_ARR_8__index_mass_quantile__q_0.7',
'BAND_ARR_8__cwt_coefficients__coeff_6__w_5__widths_(2, 5, 10, 20)',
'BAND_ARR_8__spkt_welch_density__coeff_2',
'BAND_ARR_8__spkt_welch_density__coeff_5',
'BAND_ARR_8__change_quantiles__f_agg_"var"__isabs_False__qh_0.2__ql_0.0',
'BAND_ARR_8__change_quantiles__f_agg_"var"__isabs_False__qh_0.4__ql_0.0',
'BAND_ARR_8__change_quantiles__f_agg_"mean"__isabs_True__qh_0.4__ql_0.0',
'BAND_ARR_8__change_quantiles__f_agg_"var"__isabs_False__qh_0.6__ql_0.0',
'BAND_ARR_8__change_quantiles__f_agg_"var"__isabs_False__qh_0.4__ql_0.2',
'BAND_ARR_8__change_quantiles__f_agg_"mean"__isabs_True__qh_0.4__ql_0.2',
'BAND_ARR_8__change_quantiles__f_agg_"var"__isabs_True__qh_0.4__ql_0.2',
'BAND_ARR_8__change_quantiles__f_agg_"var"__isabs_False__qh_0.6__ql_0.2',
'BAND_ARR_8__change_quantiles__f_agg_"mean"__isabs_True__qh_0.6__ql_0.2',
'BAND_ARR_8__change_quantiles__f_agg_"mean"__isabs_True__qh_0.6__ql_0.4',
'BAND_ARR_8__change_quantiles__f_agg_"var"__isabs_True__qh_0.6__ql_0.4',
'BAND_ARR_8__change_quantiles__f_agg_"var"__isabs_False__qh_1.0__ql_0.4',
'BAND_ARR_8__change_quantiles__f_agg_"var"__isabs_False__qh_0.8__ql_0.6',
'BAND_ARR_8__change_quantiles__f_agg_"mean"__isabs_True__qh_0.8__ql_0.6',
'BAND_ARR_8__change_quantiles__f_agg_"var"__isabs_True__qh_0.8__ql_0.6',
'BAND_ARR_8__change_quantiles__f_agg_"mean"__isabs_True__qh_1.0__ql_0.8',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_0',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_1',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_2',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_3',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_4',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_5',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_6',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_7',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_8',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_9',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_14',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_15',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_16',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_17',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_19',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_20',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_23',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_24',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_25',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_27',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_29',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_39',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_43',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_48',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_52',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_69',
'BAND_ARR_8__fft_coefficient__attr_"imag"__coeff_1',
'BAND_ARR_8__fft_coefficient__attr_"imag"__coeff_2',
'BAND_ARR_8__fft_coefficient__attr_"imag"__coeff_3',
'BAND_ARR_8__fft_coefficient__attr_"imag"__coeff_5',
'BAND_ARR_8__fft_coefficient__attr_"imag"__coeff_6',
'BAND_ARR_8__fft_coefficient__attr_"imag"__coeff_7',
'BAND_ARR_8__fft_coefficient__attr_"imag"__coeff_8',
'BAND_ARR_8__fft_coefficient__attr_"imag"__coeff_10',
'BAND_ARR_8__fft_coefficient__attr_"imag"__coeff_11',
'BAND_ARR_8__fft_coefficient__attr_"imag"__coeff_12',
'BAND_ARR_8__fft_coefficient__attr_"imag"__coeff_14',
'BAND_ARR_8__fft_coefficient__attr_"imag"__coeff_19',
'BAND_ARR_8__fft_coefficient__attr_"imag"__coeff_20',
'BAND_ARR_8__fft_coefficient__attr_"imag"__coeff_23',
'BAND_ARR_8__fft_coefficient__attr_"imag"__coeff_25',
'BAND_ARR_8__fft_coefficient__attr_"imag"__coeff_26',
'BAND_ARR_8__fft_coefficient__attr_"imag"__coeff_27',
'BAND_ARR_8__fft_coefficient__attr_"imag"__coeff_28',
'BAND_ARR_8__fft_coefficient__attr_"imag"__coeff_31',
'BAND_ARR_8__fft_coefficient__attr_"imag"__coeff_32',
'BAND_ARR_8__fft_coefficient__attr_"imag"__coeff_37',
'BAND_ARR_8__fft_coefficient__attr_"abs"__coeff_0',
'BAND_ARR_8__fft_coefficient__attr_"abs"__coeff_1',
'BAND_ARR_8__fft_coefficient__attr_"abs"__coeff_2',
'BAND_ARR_8__fft_coefficient__attr_"abs"__coeff_3',
'BAND_ARR_8__fft_coefficient__attr_"abs"__coeff_4',
'BAND_ARR_8__fft_coefficient__attr_"abs"__coeff_5',
'BAND_ARR_8__fft_coefficient__attr_"abs"__coeff_6',
'BAND_ARR_8__fft_coefficient__attr_"abs"__coeff_10',
'BAND_ARR_8__fft_coefficient__attr_"abs"__coeff_13',
'BAND_ARR_8__fft_coefficient__attr_"abs"__coeff_14',
'BAND_ARR_8__fft_coefficient__attr_"abs"__coeff_15',
'BAND_ARR_8__fft_coefficient__attr_"abs"__coeff_19',
'BAND_ARR_8__fft_coefficient__attr_"abs"__coeff_21',
'BAND_ARR_8__fft_coefficient__attr_"abs"__coeff_22',
'BAND_ARR_8__fft_coefficient__attr_"abs"__coeff_23',
'BAND_ARR_8__fft_coefficient__attr_"abs"__coeff_26',
'BAND_ARR_8__fft_coefficient__attr_"abs"__coeff_28',
'BAND_ARR_8__fft_coefficient__attr_"abs"__coeff_29',
'BAND_ARR_8__fft_coefficient__attr_"abs"__coeff_30',
'BAND_ARR_8__fft_coefficient__attr_"abs"__coeff_37',
'BAND_ARR_8__fft_coefficient__attr_"abs"__coeff_83',
'BAND_ARR_8__fft_coefficient__attr_"abs"__coeff_94',
'BAND_ARR_8__fft_coefficient__attr_"abs"__coeff_98',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_1',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_2',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_3',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_4',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_6',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_7',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_8',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_10',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_11',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_14',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_15',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_16',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_17',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_19',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_21',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_22',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_23',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_27',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_29',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_30',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_31',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_32',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_34',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_35',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_36',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_37',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_38',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_39',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_40',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_41',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_42',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_43',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_44',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_46',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_47',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_48',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_49',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_50',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_52',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_53',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_54',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_55',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_56',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_57',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_58',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_62',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_64',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_65',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_66',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_67',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_69',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_70',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_71',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_72',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_74',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_75',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_78',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_79',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_80',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_81',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_83',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_84',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_86',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_87',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_88',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_89',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_90',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_92',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_93',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_94',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_95',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_96',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_97',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_98',
'BAND_ARR_8__range_count__max_1__min_-1',
'BAND_ARR_8__friedrich_coefficients__coeff_0__m_3__r_30',
'BAND_ARR_8__friedrich_coefficients__coeff_1__m_3__r_30',
'BAND_ARR_8__max_langevin_fixed_point__m_3__r_30',
'BAND_ARR_8__agg_linear_trend__attr_"rvalue"__chunk_len_5__f_agg_"mean"',
'BAND_ARR_8__agg_linear_trend__attr_"rvalue"__chunk_len_10__f_agg_"max"',
'BAND_ARR_8__agg_linear_trend__attr_"intercept"__chunk_len_5__f_agg_"max"',
'BAND_ARR_8__agg_linear_trend__attr_"intercept"__chunk_len_50__f_agg_"mean"',
'BAND_ARR_8__agg_linear_trend__attr_"slope"__chunk_len_10__f_agg_"max"',
'BAND_ARR_8__agg_linear_trend__attr_"slope"__chunk_len_50__f_agg_"min"',
'BAND_ARR_8__agg_linear_trend__attr_"stderr"__chunk_len_5__f_agg_"var"',
'BAND_ARR_8__agg_linear_trend__attr_"stderr"__chunk_len_10__f_agg_"min"',
'BAND_ARR_8__augmented_dickey_fuller__attr_"teststat"__autolag_"AIC"',
'BAND_ARR_8__energy_ratio_by_chunks__num_segments_10__segment_focus_1',
'BAND_ARR_8__energy_ratio_by_chunks__num_segments_10__segment_focus_5',
'BAND_ARR_8__ratio_beyond_r_sigma__r_1',
'VALUE'

]]


In [188]:
df_train_at_least_1 = df_train[['INTERVAL_IN_FILE',
'SN',
'ACCL_X',
'ACCL_Y',
'BAND_ARR_1',
'BAND_ARR_2',
'BAND_ARR_3',
'BAND_ARR_4',
'BAND_ARR_5',
'BAND_ARR_6',
'BAND_ARR_7',
'BAND_ARR_8',
'BAND_ARR_9',
'BAND_ARR_10',
'BAND_ARR_11',
'BAND_ARR_12',
'BAND_ARR_13',
'BAND_ARR_14',
'BAND_ARR_15',
'BAND_ARR_16',
'BAND_ARR_17',
'BAND_ARR_18',
'BAND_ARR_19',
'BAND_ARR_20',
'BAND_ARR_21',
'BAND_ARR_22',
'BAND_ARR_23',
'BAND_ARR_24',
'BAND_ARR_25',
'BAND_ARR_26',
'BAND_ARR_27',
'BAND_ARR_28',
'BAND_ARR_29',
'BAND_ARR_30',
'BAND_ARR_31',
'BAND_ARR_32',
'BATTERY',
'BIT_FLAG',
'MAX_VALUE',
'MIC_TD_RAW',
'MIN_VALUE',
'NTC',
'VAA',
'ADVERTISE_TS',
'FIRST_PACKET_TS',
'RSSI',
'NTC__mean_change',
'NTC__median',
'NTC__mean',
'NTC__standard_deviation',
'NTC__root_mean_square',
'NTC__count_above_mean',
'NTC__count_below_mean',
'NTC__maximum',
'NTC__absolute_maximum',
'NTC__minimum',
'NTC__c3__lag_3',
'NTC__cid_ce__normalize_False',
'NTC__quantile__q_0.1',
'NTC__quantile__q_0.2',
'NTC__quantile__q_0.3',
'NTC__quantile__q_0.4',
'NTC__quantile__q_0.6',
'NTC__quantile__q_0.7',
'NTC__quantile__q_0.8',
'NTC__quantile__q_0.9',
'NTC__number_cwt_peaks__n_1',
'NTC__number_cwt_peaks__n_5',
'NTC__number_peaks__n_1',
'NTC__cwt_coefficients__coeff_0__w_2__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_1__w_2__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_1__w_5__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_1__w_10__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_1__w_20__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_2__w_2__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_2__w_5__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_2__w_10__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_2__w_20__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_3__w_2__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_3__w_5__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_3__w_10__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_3__w_20__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_4__w_2__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_4__w_5__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_4__w_10__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_4__w_20__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_5__w_2__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_5__w_5__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_5__w_10__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_5__w_20__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_6__w_2__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_6__w_5__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_6__w_10__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_6__w_20__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_7__w_5__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_7__w_10__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_7__w_20__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_8__w_5__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_8__w_10__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_8__w_20__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_9__w_5__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_9__w_10__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_9__w_20__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_10__w_5__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_10__w_10__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_10__w_20__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_11__w_5__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_11__w_10__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_11__w_20__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_12__w_5__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_12__w_10__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_12__w_20__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_13__w_5__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_13__w_10__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_13__w_20__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_14__w_5__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_14__w_10__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_14__w_20__widths_(2, 5, 10, 20)',
'NTC__ar_coefficient__coeff_0__k_10',
'NTC__change_quantiles__f_agg_"var"__isabs_False__qh_0.4__ql_0.2',
'NTC__fft_coefficient__attr_"real"__coeff_1',
'NTC__fft_coefficient__attr_"real"__coeff_2',
'NTC__fft_coefficient__attr_"real"__coeff_3',
'NTC__fft_coefficient__attr_"real"__coeff_4',
'NTC__fft_coefficient__attr_"real"__coeff_9',
'NTC__fft_coefficient__attr_"real"__coeff_10',
'NTC__fft_coefficient__attr_"real"__coeff_13',
'NTC__fft_coefficient__attr_"real"__coeff_15',
'NTC__fft_coefficient__attr_"real"__coeff_18',
'NTC__fft_coefficient__attr_"real"__coeff_21',
'NTC__fft_coefficient__attr_"real"__coeff_22',
'NTC__fft_coefficient__attr_"real"__coeff_23',
'NTC__fft_coefficient__attr_"real"__coeff_24',
'NTC__fft_coefficient__attr_"real"__coeff_27',
'NTC__fft_coefficient__attr_"real"__coeff_28',
'NTC__fft_coefficient__attr_"real"__coeff_30',
'NTC__fft_coefficient__attr_"real"__coeff_31',
'NTC__fft_coefficient__attr_"real"__coeff_32',
'NTC__fft_coefficient__attr_"real"__coeff_38',
'NTC__fft_coefficient__attr_"real"__coeff_40',
'NTC__fft_coefficient__attr_"real"__coeff_42',
'NTC__fft_coefficient__attr_"real"__coeff_43',
'NTC__fft_coefficient__attr_"real"__coeff_45',
'NTC__fft_coefficient__attr_"real"__coeff_46',
'NTC__fft_coefficient__attr_"real"__coeff_50',
'NTC__fft_coefficient__attr_"real"__coeff_52',
'NTC__fft_coefficient__attr_"real"__coeff_55',
'NTC__fft_coefficient__attr_"real"__coeff_57',
'NTC__fft_coefficient__attr_"real"__coeff_59',
'NTC__fft_coefficient__attr_"real"__coeff_64',
'NTC__fft_coefficient__attr_"real"__coeff_65',
'NTC__fft_coefficient__attr_"real"__coeff_66',
'NTC__fft_coefficient__attr_"real"__coeff_67',
'NTC__fft_coefficient__attr_"real"__coeff_68',
'NTC__fft_coefficient__attr_"real"__coeff_69',
'NTC__fft_coefficient__attr_"real"__coeff_70',
'NTC__fft_coefficient__attr_"real"__coeff_71',
'NTC__fft_coefficient__attr_"real"__coeff_72',
'NTC__fft_coefficient__attr_"real"__coeff_74',
'NTC__fft_coefficient__attr_"real"__coeff_75',
'NTC__fft_coefficient__attr_"real"__coeff_76',
'NTC__fft_coefficient__attr_"real"__coeff_77',
'NTC__fft_coefficient__attr_"real"__coeff_78',
'NTC__fft_coefficient__attr_"real"__coeff_81',
'NTC__fft_coefficient__attr_"real"__coeff_83',
'NTC__fft_coefficient__attr_"real"__coeff_86',
'NTC__fft_coefficient__attr_"real"__coeff_87',
'NTC__fft_coefficient__attr_"real"__coeff_90',
'NTC__fft_coefficient__attr_"real"__coeff_92',
'NTC__fft_coefficient__attr_"real"__coeff_94',
'NTC__fft_coefficient__attr_"imag"__coeff_1',
'NTC__fft_coefficient__attr_"imag"__coeff_3',
'NTC__fft_coefficient__attr_"imag"__coeff_4',
'NTC__fft_coefficient__attr_"imag"__coeff_5',
'NTC__fft_coefficient__attr_"imag"__coeff_6',
'NTC__fft_coefficient__attr_"imag"__coeff_7',
'NTC__fft_coefficient__attr_"imag"__coeff_8',
'NTC__fft_coefficient__attr_"imag"__coeff_9',
'NTC__fft_coefficient__attr_"imag"__coeff_10',
'NTC__fft_coefficient__attr_"imag"__coeff_11',
'NTC__fft_coefficient__attr_"imag"__coeff_15',
'NTC__fft_coefficient__attr_"imag"__coeff_17',
'NTC__fft_coefficient__attr_"imag"__coeff_18',
'NTC__fft_coefficient__attr_"imag"__coeff_19',
'NTC__fft_coefficient__attr_"imag"__coeff_20',
'NTC__fft_coefficient__attr_"imag"__coeff_22',
'NTC__fft_coefficient__attr_"imag"__coeff_23',
'NTC__fft_coefficient__attr_"imag"__coeff_24',
'NTC__fft_coefficient__attr_"imag"__coeff_25',
'NTC__fft_coefficient__attr_"imag"__coeff_26',
'NTC__fft_coefficient__attr_"imag"__coeff_27',
'NTC__fft_coefficient__attr_"imag"__coeff_28',
'NTC__fft_coefficient__attr_"imag"__coeff_29',
'NTC__fft_coefficient__attr_"imag"__coeff_32',
'NTC__fft_coefficient__attr_"imag"__coeff_33',
'NTC__fft_coefficient__attr_"imag"__coeff_34',
'NTC__fft_coefficient__attr_"imag"__coeff_35',
'NTC__fft_coefficient__attr_"imag"__coeff_36',
'NTC__fft_coefficient__attr_"imag"__coeff_37',
'NTC__fft_coefficient__attr_"imag"__coeff_38',
'NTC__fft_coefficient__attr_"imag"__coeff_39',
'NTC__fft_coefficient__attr_"imag"__coeff_40',
'NTC__fft_coefficient__attr_"imag"__coeff_41',
'NTC__fft_coefficient__attr_"imag"__coeff_42',
'NTC__fft_coefficient__attr_"imag"__coeff_43',
'NTC__fft_coefficient__attr_"imag"__coeff_45',
'NTC__fft_coefficient__attr_"imag"__coeff_47',
'NTC__fft_coefficient__attr_"imag"__coeff_48',
'NTC__fft_coefficient__attr_"imag"__coeff_51',
'NTC__fft_coefficient__attr_"imag"__coeff_53',
'NTC__fft_coefficient__attr_"imag"__coeff_54',
'NTC__fft_coefficient__attr_"imag"__coeff_57',
'NTC__fft_coefficient__attr_"imag"__coeff_58',
'NTC__fft_coefficient__attr_"imag"__coeff_59',
'NTC__fft_coefficient__attr_"imag"__coeff_61',
'NTC__fft_coefficient__attr_"imag"__coeff_63',
'NTC__fft_coefficient__attr_"imag"__coeff_66',
'NTC__fft_coefficient__attr_"imag"__coeff_67',
'NTC__fft_coefficient__attr_"imag"__coeff_68',
'NTC__fft_coefficient__attr_"imag"__coeff_75',
'NTC__fft_coefficient__attr_"imag"__coeff_77',
'NTC__fft_coefficient__attr_"imag"__coeff_78',
'NTC__fft_coefficient__attr_"imag"__coeff_83',
'NTC__fft_coefficient__attr_"imag"__coeff_84',
'NTC__fft_coefficient__attr_"imag"__coeff_85',
'NTC__fft_coefficient__attr_"imag"__coeff_89',
'NTC__fft_coefficient__attr_"imag"__coeff_90',
'NTC__fft_coefficient__attr_"imag"__coeff_91',
'NTC__fft_coefficient__attr_"imag"__coeff_93',
'NTC__fft_coefficient__attr_"imag"__coeff_94',
'NTC__fft_coefficient__attr_"imag"__coeff_96',
'NTC__fft_coefficient__attr_"imag"__coeff_97',
'NTC__fft_coefficient__attr_"abs"__coeff_3',
'NTC__fft_coefficient__attr_"abs"__coeff_4',
'NTC__fft_coefficient__attr_"abs"__coeff_6',
'NTC__fft_coefficient__attr_"abs"__coeff_7',
'NTC__fft_coefficient__attr_"abs"__coeff_8',
'NTC__fft_coefficient__attr_"abs"__coeff_13',
'NTC__fft_coefficient__attr_"abs"__coeff_14',
'NTC__fft_coefficient__attr_"abs"__coeff_17',
'NTC__fft_coefficient__attr_"abs"__coeff_18',
'NTC__fft_coefficient__attr_"abs"__coeff_21',
'NTC__fft_coefficient__attr_"abs"__coeff_23',
'NTC__fft_coefficient__attr_"abs"__coeff_25',
'NTC__fft_coefficient__attr_"abs"__coeff_29',
'NTC__fft_coefficient__attr_"abs"__coeff_32',
'NTC__fft_coefficient__attr_"abs"__coeff_33',
'NTC__fft_coefficient__attr_"abs"__coeff_34',
'NTC__fft_coefficient__attr_"abs"__coeff_35',
'NTC__fft_coefficient__attr_"abs"__coeff_36',
'NTC__fft_coefficient__attr_"abs"__coeff_37',
'NTC__fft_coefficient__attr_"abs"__coeff_39',
'NTC__fft_coefficient__attr_"abs"__coeff_41',
'NTC__fft_coefficient__attr_"abs"__coeff_42',
'NTC__fft_coefficient__attr_"abs"__coeff_44',
'NTC__fft_coefficient__attr_"abs"__coeff_47',
'NTC__fft_coefficient__attr_"abs"__coeff_48',
'NTC__fft_coefficient__attr_"abs"__coeff_49',
'NTC__fft_coefficient__attr_"abs"__coeff_51',
'NTC__fft_coefficient__attr_"abs"__coeff_54',
'NTC__fft_coefficient__attr_"abs"__coeff_56',
'NTC__fft_coefficient__attr_"abs"__coeff_57',
'NTC__fft_coefficient__attr_"abs"__coeff_59',
'NTC__fft_coefficient__attr_"abs"__coeff_61',
'NTC__fft_coefficient__attr_"abs"__coeff_67',
'NTC__fft_coefficient__attr_"abs"__coeff_69',
'NTC__fft_coefficient__attr_"abs"__coeff_70',
'NTC__fft_coefficient__attr_"abs"__coeff_73',
'NTC__fft_coefficient__attr_"abs"__coeff_77',
'NTC__fft_coefficient__attr_"abs"__coeff_78',
'NTC__fft_coefficient__attr_"abs"__coeff_80',
'NTC__fft_coefficient__attr_"abs"__coeff_81',
'NTC__fft_coefficient__attr_"abs"__coeff_86',
'NTC__fft_coefficient__attr_"abs"__coeff_87',
'NTC__fft_coefficient__attr_"abs"__coeff_88',
'NTC__fft_coefficient__attr_"abs"__coeff_90',
'NTC__fft_coefficient__attr_"abs"__coeff_91',
'NTC__fft_coefficient__attr_"abs"__coeff_97',
'NTC__fft_coefficient__attr_"abs"__coeff_98',
'NTC__fft_coefficient__attr_"angle"__coeff_1',
'NTC__fft_coefficient__attr_"angle"__coeff_3',
'NTC__fft_coefficient__attr_"angle"__coeff_4',
'NTC__fft_coefficient__attr_"angle"__coeff_7',
'NTC__fft_coefficient__attr_"angle"__coeff_8',
'NTC__fft_coefficient__attr_"angle"__coeff_9',
'NTC__fft_coefficient__attr_"angle"__coeff_10',
'NTC__fft_coefficient__attr_"angle"__coeff_12',
'NTC__fft_coefficient__attr_"angle"__coeff_13',
'NTC__fft_coefficient__attr_"angle"__coeff_14',
'NTC__fft_coefficient__attr_"angle"__coeff_15',
'NTC__fft_coefficient__attr_"angle"__coeff_17',
'NTC__fft_coefficient__attr_"angle"__coeff_19',
'NTC__fft_coefficient__attr_"angle"__coeff_20',
'NTC__fft_coefficient__attr_"angle"__coeff_21',
'NTC__fft_coefficient__attr_"angle"__coeff_22',
'NTC__fft_coefficient__attr_"angle"__coeff_23',
'NTC__fft_coefficient__attr_"angle"__coeff_24',
'NTC__fft_coefficient__attr_"angle"__coeff_25',
'NTC__fft_coefficient__attr_"angle"__coeff_27',
'NTC__fft_coefficient__attr_"angle"__coeff_31',
'NTC__fft_coefficient__attr_"angle"__coeff_33',
'NTC__fft_coefficient__attr_"angle"__coeff_34',
'NTC__fft_coefficient__attr_"angle"__coeff_35',
'NTC__fft_coefficient__attr_"angle"__coeff_38',
'NTC__fft_coefficient__attr_"angle"__coeff_39',
'NTC__fft_coefficient__attr_"angle"__coeff_40',
'NTC__fft_coefficient__attr_"angle"__coeff_41',
'NTC__fft_coefficient__attr_"angle"__coeff_42',
'NTC__fft_coefficient__attr_"angle"__coeff_43',
'NTC__fft_coefficient__attr_"angle"__coeff_44',
'NTC__fft_coefficient__attr_"angle"__coeff_45',
'NTC__fft_coefficient__attr_"angle"__coeff_46',
'NTC__fft_coefficient__attr_"angle"__coeff_47',
'NTC__fft_coefficient__attr_"angle"__coeff_48',
'NTC__fft_coefficient__attr_"angle"__coeff_49',
'NTC__fft_coefficient__attr_"angle"__coeff_50',
'NTC__fft_coefficient__attr_"angle"__coeff_51',
'NTC__fft_coefficient__attr_"angle"__coeff_52',
'NTC__fft_coefficient__attr_"angle"__coeff_53',
'NTC__fft_coefficient__attr_"angle"__coeff_54',
'NTC__fft_coefficient__attr_"angle"__coeff_56',
'NTC__fft_coefficient__attr_"angle"__coeff_58',
'NTC__fft_coefficient__attr_"angle"__coeff_59',
'NTC__fft_coefficient__attr_"angle"__coeff_60',
'NTC__fft_coefficient__attr_"angle"__coeff_61',
'NTC__fft_coefficient__attr_"angle"__coeff_63',
'NTC__fft_coefficient__attr_"angle"__coeff_64',
'NTC__fft_coefficient__attr_"angle"__coeff_65',
'NTC__fft_coefficient__attr_"angle"__coeff_66',
'NTC__fft_coefficient__attr_"angle"__coeff_67',
'NTC__fft_coefficient__attr_"angle"__coeff_68',
'NTC__fft_coefficient__attr_"angle"__coeff_69',
'NTC__fft_coefficient__attr_"angle"__coeff_70',
'NTC__fft_coefficient__attr_"angle"__coeff_71',
'NTC__fft_coefficient__attr_"angle"__coeff_72',
'NTC__fft_coefficient__attr_"angle"__coeff_75',
'NTC__fft_coefficient__attr_"angle"__coeff_76',
'NTC__fft_coefficient__attr_"angle"__coeff_77',
'NTC__fft_coefficient__attr_"angle"__coeff_79',
'NTC__fft_coefficient__attr_"angle"__coeff_81',
'NTC__fft_coefficient__attr_"angle"__coeff_82',
'NTC__fft_coefficient__attr_"angle"__coeff_83',
'NTC__fft_coefficient__attr_"angle"__coeff_84',
'NTC__fft_coefficient__attr_"angle"__coeff_85',
'NTC__fft_coefficient__attr_"angle"__coeff_86',
'NTC__fft_coefficient__attr_"angle"__coeff_87',
'NTC__fft_coefficient__attr_"angle"__coeff_88',
'NTC__fft_coefficient__attr_"angle"__coeff_89',
'NTC__fft_coefficient__attr_"angle"__coeff_90',
'NTC__fft_coefficient__attr_"angle"__coeff_91',
'NTC__fft_coefficient__attr_"angle"__coeff_93',
'NTC__fft_coefficient__attr_"angle"__coeff_94',
'NTC__fft_coefficient__attr_"angle"__coeff_95',
'NTC__fft_coefficient__attr_"angle"__coeff_96',
'NTC__fft_coefficient__attr_"angle"__coeff_97',
'NTC__fft_coefficient__attr_"angle"__coeff_98',
'NTC__fft_coefficient__attr_"angle"__coeff_99',
'NTC__max_langevin_fixed_point__m_3__r_30',
'NTC__linear_trend__attr_"intercept"',
'NTC__linear_trend__attr_"slope"',
'NTC__agg_linear_trend__attr_"rvalue"__chunk_len_5__f_agg_"min"',
'NTC__agg_linear_trend__attr_"rvalue"__chunk_len_10__f_agg_"min"',
'NTC__agg_linear_trend__attr_"rvalue"__chunk_len_10__f_agg_"mean"',
'NTC__agg_linear_trend__attr_"rvalue"__chunk_len_50__f_agg_"mean"',
'NTC__agg_linear_trend__attr_"intercept"__chunk_len_5__f_agg_"max"',
'NTC__agg_linear_trend__attr_"intercept"__chunk_len_5__f_agg_"min"',
'NTC__agg_linear_trend__attr_"intercept"__chunk_len_5__f_agg_"mean"',
'NTC__agg_linear_trend__attr_"intercept"__chunk_len_10__f_agg_"max"',
'NTC__agg_linear_trend__attr_"intercept"__chunk_len_10__f_agg_"min"',
'NTC__agg_linear_trend__attr_"intercept"__chunk_len_10__f_agg_"mean"',
'NTC__agg_linear_trend__attr_"intercept"__chunk_len_50__f_agg_"max"',
'NTC__agg_linear_trend__attr_"intercept"__chunk_len_50__f_agg_"min"',
'NTC__agg_linear_trend__attr_"intercept"__chunk_len_50__f_agg_"mean"',
'NTC__agg_linear_trend__attr_"slope"__chunk_len_5__f_agg_"mean"',
'NTC__agg_linear_trend__attr_"slope"__chunk_len_10__f_agg_"max"',
'NTC__agg_linear_trend__attr_"slope"__chunk_len_50__f_agg_"mean"',
'NTC__agg_linear_trend__attr_"stderr"__chunk_len_50__f_agg_"max"',
'NTC__energy_ratio_by_chunks__num_segments_10__segment_focus_7',
'NTC__mean_n_absolute_max__number_of_maxima_7',
'BAND_ARR_2__sum_values',
'BAND_ARR_2__variation_coefficient',
'BAND_ARR_2__skewness',
'BAND_ARR_2__longest_strike_above_mean',
'BAND_ARR_2__count_below_mean',
'BAND_ARR_2__last_location_of_minimum',
'BAND_ARR_2__first_location_of_minimum',
'BAND_ARR_2__c3__lag_1',
'BAND_ARR_2__c3__lag_2',
'BAND_ARR_2__c3__lag_3',
'BAND_ARR_2__cid_ce__normalize_False',
'BAND_ARR_2__large_standard_deviation__r_0.15000000000000002',
'BAND_ARR_2__autocorrelation__lag_6',
'BAND_ARR_2__number_peaks__n_5',
'BAND_ARR_2__binned_entropy__max_bins_10',
'BAND_ARR_2__cwt_coefficients__coeff_6__w_10__widths_(2, 5, 10, 20)',
'BAND_ARR_2__cwt_coefficients__coeff_10__w_10__widths_(2, 5, 10, 20)',
'BAND_ARR_2__cwt_coefficients__coeff_12__w_10__widths_(2, 5, 10, 20)',
'BAND_ARR_2__cwt_coefficients__coeff_13__w_10__widths_(2, 5, 10, 20)',
'BAND_ARR_2__spkt_welch_density__coeff_2',
'BAND_ARR_2__spkt_welch_density__coeff_5',
'BAND_ARR_2__change_quantiles__f_agg_"mean"__isabs_False__qh_0.2__ql_0.0',
'BAND_ARR_2__change_quantiles__f_agg_"var"__isabs_False__qh_0.4__ql_0.0',
'BAND_ARR_2__change_quantiles__f_agg_"var"__isabs_False__qh_0.6__ql_0.0',
'BAND_ARR_2__change_quantiles__f_agg_"var"__isabs_False__qh_1.0__ql_0.6',
'BAND_ARR_2__change_quantiles__f_agg_"var"__isabs_False__qh_1.0__ql_0.8',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_0',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_1',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_2',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_3',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_4',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_5',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_6',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_7',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_9',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_10',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_12',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_15',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_16',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_17',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_19',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_25',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_28',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_31',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_32',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_39',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_43',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_44',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_48',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_56',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_59',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_60',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_61',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_68',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_76',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_88',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_1',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_2',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_3',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_5',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_7',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_8',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_12',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_13',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_14',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_17',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_20',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_25',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_26',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_30',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_31',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_34',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_39',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_40',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_60',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_65',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_96',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_0',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_1',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_2',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_3',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_6',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_7',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_10',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_12',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_19',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_20',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_22',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_23',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_24',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_26',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_27',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_28',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_29',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_30',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_31',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_34',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_36',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_37',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_39',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_40',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_42',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_45',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_46',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_47',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_62',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_68',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_69',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_73',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_74',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_82',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_85',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_90',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_1',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_2',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_3',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_4',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_6',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_7',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_8',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_9',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_10',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_11',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_12',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_14',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_15',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_16',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_17',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_18',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_19',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_20',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_21',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_22',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_23',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_24',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_25',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_27',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_28',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_31',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_32',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_33',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_34',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_35',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_36',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_37',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_38',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_39',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_40',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_41',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_42',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_43',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_44',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_45',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_46',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_47',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_48',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_49',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_50',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_51',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_52',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_53',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_54',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_55',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_59',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_60',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_61',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_62',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_64',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_65',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_66',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_69',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_70',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_71',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_72',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_73',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_74',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_75',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_77',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_78',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_81',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_82',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_83',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_84',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_85',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_86',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_87',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_88',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_89',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_90',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_91',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_92',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_94',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_96',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_98',
'BAND_ARR_2__fft_aggregated__aggtype_"skew"',
'BAND_ARR_2__range_count__max_1__min_-1',
'BAND_ARR_2__range_count__max_1000000000000.0__min_0',
'BAND_ARR_2__friedrich_coefficients__coeff_0__m_3__r_30',
'BAND_ARR_2__friedrich_coefficients__coeff_1__m_3__r_30',
'BAND_ARR_2__linear_trend__attr_"rvalue"',
'BAND_ARR_2__agg_linear_trend__attr_"rvalue"__chunk_len_5__f_agg_"max"',
'BAND_ARR_2__agg_linear_trend__attr_"rvalue"__chunk_len_5__f_agg_"min"',
'BAND_ARR_2__agg_linear_trend__attr_"rvalue"__chunk_len_10__f_agg_"min"',
'BAND_ARR_2__agg_linear_trend__attr_"rvalue"__chunk_len_50__f_agg_"mean"',
'BAND_ARR_2__agg_linear_trend__attr_"intercept"__chunk_len_5__f_agg_"min"',
'BAND_ARR_2__agg_linear_trend__attr_"intercept"__chunk_len_10__f_agg_"max"',
'BAND_ARR_2__agg_linear_trend__attr_"intercept"__chunk_len_10__f_agg_"min"',
'BAND_ARR_2__agg_linear_trend__attr_"intercept"__chunk_len_50__f_agg_"min"',
'BAND_ARR_2__agg_linear_trend__attr_"slope"__chunk_len_5__f_agg_"mean"',
'BAND_ARR_2__agg_linear_trend__attr_"stderr"__chunk_len_5__f_agg_"min"',
'BAND_ARR_2__energy_ratio_by_chunks__num_segments_10__segment_focus_5',
'BAND_ARR_2__energy_ratio_by_chunks__num_segments_10__segment_focus_8',
'BAND_ARR_2__ratio_beyond_r_sigma__r_5',
'BAND_ARR_2__ratio_beyond_r_sigma__r_7',
'BAND_ARR_2__matrix_profile__feature_"75"__threshold_0.98',
'BAND_ARR_2__mean_n_absolute_max__number_of_maxima_7',
'BAND_ARR_8__sum_values',
'BAND_ARR_8__median',
'BAND_ARR_8__skewness',
'BAND_ARR_8__absolute_sum_of_changes',
'BAND_ARR_8__longest_strike_below_mean',
'BAND_ARR_8__longest_strike_above_mean',
'BAND_ARR_8__count_above_mean',
'BAND_ARR_8__count_below_mean',
'BAND_ARR_8__minimum',
'BAND_ARR_8__c3__lag_1',
'BAND_ARR_8__c3__lag_2',
'BAND_ARR_8__c3__lag_3',
'BAND_ARR_8__cid_ce__normalize_True',
'BAND_ARR_8__quantile__q_0.1',
'BAND_ARR_8__quantile__q_0.2',
'BAND_ARR_8__quantile__q_0.3',
'BAND_ARR_8__quantile__q_0.4',
'BAND_ARR_8__quantile__q_0.6',
'BAND_ARR_8__quantile__q_0.7',
'BAND_ARR_8__quantile__q_0.8',
'BAND_ARR_8__number_peaks__n_1',
'BAND_ARR_8__number_peaks__n_5',
'BAND_ARR_8__number_peaks__n_50',
'BAND_ARR_8__binned_entropy__max_bins_10',
'BAND_ARR_8__index_mass_quantile__q_0.7',
'BAND_ARR_8__cwt_coefficients__coeff_6__w_5__widths_(2, 5, 10, 20)',
'BAND_ARR_8__spkt_welch_density__coeff_2',
'BAND_ARR_8__spkt_welch_density__coeff_5',
'BAND_ARR_8__change_quantiles__f_agg_"var"__isabs_False__qh_0.2__ql_0.0',
'BAND_ARR_8__change_quantiles__f_agg_"var"__isabs_False__qh_0.4__ql_0.0',
'BAND_ARR_8__change_quantiles__f_agg_"mean"__isabs_True__qh_0.4__ql_0.0',
'BAND_ARR_8__change_quantiles__f_agg_"var"__isabs_False__qh_0.6__ql_0.0',
'BAND_ARR_8__change_quantiles__f_agg_"var"__isabs_False__qh_0.4__ql_0.2',
'BAND_ARR_8__change_quantiles__f_agg_"mean"__isabs_True__qh_0.4__ql_0.2',
'BAND_ARR_8__change_quantiles__f_agg_"var"__isabs_True__qh_0.4__ql_0.2',
'BAND_ARR_8__change_quantiles__f_agg_"var"__isabs_False__qh_0.6__ql_0.2',
'BAND_ARR_8__change_quantiles__f_agg_"mean"__isabs_True__qh_0.6__ql_0.2',
'BAND_ARR_8__change_quantiles__f_agg_"mean"__isabs_True__qh_0.6__ql_0.4',
'BAND_ARR_8__change_quantiles__f_agg_"var"__isabs_True__qh_0.6__ql_0.4',
'BAND_ARR_8__change_quantiles__f_agg_"var"__isabs_False__qh_1.0__ql_0.4',
'BAND_ARR_8__change_quantiles__f_agg_"var"__isabs_False__qh_0.8__ql_0.6',
'BAND_ARR_8__change_quantiles__f_agg_"mean"__isabs_True__qh_0.8__ql_0.6',
'BAND_ARR_8__change_quantiles__f_agg_"var"__isabs_True__qh_0.8__ql_0.6',
'BAND_ARR_8__change_quantiles__f_agg_"mean"__isabs_True__qh_1.0__ql_0.8',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_0',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_1',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_2',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_3',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_4',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_5',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_6',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_7',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_8',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_9',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_14',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_15',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_16',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_17',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_19',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_20',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_23',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_24',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_25',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_27',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_29',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_39',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_43',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_48',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_52',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_69',
'BAND_ARR_8__fft_coefficient__attr_"imag"__coeff_1',
'BAND_ARR_8__fft_coefficient__attr_"imag"__coeff_2',
'BAND_ARR_8__fft_coefficient__attr_"imag"__coeff_3',
'BAND_ARR_8__fft_coefficient__attr_"imag"__coeff_5',
'BAND_ARR_8__fft_coefficient__attr_"imag"__coeff_6',
'BAND_ARR_8__fft_coefficient__attr_"imag"__coeff_7',
'BAND_ARR_8__fft_coefficient__attr_"imag"__coeff_8',
'BAND_ARR_8__fft_coefficient__attr_"imag"__coeff_10',
'BAND_ARR_8__fft_coefficient__attr_"imag"__coeff_11',
'BAND_ARR_8__fft_coefficient__attr_"imag"__coeff_12',
'BAND_ARR_8__fft_coefficient__attr_"imag"__coeff_14',
'BAND_ARR_8__fft_coefficient__attr_"imag"__coeff_19',
'BAND_ARR_8__fft_coefficient__attr_"imag"__coeff_20',
'BAND_ARR_8__fft_coefficient__attr_"imag"__coeff_23',
'BAND_ARR_8__fft_coefficient__attr_"imag"__coeff_25',
'BAND_ARR_8__fft_coefficient__attr_"imag"__coeff_26',
'BAND_ARR_8__fft_coefficient__attr_"imag"__coeff_27',
'BAND_ARR_8__fft_coefficient__attr_"imag"__coeff_28',
'BAND_ARR_8__fft_coefficient__attr_"imag"__coeff_31',
'BAND_ARR_8__fft_coefficient__attr_"imag"__coeff_32',
'BAND_ARR_8__fft_coefficient__attr_"imag"__coeff_37',
'BAND_ARR_8__fft_coefficient__attr_"abs"__coeff_0',
'BAND_ARR_8__fft_coefficient__attr_"abs"__coeff_1',
'BAND_ARR_8__fft_coefficient__attr_"abs"__coeff_2',
'BAND_ARR_8__fft_coefficient__attr_"abs"__coeff_3',
'BAND_ARR_8__fft_coefficient__attr_"abs"__coeff_4',
'BAND_ARR_8__fft_coefficient__attr_"abs"__coeff_5',
'BAND_ARR_8__fft_coefficient__attr_"abs"__coeff_6',
'BAND_ARR_8__fft_coefficient__attr_"abs"__coeff_10',
'BAND_ARR_8__fft_coefficient__attr_"abs"__coeff_13',
'BAND_ARR_8__fft_coefficient__attr_"abs"__coeff_14',
'BAND_ARR_8__fft_coefficient__attr_"abs"__coeff_15',
'BAND_ARR_8__fft_coefficient__attr_"abs"__coeff_19',
'BAND_ARR_8__fft_coefficient__attr_"abs"__coeff_21',
'BAND_ARR_8__fft_coefficient__attr_"abs"__coeff_22',
'BAND_ARR_8__fft_coefficient__attr_"abs"__coeff_23',
'BAND_ARR_8__fft_coefficient__attr_"abs"__coeff_26',
'BAND_ARR_8__fft_coefficient__attr_"abs"__coeff_28',
'BAND_ARR_8__fft_coefficient__attr_"abs"__coeff_29',
'BAND_ARR_8__fft_coefficient__attr_"abs"__coeff_30',
'BAND_ARR_8__fft_coefficient__attr_"abs"__coeff_37',
'BAND_ARR_8__fft_coefficient__attr_"abs"__coeff_83',
'BAND_ARR_8__fft_coefficient__attr_"abs"__coeff_94',
'BAND_ARR_8__fft_coefficient__attr_"abs"__coeff_98',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_1',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_2',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_3',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_4',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_6',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_7',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_8',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_10',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_11',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_14',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_15',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_16',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_17',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_19',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_21',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_22',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_23',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_27',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_29',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_30',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_31',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_32',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_34',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_35',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_36',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_37',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_38',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_39',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_40',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_41',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_42',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_43',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_44',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_46',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_47',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_48',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_49',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_50',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_52',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_53',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_54',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_55',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_56',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_57',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_58',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_62',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_64',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_65',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_66',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_67',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_69',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_70',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_71',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_72',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_74',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_75',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_78',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_79',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_80',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_81',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_83',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_84',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_86',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_87',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_88',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_89',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_90',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_92',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_93',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_94',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_95',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_96',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_97',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_98',
'BAND_ARR_8__range_count__max_1__min_-1',
'BAND_ARR_8__friedrich_coefficients__coeff_0__m_3__r_30',
'BAND_ARR_8__friedrich_coefficients__coeff_1__m_3__r_30',
'BAND_ARR_8__max_langevin_fixed_point__m_3__r_30',
'BAND_ARR_8__agg_linear_trend__attr_"rvalue"__chunk_len_5__f_agg_"mean"',
'BAND_ARR_8__agg_linear_trend__attr_"rvalue"__chunk_len_10__f_agg_"max"',
'BAND_ARR_8__agg_linear_trend__attr_"intercept"__chunk_len_5__f_agg_"max"',
'BAND_ARR_8__agg_linear_trend__attr_"intercept"__chunk_len_50__f_agg_"mean"',
'BAND_ARR_8__agg_linear_trend__attr_"slope"__chunk_len_10__f_agg_"max"',
'BAND_ARR_8__agg_linear_trend__attr_"slope"__chunk_len_50__f_agg_"min"',
'BAND_ARR_8__agg_linear_trend__attr_"stderr"__chunk_len_5__f_agg_"var"',
'BAND_ARR_8__agg_linear_trend__attr_"stderr"__chunk_len_10__f_agg_"min"',
'BAND_ARR_8__augmented_dickey_fuller__attr_"teststat"__autolag_"AIC"',
'BAND_ARR_8__energy_ratio_by_chunks__num_segments_10__segment_focus_1',
'BAND_ARR_8__energy_ratio_by_chunks__num_segments_10__segment_focus_5',
'BAND_ARR_8__ratio_beyond_r_sigma__r_1',
'VALUE'

]]


In [189]:
print(df_test_at_least_1.shape, df_validation_at_least_1.shape, df_train_at_least_1.shape  )

(22289, 800) (22537, 800) (69445, 800)


In [170]:
df_for_model_tab = pd.DataFrame(columns = ['validation metric', 'no selection', 'all methods', 'at least 3 methods', 'at least 2 methods', 'at least 1 methods'])
df_for_model_tab['validation metric'] = ('F1', 'Accuracy', 'Precision', 'Recall')
df_for_model_tab

validation metric no selection all methods at least 3 methods  \
0                F1          NaN         NaN                NaN   
1          Accuracy          NaN         NaN                NaN   
2         Precision          NaN         NaN                NaN   
3            Recall          NaN         NaN                NaN   

  at least 2 methods at least 1 methods  
0                NaN                NaN  
1                NaN                NaN  
2                NaN                NaN  
3                NaN                NaN

In [172]:
X_train = df_train.loc[:, df_train.columns != 'VALUE']
X_test = df_validation.loc[:, df_validation.columns != 'VALUE']
y_train = df_train['VALUE']
y_test = df_validation['VALUE']




In [174]:
def convert(data):
    number = preprocessing.LabelEncoder()
#     data['SESSION_INFO_ID'] = number.fit_transform(data.SESSION_INFO_ID)
    data['S_I_CREATED_AT'] = number.fit_transform(data.S_I_CREATED_AT)
    data['DATE'] = number.fit_transform(data.DATE)
    data['GW_MAC'] = number.fit_transform(data.GW_MAC)
    data['GW_NAME'] = number.fit_transform(data.GW_NAME)
    data['TOOL_MAC'] = number.fit_transform(data.TOOL_MAC)
    data['TOOL_NAME'] = number.fit_transform(data.TOOL_NAME)       
    return data

X_train=convert(X_train)
X_test=convert(X_test)


C:\Users\Arie\AppData\Local\Temp/ipykernel_6140/1665615973.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data['S_I_CREATED_AT'] = number.fit_transform(data.S_I_CREATED_AT)
C:\Users\Arie\AppData\Local\Temp/ipykernel_6140/1665615973.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data['DATE'] = number.fit_transform(data.DATE)
C:\Users\Arie\AppData\Local\Temp/ipykernel_6140/1665615973.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_

In [175]:
clf = RandomForestClassifier(max_depth=2, random_state=0)
clf.fit(X_train, y_train)
y_pred = clf.predict(X_test)


In [176]:
from sklearn import metrics


In [177]:
df_for_model_tab['no selection'] = (metrics.f1_score(y_test, y_pred), metrics.accuracy_score(y_test, y_pred), metrics.precision_score(y_test, y_pred),
                         metrics.recall_score(y_test, y_pred))
df_for_model_tab

validation metric  no selection all methods at least 3 methods  \
0                F1      0.840974         NaN                NaN   
1          Accuracy      0.885788         NaN                NaN   
2         Precision      0.988957         NaN                NaN   
3            Recall      0.731513         NaN                NaN   

  at least 2 methods at least 1 methods  
0                NaN                NaN  
1                NaN                NaN  
2                NaN                NaN  
3                NaN                NaN

In [190]:
X_train = df_train_at_least_2.loc[:, df_train_at_least_2.columns != 'VALUE']
X_test = df_validation_at_least_2.loc[:, df_validation_at_least_2.columns != 'VALUE']
y_train = df_train_at_least_2['VALUE']
y_test = df_validation_at_least_2['VALUE']





In [197]:
clf = RandomForestClassifier(max_depth=2, random_state=0)
clf.fit(X_train, y_train)
y_pred = clf.predict(X_test)


In [198]:
df_for_model_tab['at least 2 methods'] = (metrics.f1_score(y_test, y_pred), metrics.accuracy_score(y_test, y_pred), metrics.precision_score(y_test, y_pred),
                         metrics.recall_score(y_test, y_pred))
df_for_model_tab

validation metric  no selection all methods at least 3 methods  \
0                F1      0.840974         NaN                NaN   
1          Accuracy      0.885788         NaN                NaN   
2         Precision      0.988957         NaN                NaN   
3            Recall      0.731513         NaN                NaN   

   at least 2 methods at least 1 methods  
0            0.843902                NaN  
1            0.887607                NaN  
2            0.989022                NaN  
3            0.735920                NaN

In [199]:
X_train = df_train_at_least_3.loc[:, df_train_at_least_3.columns != 'VALUE']
X_test = df_validation_at_least_3.loc[:, df_validation_at_least_3.columns != 'VALUE']
y_train = df_train_at_least_3['VALUE']
y_test = df_validation_at_least_3['VALUE']




In [200]:
clf = RandomForestClassifier(max_depth=2, random_state=0)
clf.fit(X_train, y_train)
y_pred = clf.predict(X_test)


In [201]:
df_for_model_tab['at least 3 methods'] = (metrics.f1_score(y_test, y_pred), metrics.accuracy_score(y_test, y_pred), metrics.precision_score(y_test, y_pred),
                         metrics.recall_score(y_test, y_pred))
df_for_model_tab

validation metric  no selection all methods  at least 3 methods  \
0                F1      0.840974         NaN            0.845283   
1          Accuracy      0.885788         NaN            0.888361   
2         Precision      0.988957         NaN            0.987784   
3            Recall      0.731513         NaN            0.738715   

   at least 2 methods at least 1 methods  
0            0.843902                NaN  
1            0.887607                NaN  
2            0.989022                NaN  
3            0.735920                NaN

In [202]:
X_train = df_train_at_least_1.loc[:, df_train_at_least_1.columns != 'VALUE']
X_test = df_validation_at_least_1.loc[:, df_validation_at_least_1.columns != 'VALUE']
y_train = df_train_at_least_1['VALUE']
y_test = df_validation_at_least_1['VALUE']




In [203]:
clf = RandomForestClassifier(max_depth=2, random_state=0)
clf.fit(X_train, y_train)
y_pred = clf.predict(X_test)


In [204]:
df_for_model_tab['at least 1 methods'] = (metrics.f1_score(y_test, y_pred), metrics.accuracy_score(y_test, y_pred), metrics.precision_score(y_test, y_pred),
                         metrics.recall_score(y_test, y_pred))
df_for_model_tab

validation metric  no selection all methods  at least 3 methods  \
0                F1      0.840974         NaN            0.845283   
1          Accuracy      0.885788         NaN            0.888361   
2         Precision      0.988957         NaN            0.987784   
3            Recall      0.731513         NaN            0.738715   

   at least 2 methods  at least 1 methods  
0            0.843902            0.841514  
1            0.887607            0.886098  
2            0.989022            0.988684  
3            0.735920            0.732481

In [205]:
X_train = df_train_4.loc[:, df_train_4.columns != 'VALUE']
X_test = df_validation_4.loc[:, df_validation_4.columns != 'VALUE']
y_train = df_train_4['VALUE']
y_test = df_validation_4['VALUE']




In [206]:
clf = RandomForestClassifier(max_depth=2, random_state=0)
clf.fit(X_train, y_train)
y_pred = clf.predict(X_test)


In [207]:
df_for_model_tab['all methods'] = (metrics.f1_score(y_test, y_pred), metrics.accuracy_score(y_test, y_pred), metrics.precision_score(y_test, y_pred),
                         metrics.recall_score(y_test, y_pred))
df_for_model_tab

validation metric  no selection  all methods  at least 3 methods  \
0                F1      0.840974     0.853511            0.845283   
1          Accuracy      0.885788     0.892621            0.888361   
2         Precision      0.988957     0.976996            0.987784   
3            Recall      0.731513     0.757739            0.738715   

   at least 2 methods  at least 1 methods  
0            0.843902            0.841514  
1            0.887607            0.886098  
2            0.989022            0.988684  
3            0.735920            0.732481

We now have scores for all options! But I thought of adding another option.
  I learned that the "lasso" method is particularly effective for data sets that are characterized by close relationships between the variables. Our data is like this, so I decided to check what happens if
Selected only in the features selected by this method.

In [209]:
varSel_lasso = varSel[varSel['Lasso']==1]
varSel_lasso = varSel_lasso['Variable']
for var in varSel_lasso:
    {print ("'",var,"',")}

' INTERVAL_IN_FILE ',
' SN ',
' BAND_ARR_4 ',
' BAND_ARR_5 ',
' BAND_ARR_6 ',
' BAND_ARR_7 ',
' BAND_ARR_8 ',
' BAND_ARR_9 ',
' BAND_ARR_10 ',
' BAND_ARR_13 ',
' BIT_FLAG ',
' MAX_VALUE ',
' NTC ',
' FIRST_PACKET_TS ',
' NTC__cwt_coefficients__coeff_2__w_2__widths_(2, 5, 10, 20) ',
' NTC__cwt_coefficients__coeff_7__w_10__widths_(2, 5, 10, 20) ',
' NTC__cwt_coefficients__coeff_8__w_10__widths_(2, 5, 10, 20) ',
' NTC__cwt_coefficients__coeff_9__w_10__widths_(2, 5, 10, 20) ',
' NTC__cwt_coefficients__coeff_11__w_20__widths_(2, 5, 10, 20) ',
' NTC__cwt_coefficients__coeff_12__w_20__widths_(2, 5, 10, 20) ',
' NTC__cwt_coefficients__coeff_13__w_20__widths_(2, 5, 10, 20) ',
' NTC__ar_coefficient__coeff_0__k_10 ',
' NTC__fft_coefficient__attr_"real"__coeff_1 ',
' NTC__fft_coefficient__attr_"real"__coeff_4 ',
' NTC__fft_coefficient__attr_"real"__coeff_52 ',
' NTC__fft_coefficient__attr_"real"__coeff_70 ',
' NTC__fft_coefficient__attr_"real"__coeff_90 ',
' NTC__fft_coefficient__attr_"imag"__coef

In [211]:
df_test_lasso = df_test[['INTERVAL_IN_FILE',
'SN',
'BAND_ARR_4',
'BAND_ARR_5',
'BAND_ARR_6',
'BAND_ARR_7',
'BAND_ARR_8',
'BAND_ARR_9',
'BAND_ARR_10',
'BAND_ARR_13',
'BIT_FLAG',
'MAX_VALUE',
'NTC',
'FIRST_PACKET_TS',
'NTC__cwt_coefficients__coeff_2__w_2__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_7__w_10__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_8__w_10__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_9__w_10__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_11__w_20__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_12__w_20__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_13__w_20__widths_(2, 5, 10, 20)',
'NTC__ar_coefficient__coeff_0__k_10',
'NTC__fft_coefficient__attr_"real"__coeff_1',
'NTC__fft_coefficient__attr_"real"__coeff_4',
'NTC__fft_coefficient__attr_"real"__coeff_52',
'NTC__fft_coefficient__attr_"real"__coeff_70',
'NTC__fft_coefficient__attr_"real"__coeff_90',
'NTC__fft_coefficient__attr_"imag"__coeff_1',
'NTC__fft_coefficient__attr_"imag"__coeff_26',
'NTC__fft_coefficient__attr_"imag"__coeff_27',
'NTC__fft_coefficient__attr_"imag"__coeff_28',
'NTC__fft_coefficient__attr_"imag"__coeff_51',
'NTC__fft_coefficient__attr_"imag"__coeff_53',
'NTC__fft_coefficient__attr_"imag"__coeff_54',
'NTC__fft_coefficient__attr_"imag"__coeff_59',
'NTC__fft_coefficient__attr_"imag"__coeff_61',
'NTC__fft_coefficient__attr_"imag"__coeff_63',
'NTC__fft_coefficient__attr_"imag"__coeff_93',
'NTC__fft_coefficient__attr_"angle"__coeff_9',
'NTC__fft_coefficient__attr_"angle"__coeff_10',
'NTC__fft_coefficient__attr_"angle"__coeff_45',
'NTC__fft_coefficient__attr_"angle"__coeff_46',
'NTC__fft_coefficient__attr_"angle"__coeff_58',
'NTC__fft_coefficient__attr_"angle"__coeff_59',
'NTC__fft_coefficient__attr_"angle"__coeff_69',
'NTC__fft_coefficient__attr_"angle"__coeff_77',
'NTC__fft_coefficient__attr_"angle"__coeff_84',
'NTC__fft_coefficient__attr_"angle"__coeff_86',
'NTC__fft_coefficient__attr_"angle"__coeff_89',
'NTC__fft_coefficient__attr_"angle"__coeff_90',
'NTC__fft_coefficient__attr_"angle"__coeff_95',
'NTC__max_langevin_fixed_point__m_3__r_30',
'BAND_ARR_2__sum_values',
'BAND_ARR_2__count_below_mean',
'BAND_ARR_2__spkt_welch_density__coeff_2',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_0',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_2',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_3',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_1',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_2',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_3',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_5',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_1',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_2',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_2',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_4',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_9',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_23',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_28',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_40',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_44',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_47',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_51',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_64',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_65',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_66',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_69',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_70',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_75',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_81',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_89',
'BAND_ARR_2__range_count__max_1__min_-1',
'BAND_ARR_8__sum_values',
'BAND_ARR_8__longest_strike_below_mean',
'BAND_ARR_8__count_above_mean',
'BAND_ARR_8__count_below_mean',
'BAND_ARR_8__c3__lag_1',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_3',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_4',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_2',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_7',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_14',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_15',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_38',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_58',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_62',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_64',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_65',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_69',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_72',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_78',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_89',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_96',
'BAND_ARR_8__max_langevin_fixed_point__m_3__r_30',
'VALUE'
]]


In [212]:
df_validation_lasso = df_validation[['INTERVAL_IN_FILE',
'SN',
'BAND_ARR_4',
'BAND_ARR_5',
'BAND_ARR_6',
'BAND_ARR_7',
'BAND_ARR_8',
'BAND_ARR_9',
'BAND_ARR_10',
'BAND_ARR_13',
'BIT_FLAG',
'MAX_VALUE',
'NTC',
'FIRST_PACKET_TS',
'NTC__cwt_coefficients__coeff_2__w_2__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_7__w_10__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_8__w_10__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_9__w_10__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_11__w_20__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_12__w_20__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_13__w_20__widths_(2, 5, 10, 20)',
'NTC__ar_coefficient__coeff_0__k_10',
'NTC__fft_coefficient__attr_"real"__coeff_1',
'NTC__fft_coefficient__attr_"real"__coeff_4',
'NTC__fft_coefficient__attr_"real"__coeff_52',
'NTC__fft_coefficient__attr_"real"__coeff_70',
'NTC__fft_coefficient__attr_"real"__coeff_90',
'NTC__fft_coefficient__attr_"imag"__coeff_1',
'NTC__fft_coefficient__attr_"imag"__coeff_26',
'NTC__fft_coefficient__attr_"imag"__coeff_27',
'NTC__fft_coefficient__attr_"imag"__coeff_28',
'NTC__fft_coefficient__attr_"imag"__coeff_51',
'NTC__fft_coefficient__attr_"imag"__coeff_53',
'NTC__fft_coefficient__attr_"imag"__coeff_54',
'NTC__fft_coefficient__attr_"imag"__coeff_59',
'NTC__fft_coefficient__attr_"imag"__coeff_61',
'NTC__fft_coefficient__attr_"imag"__coeff_63',
'NTC__fft_coefficient__attr_"imag"__coeff_93',
'NTC__fft_coefficient__attr_"angle"__coeff_9',
'NTC__fft_coefficient__attr_"angle"__coeff_10',
'NTC__fft_coefficient__attr_"angle"__coeff_45',
'NTC__fft_coefficient__attr_"angle"__coeff_46',
'NTC__fft_coefficient__attr_"angle"__coeff_58',
'NTC__fft_coefficient__attr_"angle"__coeff_59',
'NTC__fft_coefficient__attr_"angle"__coeff_69',
'NTC__fft_coefficient__attr_"angle"__coeff_77',
'NTC__fft_coefficient__attr_"angle"__coeff_84',
'NTC__fft_coefficient__attr_"angle"__coeff_86',
'NTC__fft_coefficient__attr_"angle"__coeff_89',
'NTC__fft_coefficient__attr_"angle"__coeff_90',
'NTC__fft_coefficient__attr_"angle"__coeff_95',
'NTC__max_langevin_fixed_point__m_3__r_30',
'BAND_ARR_2__sum_values',
'BAND_ARR_2__count_below_mean',
'BAND_ARR_2__spkt_welch_density__coeff_2',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_0',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_2',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_3',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_1',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_2',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_3',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_5',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_1',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_2',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_2',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_4',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_9',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_23',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_28',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_40',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_44',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_47',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_51',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_64',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_65',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_66',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_69',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_70',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_75',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_81',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_89',
'BAND_ARR_2__range_count__max_1__min_-1',
'BAND_ARR_8__sum_values',
'BAND_ARR_8__longest_strike_below_mean',
'BAND_ARR_8__count_above_mean',
'BAND_ARR_8__count_below_mean',
'BAND_ARR_8__c3__lag_1',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_3',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_4',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_2',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_7',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_14',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_15',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_38',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_58',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_62',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_64',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_65',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_69',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_72',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_78',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_89',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_96',
'BAND_ARR_8__max_langevin_fixed_point__m_3__r_30',
'VALUE'
]]


In [213]:
df_train_lasso = df_train[['INTERVAL_IN_FILE',
'SN',
'BAND_ARR_4',
'BAND_ARR_5',
'BAND_ARR_6',
'BAND_ARR_7',
'BAND_ARR_8',
'BAND_ARR_9',
'BAND_ARR_10',
'BAND_ARR_13',
'BIT_FLAG',
'MAX_VALUE',
'NTC',
'FIRST_PACKET_TS',
'NTC__cwt_coefficients__coeff_2__w_2__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_7__w_10__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_8__w_10__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_9__w_10__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_11__w_20__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_12__w_20__widths_(2, 5, 10, 20)',
'NTC__cwt_coefficients__coeff_13__w_20__widths_(2, 5, 10, 20)',
'NTC__ar_coefficient__coeff_0__k_10',
'NTC__fft_coefficient__attr_"real"__coeff_1',
'NTC__fft_coefficient__attr_"real"__coeff_4',
'NTC__fft_coefficient__attr_"real"__coeff_52',
'NTC__fft_coefficient__attr_"real"__coeff_70',
'NTC__fft_coefficient__attr_"real"__coeff_90',
'NTC__fft_coefficient__attr_"imag"__coeff_1',
'NTC__fft_coefficient__attr_"imag"__coeff_26',
'NTC__fft_coefficient__attr_"imag"__coeff_27',
'NTC__fft_coefficient__attr_"imag"__coeff_28',
'NTC__fft_coefficient__attr_"imag"__coeff_51',
'NTC__fft_coefficient__attr_"imag"__coeff_53',
'NTC__fft_coefficient__attr_"imag"__coeff_54',
'NTC__fft_coefficient__attr_"imag"__coeff_59',
'NTC__fft_coefficient__attr_"imag"__coeff_61',
'NTC__fft_coefficient__attr_"imag"__coeff_63',
'NTC__fft_coefficient__attr_"imag"__coeff_93',
'NTC__fft_coefficient__attr_"angle"__coeff_9',
'NTC__fft_coefficient__attr_"angle"__coeff_10',
'NTC__fft_coefficient__attr_"angle"__coeff_45',
'NTC__fft_coefficient__attr_"angle"__coeff_46',
'NTC__fft_coefficient__attr_"angle"__coeff_58',
'NTC__fft_coefficient__attr_"angle"__coeff_59',
'NTC__fft_coefficient__attr_"angle"__coeff_69',
'NTC__fft_coefficient__attr_"angle"__coeff_77',
'NTC__fft_coefficient__attr_"angle"__coeff_84',
'NTC__fft_coefficient__attr_"angle"__coeff_86',
'NTC__fft_coefficient__attr_"angle"__coeff_89',
'NTC__fft_coefficient__attr_"angle"__coeff_90',
'NTC__fft_coefficient__attr_"angle"__coeff_95',
'NTC__max_langevin_fixed_point__m_3__r_30',
'BAND_ARR_2__sum_values',
'BAND_ARR_2__count_below_mean',
'BAND_ARR_2__spkt_welch_density__coeff_2',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_0',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_2',
'BAND_ARR_2__fft_coefficient__attr_"real"__coeff_3',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_1',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_2',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_3',
'BAND_ARR_2__fft_coefficient__attr_"imag"__coeff_5',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_1',
'BAND_ARR_2__fft_coefficient__attr_"abs"__coeff_2',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_2',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_4',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_9',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_23',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_28',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_40',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_44',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_47',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_51',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_64',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_65',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_66',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_69',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_70',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_75',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_81',
'BAND_ARR_2__fft_coefficient__attr_"angle"__coeff_89',
'BAND_ARR_2__range_count__max_1__min_-1',
'BAND_ARR_8__sum_values',
'BAND_ARR_8__longest_strike_below_mean',
'BAND_ARR_8__count_above_mean',
'BAND_ARR_8__count_below_mean',
'BAND_ARR_8__c3__lag_1',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_3',
'BAND_ARR_8__fft_coefficient__attr_"real"__coeff_4',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_2',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_7',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_14',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_15',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_38',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_58',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_62',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_64',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_65',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_69',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_72',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_78',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_89',
'BAND_ARR_8__fft_coefficient__attr_"angle"__coeff_96',
'BAND_ARR_8__max_langevin_fixed_point__m_3__r_30',
'VALUE'
]]


In [214]:
print (df_train_lasso.shape, df_test_lasso.shape, df_validation_lasso.shape)

(69445, 105) (22289, 105) (22537, 105)


In [215]:
X_train = df_train_lasso.loc[:, df_train_lasso.columns != 'VALUE']
X_test = df_validation_lasso.loc[:, df_validation_lasso.columns != 'VALUE']
y_train = df_train_lasso['VALUE']
y_test = df_validation_lasso['VALUE']




In [216]:
clf = RandomForestClassifier(max_depth=2, random_state=0)
clf.fit(X_train, y_train)
y_pred = clf.predict(X_test)


In [217]:
df_for_model_tab['lasso method'] = (metrics.f1_score(y_test, y_pred), metrics.accuracy_score(y_test, y_pred), metrics.precision_score(y_test, y_pred),
                         metrics.recall_score(y_test, y_pred))
df_for_model_tab

validation metric  no selection  all methods  at least 3 methods  \
0                F1      0.840974     0.853511            0.845283   
1          Accuracy      0.885788     0.892621            0.888361   
2         Precision      0.988957     0.976996            0.987784   
3            Recall      0.731513     0.757739            0.738715   

   at least 2 methods  at least 1 methods  lasso method  
0            0.843902            0.841514      0.832071  
1            0.887607            0.886098      0.880020  
2            0.989022            0.988684      0.985437  
3            0.735920            0.732481      0.720013

Well, by the way, the deeper the selection, the better the results, but by a small margin. I thought of adding the amount of features to the comparison table, so that the connection between the amount of features and the results is noticeable, and this will make the decision more convenient.

In [226]:
feature_num_row = {'validation metric':'Number of features', 'no selection':'2367', 'all methods':'12', 'at least 3 methods':'25',
                  'at least 2 methods': '127', 'at least 1 methods': '800', 'lasso method': '105' }
df_for_model_tab = df_for_model_tab.append(feature_num_row, ignore_index=True)
df_for_model_tab

validation metric no selection all methods at least 3 methods  \
0                  F1     0.840974    0.853511           0.845283   
1            Accuracy     0.885788    0.892621           0.888361   
2           Precision     0.988957    0.976996           0.987784   
3              Recall     0.731513    0.757739           0.738715   
4  Number of features         2367          12                 25   

  at least 2 methods at least 1 methods lasso method  
0           0.843902           0.841514     0.832071  
1           0.887607           0.886098      0.88002  
2           0.989022           0.988684     0.985437  
3            0.73592           0.732481     0.720013  
4                127                800          105

In [228]:
df_for_model_tab = df_for_model_tab.reindex([4,0,1,2,3])


df_for_model_tab

validation metric no selection all methods at least 3 methods  \
4  Number of features         2367          12                 25   
0                  F1     0.840974    0.853511           0.845283   
1            Accuracy     0.885788    0.892621           0.888361   
2           Precision     0.988957    0.976996           0.987784   
3              Recall     0.731513    0.757739           0.738715   

  at least 2 methods at least 1 methods lasso method  
4                127                800          105  
0           0.843902           0.841514     0.832071  
1           0.887607           0.886098      0.88002  
2           0.989022           0.988684     0.985437  
3            0.73592           0.732481     0.720013

Now things are indeed noticeable. The trend is clear: more selection leads to improved results. On the other hand - the differences in the trend are very small.
At this point what I thought was better to actually opt for data with slightly less good results, and with more features. This is with the thought that the more features there are, the more stable the model is likely to be, will be able to maintain good results in changing situations, the less inclined to
over fitting.

I presented this thought along with the table to my facilitator. What he asked for was indeed to test stability, based on a criterion that is important to the customer: the success of the model with minimal dependence on the question of on which session info id the prediction was made.

In the following cells I created the method to test this, first on the last prediction that was stored in the system - the prediction based on the lasso method.
I created a table that compares the prediction with the true value, where a prediction error gets a point and success gets 0 points.

Then for each session info id I created an average of the scores, i.e. - probability of error. Then I compared the probability of error to the general probability of error in the whole prediction. From here I created 2 metrics (2 more were added later):
1. The average difference for each session between its probability of error and the general explanation of error
2. The maximum gap for each session

In [300]:



prediction_row_check = pd.DataFrame(columns = ['y pred', 'y'])
prediction_row_check['y']=y_test
prediction_row_check['y pred']=y_pred
prediction_row_check = prediction_row_check.reset_index()
prediction_row_check['is prediction wrong'] = (prediction_row_check['y pred'] - prediction_row_check['y'])**2
prediction_row_check

SESSION_INFO_ID  y pred  y  is prediction wrong
0      01f1616f1d05450188aab06aec94e657       0  0                    0
1      01f1616f1d05450188aab06aec94e657       0  0                    0
2      01f1616f1d05450188aab06aec94e657       0  0                    0
3      01f1616f1d05450188aab06aec94e657       0  0                    0
4      01f1616f1d05450188aab06aec94e657       0  0                    0
5      01f1616f1d05450188aab06aec94e657       1  0                    1
6      01f1616f1d05450188aab06aec94e657       1  0                    1
7      01f1616f1d05450188aab06aec94e657       0  0                    0
8      01f1616f1d05450188aab06aec94e657       1  1                    0
9      01f1616f1d05450188aab06aec94e657       1  1                    0
10     01f1616f1d05450188aab06aec94e657       1  1                    0
11     01f1616f1d05450188aab06aec94e657       1  1                    0
12     01f1616f1d05450188aab06aec94e657       1  1                    0
13     01f1616f1d05450188aab06aec94e657       1  1                    0
14     01f1616f1d05450188aab06aec94e657       1  1                    0
15     01f1616f1d05450188aab06aec94e657       1  1                    0
16     01f1616f1d05450188aab06aec94e657       1  1                    0
17     01f1616f1d05450188aab06aec94e657       1  1                    0
18     01f1616f1d05450188aab06aec94e657       1  1                    0
19     01f1616f1d05450188aab06aec94e657       1  1                    0
20     01f1616f1d05450188aab06aec94e657       1  1                    0
21     01f1616f1d05450188aab06aec94e657       1  1                    0
22     01f1616f1d05450188aab06aec94e657       1  1                    0
23     01f1616f1d05450188aab06aec94e657       1  1                    0
24     01f1616f1d05450188aab06aec94e657       1  1                    0
25     01f1616f1d05450188aab06aec94e657       0  0                    0
26     01f1616f1d05450188aab06aec94e657       0  0                    0
27     01f1616f1d05450188aab06aec94e657       1  1                    0
28     01f1616f1d05450188aab06aec94e657       1  1                    0
29     01f1616f1d05450188aab06aec94e657       1  1                    0
30     01f1616f1d05450188aab06aec94e657       1  1                    0
31     01f1616f1d05450188aab06aec94e657       1  1                    0
32     01f1616f1d05450188aab06aec94e657       1  1                    0
33     01f1616f1d05450188aab06aec94e657       1  1                    0
34     01f1616f1d05450188aab06aec94e657       1  1                    0
35     01f1616f1d05450188aab06aec94e657       1  1                    0
36     01f1616f1d05450188aab06aec94e657       1  1                    0
37     01f1616f1d05450188aab06aec94e657       1  1                    0
38     01f1616f1d05450188aab06aec94e657       1  1                    0
39     01f1616f1d05450188aab06aec94e657       1  1                    0
40     01f1616f1d05450188aab06aec94e657       0  0                    0
41     01f1616f1d05450188aab06aec94e657       0  0                    0
42     01f1616f1d05450188aab06aec94e657       0  0                    0
43     01f1616f1d05450188aab06aec94e657       0  0                    0
44     01f1616f1d05450188aab06aec94e657       0  0                    0
45     01f1616f1d05450188aab06aec94e657       0  0                    0
46     01f1616f1d05450188aab06aec94e657       0  0                    0
47     01f1616f1d05450188aab06aec94e657       0  0                    0
48     01f1616f1d05450188aab06aec94e657       1  1                    0
49     01f1616f1d05450188aab06aec94e657       1  1                    0
50     01f1616f1d05450188aab06aec94e657       1  1                    0
51     01f1616f1d05450188aab06aec94e657       1  1                    0
52     01f1616f1d05450188aab06aec94e657       1  1                    0
53     01f1616f1d05450188aab06aec94e657       1  1                    0
54     01f1616f1d05450188aab06aec94e657       1  1              

In [308]:
prediction_session_check=pd.DataFrame(prediction_row_check.groupby('SESSION_INFO_ID')['is prediction wrong'].mean())
prediction_session_check = prediction_session_check.reset_index()
prediction_session_check

SESSION_INFO_ID  is prediction wrong
0   01f1616f1d05450188aab06aec94e657             0.002477
1   0d62401243a147b6942f38ec0a103e73             0.000000
2   0f3ecc21cca044f889e17541eff51a88             0.002327
3   1202068c82a8469d8765040d58b8df57             0.004211
4   121a0a371aa24781868792af2e030e5f             0.000000
5   13ff1cd6be5a4af0b4dd2f5fa24cff6b             0.000000
6   1509358e6dda4f7ebaa35521b6811beb             0.018634
7   15969800ce3140169107aa2fc58cd8fd             0.000000
8   1ee54a59431c4025bc181b0d88a628da             0.010395
9   27f7055be4a74e68968df48a6bc6abbe             0.000000
10  2a1a43ad7a30460dbc8fea4f5fc07ade             0.004211
11  37ce4ebe8de74850bf795484b146faf3             0.000000
12  45dfe3e2dced4c46b6fab6cc74c2ad57             0.000000
13  477a067121dc4a3db0a7f86b87279aa9             0.000000
14  50057e85e6bd48d98cc2b07fa10c5886             0.783719
15  5c0decab30c540d290f3db54b61e62bc             0.275362
16  6418a96dd176490fbd4df5623c1a2ee3             0.000000
17  6933e306784d4bfa809307744e12c82a             0.008475
18  6b534e5354394a7281d592e724a279a0             0.000000
19  70d728fb861e45f8954bbb5ec5a47dcb             0.000000
20  720c89d8ab7d4f99870b57cde11e6812             0.023041
21  7c7b5ca9eef84b45b30914d568860775             0.014583
22  808fc1e8d91f4503a454b04c4715b47c             0.012448
23  8cc080131be146deb2b5fa3e85da6563             0.255814
24  9170712a51e944dcb877b3c425791e17             0.010571
25  98285ddc802648e6b86e5cdf7aa3c41a             0.000000
26  99d11e15c4d440deb0183195faeea1a2             0.000000
27  9afb7961cfb2406d90ee5a162350e86b             0.000000
28  a1a916f55354450899185d74a25c872c             0.012448
29  afc8da1dbc3e4d7087e82ccc2d9a2ccd             0.000000
30  b0604e64e447484d8cc0f706ea2ec33a             0.000000
31  b61fd222b7ff4581b962b9c82aa187ee             0.000000
32  b660d177d6a84d2dba1e23b92301279c             0.006316
33  c45c3bcd5e8542c48f9ec4c4fee3c074             0.010460
34  c95d52c117dc4007834271189dc835b3             0.356077
35  cc5c8bcfb8c348a18c34523bc8705645             0.000000
36  cd6cd64e20544dccaf20cca2d80ec6c6             0.364896
37  ce20e41a51dd4cc6b4fc0e035ec5079d             0.004237
38  ce9b7631df5846eeb7dbc1bc3271dc6a             0.002101
39  cedbdd9d9e24409c9704a11ca0470a74             0.008439
40  d505825721104ed7a624d2d20aaa40df             0.010549
41  d8c549b1b5d5454d9ed299a7b7ff87f8             0.000000
42  e3130d395ebd4409802874d380015f60             0.000000
43  e56da7e42a72495188df72d7ce34c19c             0.000000
44  e7cd598fde834ce7b73a146598b6f768             0.000000
45  e9acd14a218c4fa4b8a07345022a3f17             0.103356
46  ecb61756dbd14a7cb678d79c0c691c10             0.008403
47  ee3761b64bfc4d6e8486404fadbecfc1             0.009416
48  f7215673af734314a9e5798074c2a8c2             0.004458
49  f7b54a99049a4169aa3da093254ecb76             0.000000
50  f96905f611dc42338449fa984a6755f6             0.003375
51  faf5fbaf0e0a49fc96fa5ed1cd7b8ce2             0.003293
52  fba643b92532440ea9776c33c35b6ace             0.014583

In [309]:
prediction_session_check['abs difference from average'] = abs(prediction_session_check['is prediction wrong']-statistics.mean(prediction_row_check['is prediction wrong']))
prediction_session_check

SESSION_INFO_ID  is prediction wrong  \
0   01f1616f1d05450188aab06aec94e657             0.002477   
1   0d62401243a147b6942f38ec0a103e73             0.000000   
2   0f3ecc21cca044f889e17541eff51a88             0.002327   
3   1202068c82a8469d8765040d58b8df57             0.004211   
4   121a0a371aa24781868792af2e030e5f             0.000000   
5   13ff1cd6be5a4af0b4dd2f5fa24cff6b             0.000000   
6   1509358e6dda4f7ebaa35521b6811beb             0.018634   
7   15969800ce3140169107aa2fc58cd8fd             0.000000   
8   1ee54a59431c4025bc181b0d88a628da             0.010395   
9   27f7055be4a74e68968df48a6bc6abbe             0.000000   
10  2a1a43ad7a30460dbc8fea4f5fc07ade             0.004211   
11  37ce4ebe8de74850bf795484b146faf3             0.000000   
12  45dfe3e2dced4c46b6fab6cc74c2ad57             0.000000   
13  477a067121dc4a3db0a7f86b87279aa9             0.000000   
14  50057e85e6bd48d98cc2b07fa10c5886             0.783719   
15  5c0decab30c540d290f3db54b61e62bc             0.275362   
16  6418a96dd176490fbd4df5623c1a2ee3             0.000000   
17  6933e306784d4bfa809307744e12c82a             0.008475   
18  6b534e5354394a7281d592e724a279a0             0.000000   
19  70d728fb861e45f8954bbb5ec5a47dcb             0.000000   
20  720c89d8ab7d4f99870b57cde11e6812             0.023041   
21  7c7b5ca9eef84b45b30914d568860775             0.014583   
22  808fc1e8d91f4503a454b04c4715b47c             0.012448   
23  8cc080131be146deb2b5fa3e85da6563             0.255814   
24  9170712a51e944dcb877b3c425791e17             0.010571   
25  98285ddc802648e6b86e5cdf7aa3c41a             0.000000   
26  99d11e15c4d440deb0183195faeea1a2             0.000000   
27  9afb7961cfb2406d90ee5a162350e86b             0.000000   
28  a1a916f55354450899185d74a25c872c             0.012448   
29  afc8da1dbc3e4d7087e82ccc2d9a2ccd             0.000000   
30  b0604e64e447484d8cc0f706ea2ec33a             0.000000   
31  b61fd222b7ff4581b962b9c82aa187ee             0.000000   
32  b660d177d6a84d2dba1e23b92301279c             0.006316   
33  c45c3bcd5e8542c48f9ec4c4fee3c074             0.010460   
34  c95d52c117dc4007834271189dc835b3             0.356077   
35  cc5c8bcfb8c348a18c34523bc8705645             0.000000   
36  cd6cd64e20544dccaf20cca2d80ec6c6             0.364896   
37  ce20e41a51dd4cc6b4fc0e035ec5079d             0.004237   
38  ce9b7631df5846eeb7dbc1bc3271dc6a             0.002101   
39  cedbdd9d9e24409c9704a11ca0470a74             0.008439   
40  d505825721104ed7a624d2d20aaa40df             0.010549   
41  d8c549b1b5d5454d9ed299a7b7ff87f8             0.000000   
42  e3130d395ebd4409802874d380015f60             0.000000   
43  e56da7e42a72495188df72d7ce34c19c             0.000000   
44  e7cd598fde834ce7b73a146598b6f768             0.000000   
45  e9acd14a218c4fa4b8a07345022a3f17             0.103356   
46  ecb61756dbd14a7cb678d79c0c691c10             0.008403   
47  ee3761b64bfc4d6e8486404fadbecfc1             0.009416   
48  f7215673af734314a9e5798074c2a8c2             0.004458   
49  f7b54a99049a4169aa3da093254ecb76             0.000000   
50  f96905f611dc42338449fa984a6755f6             0.003375   
51  faf5fbaf0e0a49fc96fa5ed1cd7b8ce2             0.003293   
52  fba643b92532440ea9776c33c35b6ace             0.014583   

    abs difference from average  
0                      0.117503  
1                      0.119980  
2                      0.117654  
3                      0.115770  
4                      0.119980  
5                      0.119980  
6                      0.101347  
7                      0.119980  
8                      0.109585  
9                      0.119980  
10                     0.115770  
11                     0.119980  
12                     0.119980  
13                     0.119980  
14                     0.663738  
15                     0.155382  
16                     0.119980  
17                     0.111506  
18                     0.119980  
19                     0.119980  
20          

In [311]:
prediction_session_check['abs difference from average'].mean()


0.12985325589088242

In [352]:
df_for_model_tab2 = pd.DataFrame(columns = ['validation metric', 'no selection', 'all methods', 'at least 3 methods', 'at least 2 methods', 'at least 1 methods', 'lasso method'])
df_for_model_tab2['validation metric'] = ('per session max difference from average', 'per session average difference from average')
df_for_model_tab2

validation metric no selection all methods  \
0      per session max difference from average          NaN         NaN   
1  per session average difference from average          NaN         NaN   

  at least 3 methods at least 2 methods at least 1 methods lasso method  
0                NaN                NaN                NaN          NaN  
1                NaN                NaN                NaN          NaN

In [353]:
df_for_model_tab2['lasso method'] = prediction_session_check['abs difference from average'].max(), prediction_session_check['abs difference from average'].mean()
df_for_model_tab2


validation metric no selection all methods  \
0      per session max difference from average          NaN         NaN   
1  per session average difference from average          NaN         NaN   

  at least 3 methods at least 2 methods at least 1 methods  lasso method  
0                NaN                NaN                NaN      0.663738  
1                NaN                NaN                NaN      0.129853

I created a comparison table for the two new metrics and entered the results for the LASO-based data set in it.
The next step is to repeat the same process with the other data sets. This time, after understanding my own method, I created a function that would shorten the move.

In [354]:
def error_per_session(train_data, test_data, data_set_name_in_tab):
    
    X_train = train_data.loc[:, train_data.columns != 'VALUE']
    X_test = test_data.loc[:, test_data.columns != 'VALUE']
    y_train = train_data['VALUE']
    y_test = test_data['VALUE']

    
    clf = RandomForestClassifier(max_depth=2, random_state=0)
    clf.fit(X_train, y_train)
    y_pred = clf.predict(X_test)
    
    prediction_row_check = pd.DataFrame(columns = ['y pred', 'y'])
    prediction_row_check['y']=y_test
    prediction_row_check['y pred']=y_pred
    prediction_row_check = prediction_row_check.reset_index()
    prediction_row_check['is prediction wrong'] = (prediction_row_check['y pred'] - prediction_row_check['y'])**2
    
    prediction_session_check=pd.DataFrame(prediction_row_check.groupby('SESSION_INFO_ID')['is prediction wrong'].mean())
    prediction_session_check = prediction_session_check.reset_index()
    
    prediction_session_check['abs difference from average'] = abs(prediction_session_check['is prediction wrong']-statistics.mean(prediction_row_check['is prediction wrong']))
    
    df_for_model_tab2[data_set_name_in_tab] = prediction_session_check['abs difference from average'].max(), prediction_session_check['abs difference from average'].mean()


In [355]:
error_per_session(df_train_at_least_2, df_validation_at_least_2, 'at least 2 methods' )

In [356]:
df_for_model_tab2

validation metric no selection all methods  \
0      per session max difference from average          NaN         NaN   
1  per session average difference from average          NaN         NaN   

  at least 3 methods  at least 2 methods at least 1 methods  lasso method  
0                NaN            0.666990                NaN      0.663738  
1                NaN            0.120373                NaN      0.129853

In [357]:
error_per_session(df_train_4, df_validation_4, 'all methods' )
df_for_model_tab2

validation metric no selection  all methods  \
0      per session max difference from average          NaN     0.641176   
1  per session average difference from average          NaN     0.110062   

  at least 3 methods  at least 2 methods at least 1 methods  lasso method  
0                NaN            0.666990                NaN      0.663738  
1                NaN            0.120373                NaN      0.129853

In [358]:
error_per_session(df_train_at_least_3, df_validation_at_least_3, 'at least 3 methods' )
df_for_model_tab2

validation metric no selection  all methods  \
0      per session max difference from average          NaN     0.641176   
1  per session average difference from average          NaN     0.110062   

   at least 3 methods  at least 2 methods at least 1 methods  lasso method  
0            0.659556            0.666990                NaN      0.663738  
1            0.119590            0.120373                NaN      0.129853

In [359]:
error_per_session(df_train_at_least_1, df_validation_at_least_1, 'at least 1 methods' )
df_for_model_tab2

validation metric no selection  all methods  \
0      per session max difference from average          NaN     0.641176   
1  per session average difference from average          NaN     0.110062   

   at least 3 methods  at least 2 methods  at least 1 methods  lasso method  
0            0.659556            0.666990            0.665482      0.663738  
1            0.119590            0.120373            0.120902      0.129853

In [360]:
error_per_session(df_train, df_validation, 'no selection')
df_for_model_tab2

MemoryError: 

In [363]:
df_selection = [df_for_model_tab, df_for_model_tab2]
df_selection = pd.concat(df_selection)
df_selection

validation metric no selection all methods  \
4                           Number of features         2367          12   
0                                           F1     0.840974    0.853511   
1                                     Accuracy     0.885788    0.892621   
2                                    Precision     0.988957    0.976996   
3                                       Recall     0.731513    0.757739   
0      per session max difference from average          NaN    0.641176   
1  per session average difference from average          NaN    0.110062   

  at least 3 methods at least 2 methods at least 1 methods lasso method  
4                 25                127                800          105  
0           0.845283           0.843902           0.841514     0.832071  
1           0.888361           0.887607           0.886098      0.88002  
2           0.987784           0.989022           0.988684     0.985437  
3           0.738715            0.73592           0.732481     0.720013  
0           0.659556            0.66699           0.665482     0.663738  
1            0.11959           0.120373           0.120902     0.129853

For the dataset with the 2367 variables a memory error has been created, but there seems to be no point in trying to resolve it because the trend is clear. The stable models in our case are according to the same rule of thumb of the models with the best results: the more filtering for features, the better the results.
     Therefore, I decided to move on to the latest notebook, which will deal with the selection of the model, with the selected dataset, which has only 12 features, the dataset in which the features were selected by all 4 methods of
     The feature selection.